This Google Colloboratory Link contains all the code for the DEA Models to be used in the analysis FOR STRIKERS

The Excel file to be used for strikers is:

DEA MODEL 1: /content/DEA Model 1_Strikers.csv 

DEA MODEL 2: /content/Strikers DEA Model 2 and 3.csv

#**DEA Model 1** 

Performance Efficiency

4 Technical Areas:


*   Goal Scoring
*   Creativity
*   Dribbling and Ball Carrying
*   Defending












In [ ]:
!pip install pulp #Loading the required libraries
import pulp
!apt-get install -y -qq glpk-utils

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


# **Strikers**

**1) Goal Scoring for Strikers**


In [ ]:
!pip install pulp
import pulp
!apt-get install -y -qq glpk-utils

from pulp import GLPK
import pandas as pd # Library to handle data
import numpy as np
from statistics import mean

data = pd.read_csv("/content/DEA Model 1_Strikers.csv", encoding = 'unicode_escape', engine ='python')
#creating a list to store the optimal decision variables
weights_matrix = np.empty((5,52))
for k in range(52):  # Where k represents the number of observations
    model = pulp.LpProblem("DEA Model 1 for Strikers (Goal-Scoring)", pulp.LpMaximize) # Create an LP maximization problem. We have 1 input, 6 outputs for goal scoring
    m1 = pulp.LpVariable("m1", lowBound=0.0001, upBound=None, cat='Continuous') # Create a variable m1>=0 , where m denotes my inputs. In DEA model 1, there is just 1 input - playing time
    n1 = pulp.LpVariable("n1", lowBound=0.0001, upBound=None, cat='Continuous') # Create a variable n1>=0, where n1 represents the weight associated with output 1 - with goal scoring, it will be goals scored
    n2 = pulp.LpVariable("n2", lowBound=0.0001, upBound=None, cat='Continuous') # Create a variable n2>=0  , simmilar to above
    n3 = pulp.LpVariable("n3", lowBound=0.0001, upBound=None, cat='Continuous') # Create a variable n3>=0
    n5 = pulp.LpVariable("n5", lowBound=0.0001, upBound=None, cat='Continuous') # Create a variable n5>=0
    
   
    model += n1*data["Gls"][k] + n2*data["SoT"][k] + n3*data["G-xG"][k]+ n5*data["GCA"][k]  #objective function
    
    model += m1*data["Minutes Played"][k] == 1 #first constraint (equality)

    for i in range(52): #NUMBER OF STRIKERS
        model += n1*data["Gls"][i] + n2*data["SoT"][i] + n3*data["G-xG"][i] + n5*data["GCA"][i] -  m1*data["Minutes Played"][i] <= 0
   

    #ADD IN RELATIVE WEIGHT RESTRICTIONS AND CONDITION FOR WEIGHTS TO BE POSITIVE.
    model += n1*data["Gls"][i] >= n2*data["SoT"][i]  #Goals > SoT
    model += n1*data["Gls"][i] >= n3*data["G-xG"][i]  #Goals > G-Xg
    model += n5*data["GCA"][i] >= n2*data["SoT"][i]  #GCA > Shots on Target
    model += n5*data["GCA"][i] >= n3*data["G-xG"][i]  #GCA > Big Chances Missed
    
  
    status = model.solve(GLPK(msg=True, options=['--ranges', 'sensitivity.txt'])) 
 
    
     # Displaying Optimal Decision Variables & Reduced Cost per Variable
    list_weights=[]
    for v in model.variables():
	      print(v.name, "=", v.varValue, "\tReduced Cost =", v.dj)
    for v in model.variables():  
        list_weights=list_weights+[v.varValue]
    for n in range(4):
        value= list_weights[n]
        weights_matrix[n,k] = value
        
    # Displaying Optimal Value of Objective Function	
    print(pulp.value(model.objective))
	
    # Displaying Shadow Price & Slack Value per Constraint
    print ("\nSensitivity Analysis\nConstraint\t\tShadow Price\tSlack")
    for name, c in model.constraints.items():
	      print(name, ":", c, "\t", c.pi, "\t\t", c.slack)
   
        
   
	

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
m1 = 0.000513084 	Reduced Cost = None
n1 = 0.0004 	Reduced Cost = None
n2 = 0.0001 	Reduced Cost = None
n3 = 0.0292793 	Reduced Cost = None
n5 = 0.059769 	Reduced Cost = None
0.94211562

Sensitivity Analysis
Constraint		Shadow Price	Slack
_C1 : 1949.0*m1 = 1.0 	 None 		 None
_C2 : -1949.0*m1 + 9.0*n1 + 22.0*n2 + 3.4*n3 + 14.0*n5 <= -0.0 	 None 		 None
_C3 : -3114.0*m1 + 17.0*n1 + 35.0*n2 + 6.7*n3 + 15.0*n5 <= -0.0 	 None 		 None
_C4 : -3082.0*m1 + 23.0*n1 + 47.0*n2 + 2.5*n3 + 25.0*n5 <= -0.0 	 None 		 None
_C5 : -2602.0*m1 + 6.0*n1 + 31.0*n2 - 5.9*n3 + 19.0*n5 <= -0.0 	 None 		 None
_C6 : -2838.0*m1 + 9.0*n1 + 32.0*n2 - 3.6*n3 + 9.0*n5 <= -0.0 	 None 		 None
_C7 : -2667.0*m1 + 9.0*n1 + 31.0*n2 + 0.3*n3 + 8.0*n5 <= -0.0 	 None 		 None
_C8 : -920.0*m1 + 11.0*n1 + 19.0*n2 + 5.7*n3 + 5.0*n5 <= -0.0 	 None 		 None
_C9 : -3078.0*m1 + 22.0*n1 + 46.0*n2 + 1.1*n3 + 14.0*n5 <= -0.0 	 None 		 None
_

In [ ]:
weights_matrix

array([[6.62252000e-001, 2.45700000e-001, 4.25532000e-001,
        3.25733000e-001, 4.06504000e-001, 3.78788000e-001,
        4.44444000e-001, 2.77008000e-001, 6.99301000e-001,
        3.03951000e-001, 2.44499000e-001, 2.38663000e-001,
        3.42466000e-001, 5.98802000e-001, 2.93255000e-001,
        3.93701000e-001, 5.12821000e-001, 2.28833000e-001,
        4.32900000e-001, 4.34783000e-001, 3.06748000e-001,
        5.95238000e-001, 2.14592000e-001, 2.30947000e-001,
        4.11523000e-001, 2.25225000e-001, 3.41297000e-001,
        4.32900000e-001, 4.87805000e-001, 3.18471000e-001,
        7.04225000e-001, 2.14592000e-001, 4.62963000e-001,
        4.46429000e-001, 6.89655000e-001, 2.00000000e-001,
        2.16450000e-001, 2.75482000e-001, 6.45161000e-001,
        2.55754000e-001, 5.07614000e-001, 2.29358000e-001,
        3.22581000e-001, 2.30947000e-001, 5.84795000e-001,
        2.33100000e-001, 2.12314000e-001, 5.40541000e-001,
        2.50000000e-001, 4.95050000e-001, 2.49377000e-00

In [ ]:
efficiency_table =np.empty((52,5))
average_list =[]
for row in range(52):
    row_values=[]
    for column in range(5):
       value = ((weights_matrix[1,column]*data["Gls"][row])+(weights_matrix[2,column]*data["SoT"][row])+(weights_matrix[3,column]*data["G-xG"][row])+(weights_matrix[4,column]*data["GCA"][row]))/((weights_matrix[0,column]*data["Minutes Played"][row]))
       efficiency_table[row,column]=value
       row_values=row_values+[value]
    average =mean(row_values)
    average_list =average_list+[average]

    average_list_rounded = [ '%.3f' % elem for elem in average_list ]

    player_list = ['Aaron Connolly', 'Adama TraorÃ©', 'Aleksandar MitroviÄ‡', 'Alexandre Lacazette', 'Anthony Martial', 'Anwar El Ghazi', 'Ashley Barnes', 'Bertrand TraorÃ©', 'Billy Sharp', 'Callum Wilson', 'Che Adams', 'Chris Wood', 'Christian Benteke', 'Daniel James', 'Danny Ings', 'Danny Welbeck', 'Diogo Jota', 'Dominic Calvert-Lewin', 'Edinson Cavani', 'FÃ¡bio Silva', 'Gabriel Jesus', 'Gareth Bale', 'Harry Kane', 'Jamie Vardy', 'Kelechi Iheanacho', 'Marcus Rashford', 'Mason Greenwood', 'MatÄ›j Vydra', 'Mbaye Diagne', 'Michail Antonio', 'Michy Batshuayi', 'Mohamed Salah', 'Oliver Burke', 'Oliver McBurnie', 'Olivier Giroud', 'Ollie Watkins', 'Patrick Bamford', 'Pierre-Emerick Aubameyang', 'RaÃºl JimÃ©nez', 'Raheem Sterling', 'Rhian Brewster', 'Richarlison', 'Riyad Mahrez', 'Roberto Firmino', 'SÃ©bastien Haller', 'Sadio ManÃ©', 'Son Heung-min', 'Tammy Abraham', 'Timo Werner', 'TrÃ©zÃ©guet', 'Wilfried Zaha', 'Willian JosÃ©']
for player in player_list:
    index = player_list.index(player)
    print(average_list_rounded[index])

display(efficiency_table)
efficiency_table = efficiency_table.round(decimals=3)
display(efficiency_table)


0.085
0.029
0.078
0.204
0.097
0.194
0.076
0.098
0.117
0.168
0.111
0.141
0.179
0.100
0.168
0.120
0.258
0.177
0.214
0.098
0.130
0.358
0.227
0.158
0.251
0.123
0.125
0.070
0.081
0.156
0.088
0.218
0.029
0.036
0.166
0.136
0.175
0.129
0.152
0.125
0.011
0.085
0.144
0.104
0.106
0.126
0.166
0.176
0.082
0.064
0.126
0.033


array([[2.02026600e-01, 6.19551109e-03, 3.27901281e-03, 2.10632357e-01,
        3.46143955e-03],
       [7.54572495e-02, 2.47999963e-03, 1.31255524e-03, 6.33528441e-02,
        1.38557880e-03],
       [1.99419450e-01, 5.95174662e-03, 3.14999895e-03, 1.78770625e-01,
        3.32524805e-03],
       [4.28423272e-01, 1.46431959e-02, 7.75000261e-03, 5.61769985e-01,
        8.18117132e-03],
       [2.42990550e-01, 7.60692454e-03, 4.02601217e-03, 2.25863540e-01,
        4.24999796e-03],
       [4.26418891e-01, 1.44356519e-02, 7.64015864e-03, 5.15912209e-01,
        8.06521622e-03],
       [1.80102499e-01, 5.55274898e-03, 2.93882697e-03, 1.87786729e-01,
        3.10232759e-03],
       [2.24338798e-01, 7.49997299e-03, 3.96940739e-03, 2.51747577e-01,
        4.19024400e-03],
       [2.28491941e-01, 7.67669273e-03, 4.06293742e-03, 3.38333275e-01,
        4.28897753e-03],
       [3.37673255e-01, 1.12747728e-02, 5.96724369e-03, 4.77626142e-01,
        6.29922922e-03],
       [2.54852252e-01, 8.4724

array([[0.202, 0.006, 0.003, 0.211, 0.003],
       [0.075, 0.002, 0.001, 0.063, 0.001],
       [0.199, 0.006, 0.003, 0.179, 0.003],
       [0.428, 0.015, 0.008, 0.562, 0.008],
       [0.243, 0.008, 0.004, 0.226, 0.004],
       [0.426, 0.014, 0.008, 0.516, 0.008],
       [0.18 , 0.006, 0.003, 0.188, 0.003],
       [0.224, 0.007, 0.004, 0.252, 0.004],
       [0.228, 0.008, 0.004, 0.338, 0.004],
       [0.338, 0.011, 0.006, 0.478, 0.006],
       [0.255, 0.008, 0.004, 0.281, 0.005],
       [0.318, 0.01 , 0.006, 0.364, 0.006],
       [0.41 , 0.014, 0.007, 0.459, 0.008],
       [0.211, 0.007, 0.004, 0.274, 0.004],
       [0.353, 0.012, 0.006, 0.459, 0.007],
       [0.259, 0.008, 0.004, 0.323, 0.005],
       [0.575, 0.02 , 0.01 , 0.674, 0.011],
       [0.396, 0.013, 0.007, 0.464, 0.007],
       [0.436, 0.015, 0.008, 0.604, 0.008],
       [0.234, 0.007, 0.004, 0.244, 0.004],
       [0.271, 0.009, 0.005, 0.362, 0.005],
       [0.739, 0.026, 0.014, 0.994, 0.015],
       [0.48 , 0.016, 0.009, 0.6

In [ ]:
!pip install pulp
import pulp
!apt-get install -y -qq glpk-utils

from pulp import GLPK
import pandas as pd # Library to handle data
import numpy as np
from statistics import mean

data = pd.read_csv("/content/DEA Model 1_Strikers.csv", encoding = 'unicode_escape', engine ='python')
#creating a list to store the optimal decision variables
weights_matrix = np.empty((5,52))
for k in range(52):  # Where k represents the number of observations
    model = pulp.LpProblem("DEA Model 1 for Strikers (Goal-Scoring)", pulp.LpMaximize) # Create an LP maximization problem. We have 1 input, 6 outputs for goal scoring
    n1 = pulp.LpVariable("n1", lowBound=0.000001, upBound=None, cat='Continuous') # Create a variable n1>=0, where n1 represents the weight associated with output 1 - with goal scoring, it will be goals scored
    n2 = pulp.LpVariable("n2", lowBound=0.000001, upBound=None, cat='Continuous') # Create a variable n2>=0  , simmilar to above
    n3 = pulp.LpVariable("n3", lowBound=0.000001, upBound=None, cat='Continuous') # Create a variable n3>=0
    n5 = pulp.LpVariable("n5", lowBound=0.000001, upBound=None, cat='Continuous') # Create a variable n5>=0
    m1 = pulp.LpVariable("m1", lowBound=0.000001, upBound=None, cat='Continuous') # Create a variable m1>=0 , where m is denotes my inputs. In DEA model 1, there is just 1 input - playing time
    
   
    model += n1*data["Gls"][k] + n2*data["SoT"][k] + n3*data["G-xG"][k]+ n5*data["GCA"][k]  #objective function
    
    model += m1*data["Minutes Played"][k] == 1 #first constraint (equality)

    for i in range(52): #NUMBER OF STRIKERS
        model += n1*data["Gls"][i] + n2*data["SoT"][i] + n3*data["G-xG"][i] + n5*data["GCA"][i] -  m1*data["Minutes Played"][i] <= 0
   

    #ADD IN RELATIVE WEIGHT RESTRICTIONS AND CONDITION FOR WEIGHTS TO BE POSITIVE.
    model += n1*data["Gls"][i] >= n2*data["SoT"][i]  #Goals > SoT
    model += n1*data["Gls"][i] >= n3*data["G-xG"][i]  #Goals > G-Xg
    model += n5*data["GCA"][i] >= n2*data["SoT"][i]  #GCA > Shots on Target
    model += n5*data["GCA"][i] >= n3*data["G-xG"][i]  #GCA > Big Chances Missed
    
  
    status = model.solve(GLPK(msg=True, options=['--ranges', 'sensitivity.txt'])) 

    # Displaying Optimal Value of Objective Function	
    print(pulp.value(model.objective))

        
   
	

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
0.2629553
0.2792096
0.43965150000000003
0.5653984000000001
0.6663608999999999
0.5184988999999999
0.25747152
0.4788584
0.3413613
0.6934944000000001
0.43097667
0.47471918
0.54184582
0.43207879
0.6398673
0.45218206
0.7050339999999999
0.55256016
0.6082565999999999
0.4082504
0.6573213
0.9999975999999999
0.99999951
0.9115333
0.6878812000000001
0.7599143
0.43550635000000004
0.5394977
0.7257570000000001
0.69209455
0.37075964
0.7136050999999999
0.12007287999999999
0.2793288
0.4472412
0.5668737500000001
0.7310949
0.44382024000000003
0.6842971999999999
0.7291533
0.04964335
0.40416202
0.9454084
0.43418074
0.2677755
0.5539168
0.6913076600000001
0.4825122
0.9001177
0.26136064000000003
0.6177558
0.13727324000000002


In [ ]:
!pip install pulp
import pulp
!apt-get install -y -qq glpk-utils

from pulp import GLPK
import pandas as pd # Library to handle data
import numpy as np
from statistics import mean

data = pd.read_csv("/content/DEA Model 1_Strikers.csv", encoding = 'unicode_escape', engine ='python')
#creating a list to store the optimal decision variables
weights_matrix = np.empty((6,52))
for k in range(52):  # Where k represents the number of observations
    model = pulp.LpProblem("DEA Model 1 for Strikers (Goal-Scoring)", pulp.LpMaximize) # Create an LP maximization problem. We have 1 input, 6 outputs for goal scoring
    n1 = pulp.LpVariable("n1", lowBound=0.0000001, upBound=None, cat='Continuous') # Create a variable n1>=0, where n1 represents the weight associated with output 1 - with goal scoring, it will be goals scored
    n2 = pulp.LpVariable("n2", lowBound=0.0000001, upBound=None, cat='Continuous') # Create a variable n2>=0  , simmilar to above
    n3 = pulp.LpVariable("n3", lowBound=0.0000001, upBound=None, cat='Continuous') # Create a variable n3>=0
    n4 = pulp.LpVariable("n4", lowBound=0.0000001, upBound=None, cat='Continuous') # Create a variable n4>=0
    n5 = pulp.LpVariable("n5", lowBound=0.0000001, upBound=None, cat='Continuous') # Create a variable n5>=0
    m1 = pulp.LpVariable("m1", lowBound=0.0000001, upBound=None, cat='Continuous') # Create a variable m1>=0 , where m is denotes my inputs. In DEA model 1, there is just 1 input - playing time
    
   
    model += n1*data["Gls"][k] + n2*data["SoT"][k] + n3*data["G-xG"][k]+ n4*data["Big Chances Missed"][k] + n5*data["GCA"][k]  #objective function
    
    model += m1*data["Minutes Played"][k] == 1 #first constraint (equality)

    for i in range(52): #NUMBER OF STRIKERS
        model += n1*data["Gls"][i] + n2*data["SoT"][i] + n3*data["G-xG"][i] + n4*data["Big Chances Missed"][i] + n5*data["GCA"][i] -  m1*data["Minutes Played"][i] <= 0
   

    #ADD IN RELATIVE WEIGHT RESTRICTIONS AND CONDITION FOR WEIGHTS TO BE POSITIVE.
    model += n1 >= n2  #Goals > SoT
    model += n1 >= n3   #Goals > G-Xg
    model += n1 >= n4  #Goals > Big Chances Missed
    model += n4 >= n2  #Goals > Shots on Target
    model += n5 >= n2  #Goals > Shots on Target
    model += n5 >= n4  #Goals > Big Chances Missed
    status = model.solve(GLPK(msg=True, options=['--ranges', 'sensitivity.txt'])) 
    
    
    # Displaying Optimal Value of Objective Function	
    print(pulp.value(model.objective))
	

	

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
0.71670225148
0.489212183
0.7142540741000001
0.6130505089999999
0.8639219158799999
0.5991868680000001
0.54741888224
0.6301720469150001
0.9999976370000001
0.7820904347699998
0.51989110415
0.50764620414
0.592480236
0.9453221170000001
0.71103113846
0.6608201616800001
0.7689690329999999
0.52104746988
0.6847871480000001
0.66507503009
0.78923335192
0.9999983290000001
0.9999982499999999
0.938456037
0.734123186
0.814451943
0.57307442358
0.7909264551199999
0.96396099484
0.8193519868
0.86732988406
0.64873604065
0.50109212872
0.6161015223999999
0.698867452
0.6042229399100001
0.7506626108000001
0.54467771666
0.98713272064
0.810435126
0.517083633
0.52182107
0.97428705077
0.52547929526
0.62919263
0.6345810502499999
0.6731302672399999
0.66591976
0.941320762
0.60957390528
0.67890944951
0.719631176


**2) Creativity for strikers**

In [ ]:
from pulp import GLPK
import pandas as pd # Library to handle data
import numpy as np
from statistics import mean

data = pd.read_csv("/content/DEA Model 1_Strikers.csv", encoding = 'unicode_escape', engine ='python')
#creating a list to store the optimal decision variables
weights_matrix = np.empty((6,52))
for k in range(52):  # Where k represents the number of observations
    model = pulp.LpProblem("DEA Model 1 for Strikers (Creativity)", pulp.LpMaximize) # Create an LP maximization problem. We have 1 input, 6 outputs for goal scoring
    n1 = pulp.LpVariable("n1", lowBound=0.000001, upBound=None, cat='Continuous') # Create a variable n1>=0, where n1 represents the weight associated with output 1 - with goal scoring, it will be goals scored
    n2 = pulp.LpVariable("n2", lowBound=0.000001, upBound=None, cat='Continuous') # Create a variable n2>=0  , simmilar to above
    n3 = pulp.LpVariable("n3", lowBound=0.000001, upBound=None, cat='Continuous') # Create a variable n3>=0
    n4 = pulp.LpVariable("n4", lowBound=0.000001, upBound=None, cat='Continuous') # Create a variable n4>=0
    n5 = pulp.LpVariable("n5", lowBound=0.000001, upBound=None, cat='Continuous') # Create a variable n4>=0
    m1 = pulp.LpVariable("m1", lowBound=0.000001, upBound=None, cat='Continuous') # Create a variable m1>=0 , where m is denotes my inputs. In DEA model 1, there is just 1 input - playing time

    model += n1*data["xA"][k] + n2*data["KP"][k] + n3*data["PPA"][k]+ n4*data["SCA"][k] + n5*data["Progressive Passes"][k] #objective function
    
    model += m1*data["Minutes Played"][k] == 1 #first constraint (equality)

    for i in range(52): #NUMBER OF STRIKERS
        model += n1*data["xA"][i] + n2*data["KP"][i] + n3*data["PPA"][i] + n4*data["SCA"][i] + n5*data["Progressive Passes"][i] - m1*data["Minutes Played"][i] <= 0
   
    status = model.solve(GLPK(msg=True, options=['--ranges', 'sensitivity.txt'])) 
    print("Model Status:{}".format(pulp.LpStatus[model.status])) 
    
    #ADD IN RELATIVE WEIGHT RESTRICTIONS AND CONDITION FOR WEIGHTS TO BE POSITIVE.
    model += n1 >= n3 #xA > PPA
    model += n2 >= n3  #KP > PPA
    model += n4 >= n3   #SCA > PPA
    model += n1 >= n2   #SCA > PPA

    # Displaying Optimal Decision Variables & Reduced Cost per Variable
    list_weights=[]
    for v in model.variables():
	      print(v.name, "=", v.varValue, "\tReduced Cost =", v.dj)
    for v in model.variables():  
        list_weights=list_weights+[v.varValue]
    for n in range(5):
        value= list_weights[n]
        weights_matrix[n,k] = value
        
    # Displaying Optimal Value of Objective Function	
    print("Objective=", pulp.value(model.objective))
	
    # Displaying Shadow Price & Slack Value per Constraint
    print ("\nSensitivity Analysis\nConstraint\t\tShadow Price\tSlack")
    for name, c in model.constraints.items():
	      print(name, ":", c, "\t", c.pi, "\t\t", c.slack)

Model Status:Optimal
m1 = 0.00108696 	Reduced Cost = None
n1 = 1e-06 	Reduced Cost = None
n2 = 1e-06 	Reduced Cost = None
n3 = 0.0113755 	Reduced Cost = None
n4 = 0.0181764 	Reduced Cost = None
n5 = 1e-06 	Reduced Cost = None
Objective= 0.9999998999999999

Sensitivity Analysis
Constraint		Shadow Price	Slack
_C1 : 920.0*m1 = 1.0 	 None 		 None
_C2 : -920.0*m1 + 1.9*n1 + 20.0*n2 + 16.0*n3 + 45.0*n4 + 32.0*n5 <= -0.0 	 None 		 None
_C3 : -1112.0*m1 + 1.6*n1 + 12.0*n2 + 14.0*n3 + 34.0*n4 + 46.0*n5 <= -0.0 	 None 		 None
_C4 : -1459.0*m1 + 2.9*n1 + 25.0*n2 + 22.0*n3 + 44.0*n4 + 29.0*n5 <= -0.0 	 None 		 None
_C5 : -3082.0*m1 + 7.4*n1 + 48.0*n2 + 41.0*n3 + 113.0*n4 + 125.0*n5 <= -0.0 	 None 		 None
_C6 : -3078.0*m1 + 6.3*n1 + 54.0*n2 + 74.0*n3 + 117.0*n4 + 137.0*n5 <= -0.0 	 None 		 None
_C7 : -1375.0*m1 + 2.7*n1 + 15.0*n2 + 13.0*n3 + 34.0*n4 + 18.0*n5 <= -0.0 	 None 		 None
_C8 : -1923.0*m1 + 2.7*n1 + 18.0*n2 + 21.0*n3 + 46.0*n4 + 46.0*n5 <= -0.0 	 None 		 None
_C9 : -1613.0*m1 + 2.3*n1 + 2

In [ ]:
efficiency_table =np.empty((52,5))
average_list =[]
for row in range(52):
    row_values=[]
    for column in range(5):
       value = ((weights_matrix[1,column]*data["xA"][row])+(weights_matrix[2,column]*data["KP"][row])+(weights_matrix[3,column]*data["PPA"][row])+(weights_matrix[4,column]*data["SCA"][row])++(weights_matrix[5,column]*data["Progressive Passes"][row]))/((weights_matrix[0,column]*data["Minutes Played"][row]))
       efficiency_table[row,column]=value
       row_values=row_values+[value]
    average =mean(row_values)
    average_list =average_list+[average]

    average_list_rounded = [ '%.2f' % elem for elem in average_list ]

    player_list = ['Aaron Connolly', 'Adama TraorÃ©', 'Aleksandar MitroviÄ‡', 'Alexandre Lacazette', 'Anthony Martial', 'Anwar El Ghazi', 'Ashley Barnes', 'Bertrand TraorÃ©', 'Billy Sharp', 'Callum Wilson', 'Che Adams', 'Chris Wood', 'Christian Benteke', 'Daniel James', 'Danny Ings', 'Danny Welbeck', 'Diogo Jota', 'Dominic Calvert-Lewin', 'Edinson Cavani', 'FÃ¡bio Silva', 'Gabriel Jesus', 'Gareth Bale', 'Harry Kane', 'Jamie Vardy', 'Kelechi Iheanacho', 'Marcus Rashford', 'Mason Greenwood', 'MatÄ›j Vydra', 'Mbaye Diagne', 'Michail Antonio', 'Michy Batshuayi', 'Mohamed Salah', 'Oliver Burke', 'Oliver McBurnie', 'Olivier Giroud', 'Ollie Watkins', 'Patrick Bamford', 'Pierre-Emerick Aubameyang', 'RaÃºl JimÃ©nez', 'Raheem Sterling', 'Rhian Brewster', 'Richarlison', 'Riyad Mahrez', 'Roberto Firmino', 'SÃ©bastien Haller', 'Sadio ManÃ©', 'Son Heung-min', 'Tammy Abraham', 'Timo Werner', 'TrÃ©zÃ©guet', 'Wilfried Zaha', 'Willian JosÃ©']
for player in player_list:
    index = player_list.index(player)
    print(average_list_rounded[index])

display(efficiency_table)
efficiency_table = efficiency_table.round(decimals=2)
display(efficiency_table)

0.46
0.28
0.33
0.34
0.41
0.24
0.23
0.32
0.19
0.14
0.15
0.18
0.19
0.23
0.17
0.40
0.19
0.27
0.24
0.47
0.15
0.26
0.29
0.21
0.46
0.29
0.23
0.34
0.35
0.27
0.09
0.25
0.18
0.36
0.22
0.31
0.18
0.25
0.22
0.12
0.22
0.29
0.20
0.31
0.22
0.23
0.23
0.23
0.16
0.40
0.21
0.16


array([[9.99964700e-01, 1.00200822e-04, 9.52367427e-01, 3.03361755e-01,
        6.25525770e-02],
       [6.43061561e-01, 6.15999709e-05, 5.04240211e-01, 1.89628538e-01,
        4.52528407e-02],
       [6.62127052e-01, 7.15673411e-05, 7.61558155e-01, 1.87066711e-01,
        5.41927214e-02],
       [7.52351055e-01, 7.55524627e-05, 6.89006816e-01, 2.27396773e-01,
        4.78450260e-02],
       [8.87263961e-01, 9.07880013e-05, 8.48166895e-01, 2.35786722e-01,
        8.63400170e-02],
       [5.12452946e-01, 5.23246298e-05, 4.83701605e-01, 1.53364719e-01,
        3.39999093e-02],
       [5.14308782e-01, 5.07136526e-05, 4.37371718e-01, 1.48364011e-01,
        3.92445510e-02],
       [6.86996138e-01, 6.84572523e-05, 6.45920880e-01, 2.11473780e-01,
        4.01491014e-02],
       [4.30603305e-01, 4.16387469e-05, 3.70620605e-01, 1.29775440e-01,
        2.77207368e-02],
       [3.31330162e-01, 3.09857046e-05, 2.52207853e-01, 1.07999234e-01,
        1.38054052e-02],
       [3.09556982e-01, 3.0900

array([[1.  , 0.  , 0.95, 0.3 , 0.06],
       [0.64, 0.  , 0.5 , 0.19, 0.05],
       [0.66, 0.  , 0.76, 0.19, 0.05],
       [0.75, 0.  , 0.69, 0.23, 0.05],
       [0.89, 0.  , 0.85, 0.24, 0.09],
       [0.51, 0.  , 0.48, 0.15, 0.03],
       [0.51, 0.  , 0.44, 0.15, 0.04],
       [0.69, 0.  , 0.65, 0.21, 0.04],
       [0.43, 0.  , 0.37, 0.13, 0.03],
       [0.33, 0.  , 0.25, 0.11, 0.01],
       [0.31, 0.  , 0.3 , 0.11, 0.01],
       [0.37, 0.  , 0.39, 0.12, 0.02],
       [0.48, 0.  , 0.3 , 0.15, 0.02],
       [0.53, 0.  , 0.45, 0.16, 0.03],
       [0.35, 0.  , 0.36, 0.12, 0.  ],
       [0.73, 0.  , 1.  , 0.23, 0.03],
       [0.42, 0.  , 0.39, 0.14, 0.01],
       [0.61, 0.  , 0.48, 0.2 , 0.02],
       [0.56, 0.  , 0.45, 0.17, 0.04],
       [1.  , 0.  , 1.  , 0.27, 0.1 ],
       [0.31, 0.  , 0.33, 0.11, 0.01],
       [0.57, 0.  , 0.53, 0.18, 0.03],
       [0.65, 0.  , 0.56, 0.21, 0.02],
       [0.44, 0.  , 0.45, 0.12, 0.04],
       [0.99, 0.  , 0.95, 0.27, 0.09],
       [0.69, 0.  , 0.5 ,

In [ ]:
from pulp import GLPK
import pandas as pd # Library to handle data
import numpy as np
from statistics import mean

data = pd.read_csv("/content/DEA Model 1_Strikers.csv", encoding = 'unicode_escape', engine ='python')
#creating a list to store the optimal decision variables
weights_matrix = np.empty((6,52))
for k in range(52):  # Where k represents the number of observations
    model = pulp.LpProblem("DEA Model 1 for Strikers (Creativity)", pulp.LpMaximize) # Create an LP maximization problem. We have 1 input, 6 outputs for goal scoring
    n1 = pulp.LpVariable("n1", lowBound=0.000001, upBound=None, cat='Continuous') # Create a variable n1>=0, where n1 represents the weight associated with output 1 - with goal scoring, it will be goals scored
    n2 = pulp.LpVariable("n2", lowBound=0.000001, upBound=None, cat='Continuous') # Create a variable n2>=0  , simmilar to above
    n3 = pulp.LpVariable("n3", lowBound=0.000001, upBound=None, cat='Continuous') # Create a variable n3>=0
    n4 = pulp.LpVariable("n4", lowBound=0.000001, upBound=None, cat='Continuous') # Create a variable n4>=0
    n5 = pulp.LpVariable("n5", lowBound=0.000001, upBound=None, cat='Continuous') # Create a variable n4>=0
    m1 = pulp.LpVariable("m1", lowBound=0.000001, upBound=None, cat='Continuous') # Create a variable m1>=0 , where m is denotes my inputs. In DEA model 1, there is just 1 input - playing time

    model += n1*data["xA"][k] + n2*data["KP"][k] + n3*data["PPA"][k]+ n4*data["SCA"][k] + n5*data["Progressive Passes"][k] #objective function
    
    model += m1*data["Minutes Played"][k] == 1 #first constraint (equality)

    for i in range(52): #NUMBER OF STRIKERS
        model += n1*data["xA"][i] + n2*data["KP"][i] + n3*data["PPA"][i] + n4*data["SCA"][i] + n5*data["Progressive Passes"][i] - m1*data["Minutes Played"][i] <= 0
   
    status = model.solve(GLPK(msg=True, options=['--ranges', 'sensitivity.txt'])) 
    
    #ADD IN RELATIVE WEIGHT RESTRICTIONS AND CONDITION FOR WEIGHTS TO BE POSITIVE.
    model += n1 >= n3 #xA > PPA
    model += n2 >= n3  #KP > PPA
    model += n4 >= n3   #SCA > PPA
    model += n1 >= n2   #SCA > PPA

    # Displaying Optimal Decision Variables & Reduced Cost per Variable
    list_weights=[]
    for v in model.variables():
	      print(v.name, "=", v.varValue, "\tReduced Cost =", v.dj)
    for v in model.variables():  
        list_weights=list_weights+[v.varValue]
    for n in range(5):
        value= list_weights[n]
        weights_matrix[n,k] = value
        
    # Displaying Optimal Value of Objective Function	
    print(pulp.value(model.objective))
	
	

m1 = 0.00108696 	Reduced Cost = None
n1 = 1e-06 	Reduced Cost = None
n2 = 1e-06 	Reduced Cost = None
n3 = 0.0113755 	Reduced Cost = None
n4 = 0.0181764 	Reduced Cost = None
n5 = 1e-06 	Reduced Cost = None
0.9999998999999999
m1 = 0.000899281 	Reduced Cost = None
n1 = 1e-06 	Reduced Cost = None
n2 = 1e-06 	Reduced Cost = None
n3 = 1e-06 	Reduced Cost = None
n4 = 1e-06 	Reduced Cost = None
n5 = 0.0190444 	Reduced Cost = None
0.876104
m1 = 0.000685401 	Reduced Cost = None
n1 = 1e-06 	Reduced Cost = None
n2 = 0.025663 	Reduced Cost = None
n3 = 0.00545165 	Reduced Cost = None
n4 = 1e-06 	Reduced Cost = None
n5 = 1e-06 	Reduced Cost = None
0.7615872
m1 = 0.000324465 	Reduced Cost = None
n1 = 1e-06 	Reduced Cost = None
n2 = 1e-06 	Reduced Cost = None
n3 = 1e-06 	Reduced Cost = None
n4 = 0.00201151 	Reduced Cost = None
n5 = 0.00526495 	Reduced Cost = None
0.88551578
m1 = 0.000324886 	Reduced Cost = None
n1 = 1e-06 	Reduced Cost = None
n2 = 1e-06 	Reduced Cost = None
n3 = 0.00116436 	Reduced Cos

In [ ]:
!pip install pulp
import pulp
!apt-get install -y -qq glpk-utils

from pulp import GLPK
import pandas as pd # Library to handle data
import numpy as np
from statistics import mean

data = pd.read_csv("/content/DEA Model 1_Strikers.csv", encoding = 'unicode_escape', engine ='python')
#creating a list to store the optimal decision variables
weights_matrix = np.empty((6,52))
for k in range(52):  # Where k represents the number of observations
    model = pulp.LpProblem("DEA Model 1 for Strikers (Creativity)", pulp.LpMaximize) # Create an LP maximization problem. We have 1 input, 6 outputs for goal scoring
    n1 = pulp.LpVariable("n1", lowBound=0.000001, upBound=None, cat='Continuous') # Create a variable n1>=0, where n1 represents the weight associated with output 1 - with goal scoring, it will be goals scored
    n2 = pulp.LpVariable("n2", lowBound=0.000001, upBound=None, cat='Continuous') # Create a variable n2>=0  , simmilar to above
    n3 = pulp.LpVariable("n3", lowBound=0.000001, upBound=None, cat='Continuous') # Create a variable n3>=0
    n4 = pulp.LpVariable("n4", lowBound=0.000001, upBound=None, cat='Continuous') # Create a variable n4>=0
    n5 = pulp.LpVariable("n5", lowBound=0.000001, upBound=None, cat='Continuous') # Create a variable n4>=0
    m1 = pulp.LpVariable("m1", lowBound=0.000001, upBound=None, cat='Continuous') # Create a variable m1>=0 , where m is denotes my inputs. In DEA model 1, there is just 1 input - playing time

    model += n1*data["xA"][k] + n2*data["KP"][k] + n3*data["PPA"][k]+ n4*data["SCA"][k] + n5*data["Progressive Passes"][k] #objective function
    
    model += m1*data["Minutes Played"][k] == 1 #first constraint (equality)

    for i in range(52): #NUMBER OF STRIKERS
        model += n1*data["xA"][i] + n2*data["KP"][i] + n3*data["PPA"][i] + n4*data["SCA"][i] + n5*data["Progressive Passes"][i] - m1*data["Minutes Played"][i] <= 0
   
    status = model.solve(GLPK(msg=True, options=['--ranges', 'sensitivity.txt'])) 
    
    #ADD IN RELATIVE WEIGHT RESTRICTIONS AND CONDITION FOR WEIGHTS TO BE POSITIVE.
    model += n1 >= n3 #xA > PPA
    model += n2 >= n3  #KP > PPA
    model += n4 >= n3   #SCA > PPA
    model += n1 >= n2   #SCA > PPA


        
    # Displaying Optimal Value of Objective Function	
    print(pulp.value(model.objective))



Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
0.9999998999999999
0.876104
0.7615872
0.88551578
0.97765783
0.6486254
0.54567714
0.6971093
0.45477239999999997
0.3573071199999999
0.36708843
0.45269811
0.5103082
0.56819893
0.42415959999999997
0.99999993
0.5698598
0.6731568
0.57992161
1.0000021
0.37603941999999996
0.6038325999999999
0.72276362
0.47094792999999996
0.98749891
0.70154693
0.59001754
0.8285610399999999
0.8020568899999999
0.6672697000000001
0.26965559999999994
0.7183246
0.45476202999999993
1.00000052
0.5975167
0.7113465
0.4629358
0.66276778
0.6367626000000001
0.3101468
0.571633
0.7743550999999999
0.52429873
0.73047445
0.5529539
0.5687926
0.6158494
0.6937957
0.41808309999999993
0.93507508
0.49899892
0.4978233


3) Dribbling and Ball Carrying for Strikers

In [ ]:
!pip install pulp
import pulp
!apt-get install -y -qq glpk-utils

from pulp import GLPK
import pandas as pd # Library to handle data
import numpy as np
from statistics import mean

data = pd.read_csv("/content/DEA Model 1_Strikers.csv", encoding = 'unicode_escape', engine ='python')
#creating a list to store the optimal decision variables
weights_matrix = np.empty((7,52))
for k in range(52):  # Where k represents the number of observations
    model = pulp.LpProblem("DEA Model 1 for Strikers (Dribbling and Ball Carrying)", pulp.LpMaximize) # Create an LP maximization problem. We have 1 input, 6 outputs for goal scoring
    n1 = pulp.LpVariable("n1", lowBound=0.00000001, upBound=None, cat='Continuous') # Create a variable n1>=0, where n1 represents the weight associated with output 1 - with goal scoring, it will be goals scored
    n2 = pulp.LpVariable("n2", lowBound=0.00000001, upBound=None, cat='Continuous') # Create a variable n2>=0  , simmilar to above
    n3 = pulp.LpVariable("n3", lowBound=0.00000001, upBound=None, cat='Continuous') # Create a variable n3>=0
    n4 = pulp.LpVariable("n4", lowBound=0.00000001, upBound=None, cat='Continuous') # Create a variable n4>=0
    n5 = pulp.LpVariable("n5", lowBound=0.00000001, upBound=None, cat='Continuous') # Create a variable n5>=0
    n6 = pulp.LpVariable("n6", lowBound=0.00000001, upBound=None, cat='Continuous') # Create a variable n6>=0
    m1 = pulp.LpVariable("m1", lowBound=0.00000001, upBound=None, cat='Continuous') # Create a variable m1>=0 , where m is denotes my inputs. In DEA model 1, there is just 1 input - playing time
    
    model += n1*data["Dribbles Succ"][k] + n2*data["SCA Drib"][k] + n3*data["GCA Drib"][k]+ n4*data["Carry PrgDist"][k] + n5*data["Carries Final Third"][k] + n6*data["Carry into box"][k]    #objective function
    
    model += m1*data["Minutes Played"][k] == 1 #first constraint (equality)

    for i in range(52): #NUMBER OF STRIKERS
        model += n1*data["Dribbles Succ"][i] + n2*data["SCA Drib"][i] + n3*data["GCA Drib"][i] + n4*data["Carry PrgDist"][i] + n5*data["Carries Final Third"][i] + n6*data["Carry into box"][i] - m1*data["Minutes Played"][i] <= 0
   
    status = model.solve(GLPK(msg=True, options=['--ranges', 'sensitivity.txt'])) 
    print("Model Status:{}".format(pulp.LpStatus[model.status])) 
    
    #ADD IN RELATIVE WEIGHT RESTRICTIONS
    model += n3*data["GCA Drib"][k] >= n1*data["Dribbles Succ"][k]   
    model += n3*data["GCA Drib"][k] >= n4*data["Carry PrgDist"][k]   
    model += n3*data["GCA Drib"][k] >= n5*data["Carries Final Third"][k]  
    model += n3*data["GCA Drib"][k] >= n6*data["Carry into box"][k]    
    model += n2*data["SCA Drib"][k] >= n1*data["Dribbles Succ"][k]   
    model += n2*data["SCA Drib"][k] >= n4*data["Carry PrgDist"][k]   
    model += n2*data["SCA Drib"][k] >= n5*data["Carries Final Third"][k]   
    model += n2*data["SCA Drib"][k] >= n6*data["Carry into box"][k]    

    # Displaying Optimal Decision Variables & Reduced Cost per Variable
    list_weights=[]
    for v in model.variables():
	      print(v.name, "=", v.varValue, "\tReduced Cost =", v.dj)
    for v in model.variables():  
        list_weights=list_weights+[v.varValue]
    for n in range(6):
        value= list_weights[n]
        weights_matrix[n,k] = value

    # Displaying Optimal Value of Objective Function	
    print("Objective=", pulp.value(model.objective))
	
    # Displaying Shadow Price & Slack Value per Constraint
    print ("\nSensitivity Analysis\nConstraint\t\tShadow Price\tSlack")
    for name, c in model.constraints.items():
	      print(name, ":", c, "\t", c.pi, "\t\t", c.slack)
	

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Model Status:Optimal
m1 = 0.00108696 	Reduced Cost = None
n1 = 1e-08 	Reduced Cost = None
n2 = 0.124999 	Reduced Cost = None
n3 = 1e-08 	Reduced Cost = None
n4 = 1e-08 	Reduced Cost = None
n5 = 1e-08 	Reduced Cost = None
n6 = 1e-08 	Reduced Cost = None
Objective= 1.0000038900000001

Sensitivity Analysis
Constraint		Shadow Price	Slack
_C1 : 920.0*m1 = 1.0 	 None 		 None
_C2 : -920.0*m1 + 29.0*n1 + 8.0*n2 + 1132.0*n4 + 17.0*n5 + 11.0*n6 <= -0.0 	 None 		 None
_C3 : -1112.0*m1 + 26.0*n1 + 2.0*n2 + n3 + 1734.0*n4 + 28.0*n5 + 20.0*n6 <= -0.0 	 None 		 None
_C4 : -1459.0*m1 + 29.0*n1 + 6.0*n2 + n3 + 1154.0*n4 + 25.0*n5 + 8.0*n6 <= -0.0 	 None 		 None
_C5 : -3082.0*m1 + 46.0*n1 + 18.0*n2 + 6.0*n3 + 2537.0*n4 + 53.0*n5 + 26.0*n6 <= -0.0 	 None 		 None
_C6 : -3078.0*m1 + 50.0*n1 + 6.0*n2 + 3460.0*n4 + 52.0*n5 + 54.0*n6 <= -0.0 	 None 		 None
_C7 : -1375.0*m1 + 6.0*n1 + 2.0*n2 + 207.0*n4 + 3.0*n5 +

In [ ]:
efficiency_table =np.empty((52,7))
average_list =[]
for row in range(52):
    row_values=[]
    for column in range(7):
       value = ((weights_matrix[1,column]*data["Dribbles Succ"][row])+(weights_matrix[2,column]*data["SCA Drib"][row])+(weights_matrix[3,column]*data["GCA Drib"][row])+(weights_matrix[4,column]*data["Carry PrgDist"][row])+(weights_matrix[5,column]*data["Carries Final Third"][row])+ (weights_matrix[6,column]*data["Carry into box"][row]))/((weights_matrix[0,column]*data["Minutes Played"][row]))
       efficiency_table[row,column]=value
       row_values=row_values+[value]
    average =mean(row_values)
    average_list =average_list+[average]

    average_list_rounded = [ '%.2f' % elem for elem in average_list ]

    player_list = ['Aaron Connolly', 'Adama TraorÃ©', 'Aleksandar MitroviÄ‡', 'Alexandre Lacazette', 'Anthony Martial', 'Anwar El Ghazi', 'Ashley Barnes', 'Bertrand TraorÃ©', 'Billy Sharp', 'Callum Wilson', 'Che Adams', 'Chris Wood', 'Christian Benteke', 'Daniel James', 'Danny Ings', 'Danny Welbeck', 'Diogo Jota', 'Dominic Calvert-Lewin', 'Edinson Cavani', 'FÃ¡bio Silva', 'Gabriel Jesus', 'Gareth Bale', 'Harry Kane', 'Jamie Vardy', 'Kelechi Iheanacho', 'Marcus Rashford', 'Mason Greenwood', 'MatÄ›j Vydra', 'Mbaye Diagne', 'Michail Antonio', 'Michy Batshuayi', 'Mohamed Salah', 'Oliver Burke', 'Oliver McBurnie', 'Olivier Giroud', 'Ollie Watkins', 'Patrick Bamford', 'Pierre-Emerick Aubameyang', 'RaÃºl JimÃ©nez', 'Raheem Sterling', 'Rhian Brewster', 'Richarlison', 'Riyad Mahrez', 'Roberto Firmino', 'SÃ©bastien Haller', 'Sadio ManÃ©', 'Son Heung-min', 'Tammy Abraham', 'Timo Werner', 'TrÃ©zÃ©guet', 'Wilfried Zaha', 'Willian JosÃ©']
for player in player_list:
    index = player_list.index(player)
    print(average_list_rounded[index])

display(efficiency_table)
efficiency_table = efficiency_table.round(decimals=2)
display(efficiency_table)

0.57
0.42
0.44
0.71
0.23
0.09
0.12
0.27
0.21
0.09
0.08
0.22
0.22
0.50
0.01
0.35
0.41
0.33
0.48
0.46
0.22
0.20
0.35
0.26
0.37
0.57
0.49
0.61
0.57
0.15
0.05
0.10
0.09
0.31
0.14
0.42
0.16
0.25
0.36
0.26
0.44
0.43
0.07
0.31
0.05
0.65
0.26
0.05
0.12
0.71
0.27
0.06


array([[1.00000058e+00, 3.98991080e-01, 5.11324266e-01, 3.97309551e-05,
        8.00916723e-02, 9.99999731e-01, 9.99998976e-01],
       [2.06847017e-01, 8.01263242e-01, 9.38885627e-01, 4.61966611e-01,
        8.36051424e-02, 2.06852956e-01, 2.53890532e-01],
       [4.72928989e-01, 5.66294223e-01, 6.58684351e-01, 3.52083015e-01,
        6.20580289e-02, 4.72929602e-01, 4.86790511e-01],
       [6.71642155e-01, 9.28908152e-01, 1.00000077e+00, 9.99997410e-01,
        5.57306603e-02, 6.71641572e-01, 6.54219773e-01],
       [2.24179676e-01, 3.64784658e-01, 4.67487254e-01, 3.57263274e-05,
        5.68226167e-02, 2.24183445e-01, 2.49787558e-01],
       [1.67272299e-01, 4.71108889e-02, 6.03746367e-02, 4.88636539e-06,
        1.02940164e-02, 1.67271897e-01, 1.64735809e-01],
       [1.79408492e-01, 1.12285278e-01, 1.43898423e-01, 1.11868620e-05,
        2.45345950e-02, 1.79408939e-01, 1.92644876e-01],
       [2.85190378e-01, 4.28366223e-01, 5.48969703e-01, 3.58642744e-05,
        6.44816844e-02, 2

array([[1.  , 0.4 , 0.51, 0.  , 0.08, 1.  , 1.  ],
       [0.21, 0.8 , 0.94, 0.46, 0.08, 0.21, 0.25],
       [0.47, 0.57, 0.66, 0.35, 0.06, 0.47, 0.49],
       [0.67, 0.93, 1.  , 1.  , 0.06, 0.67, 0.65],
       [0.22, 0.36, 0.47, 0.  , 0.06, 0.22, 0.25],
       [0.17, 0.05, 0.06, 0.  , 0.01, 0.17, 0.16],
       [0.18, 0.11, 0.14, 0.  , 0.02, 0.18, 0.19],
       [0.29, 0.43, 0.55, 0.  , 0.06, 0.29, 0.31],
       [0.19, 0.28, 0.3 , 0.28, 0.02, 0.19, 0.2 ],
       [0.08, 0.17, 0.21, 0.  , 0.03, 0.08, 0.09],
       [0.11, 0.1 , 0.13, 0.  , 0.02, 0.11, 0.12],
       [0.19, 0.31, 0.33, 0.34, 0.02, 0.19, 0.19],
       [0.28, 0.28, 0.36, 0.  , 0.05, 0.28, 0.29],
       [0.48, 0.62, 0.66, 0.71, 0.04, 0.48, 0.48],
       [0.  , 0.03, 0.04, 0.  , 0.01, 0.  , 0.01],
       [0.3 , 0.54, 0.63, 0.33, 0.05, 0.3 , 0.3 ],
       [0.49, 0.42, 0.43, 0.54, 0.03, 0.49, 0.47],
       [0.47, 0.36, 0.46, 0.  , 0.07, 0.47, 0.49],
       [0.42, 0.69, 0.76, 0.62, 0.05, 0.42, 0.42],
       [0.3 , 0.79, 0.92, 0.53,

In [ ]:
!pip install pulp
import pulp
!apt-get install -y -qq glpk-utils

from pulp import GLPK
import pandas as pd # Library to handle data
import numpy as np
from statistics import mean

data = pd.read_csv("/content/DEA Model 1_Strikers.csv", encoding = 'unicode_escape', engine ='python')
#creating a list to store the optimal decision variables
weights_matrix = np.empty((7,52))
for k in range(52):  # Where k represents the number of observations
    model = pulp.LpProblem("DEA Model 1 for Strikers (Dribbling and Ball Carrying)", pulp.LpMaximize) # Create an LP maximization problem. We have 1 input, 6 outputs for goal scoring
    m1 = pulp.LpVariable("m1", lowBound=0.00000000001, upBound=None, cat='Continuous') # Create a variable m1>=0 , where m is denotes my inputs. In DEA model 1, there is just 1 input - playing time
    n1 = pulp.LpVariable("n1", lowBound=0.00000000001, upBound=None, cat='Continuous') # Create a variable n1>=0, where n1 represents the weight associated with output 1 - with goal scoring, it will be goals scored
    n2 = pulp.LpVariable("n2", lowBound=0.00000000001, upBound=None, cat='Continuous') # Create a variable n2>=0  , simmilar to above
    n3 = pulp.LpVariable("n3", lowBound=0.00000000001, upBound=None, cat='Continuous') # Create a variable n3>=0
    n4 = pulp.LpVariable("n4", lowBound=0.00000000001, upBound=None, cat='Continuous') # Create a variable n4>=0
    n5 = pulp.LpVariable("n5", lowBound=0.00000000001, upBound=None, cat='Continuous') # Create a variable n5>=0
    n6 = pulp.LpVariable("n6", lowBound=0.00000000001, upBound=None, cat='Continuous') # Create a variable n6>=0
   
    model += n1*data["Dribbles Succ"][k] + n2*data["SCA Drib"][k] + n3*data["GCA Drib"][k]+ n4*data["Carry PrgDist"][k] + n5*data["Carries Final Third"][k] + n6*data["Carry into box"][k]    #objective function
    
    model += m1*data["Minutes Played"][k] == 1 #first constraint (equality)

    for i in range(52): #NUMBER OF STRIKERS
        model += n1*data["Dribbles Succ"][i] + n2*data["SCA Drib"][i] + n3*data["GCA Drib"][i] + n4*data["Carry PrgDist"][i] + n5*data["Carries Final Third"][i] + n6*data["Carry into box"][i] - m1*data["Minutes Played"][i] <= 0
   
    status = model.solve(GLPK(msg=True, options=['--ranges', 'sensitivity.txt'])) 
    
    #ADD IN RELATIVE WEIGHT RESTRICTIONS 
    model += n3 >= n1  
    model += n3 >= n4   
    model += n3 >= n5  
    model += n3 >= n6   
    model += n2 >= n1   
    model += n2 >= n4   
    model += n2 >= n5  
    model += n2 >= n6   
        
    # Displaying Optimal Value of Objective Function	
    print(pulp.value(model.objective))
	
	

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
1.0
0.9528314
0.6586879999999999
1.000002
0.7173240580000001
0.1672728
0.1926457
0.6110816
0.36288408
0.27914522
0.16476505
0.40562706
0.48375797
0.79946812
0.066402
0.62689278
0.71240096
0.58704272
0.7728025000000001
0.9999984
0.374802
0.5765954120000001
0.5528660200000001
0.54807679
0.8321460300000001
0.8833560899999999
0.887910415
0.9999987100000001
0.9198518600000001
0.24756866
0.22984754000000002
0.3118338
0.1413552
0.52731824
0.602803488
0.7941296
0.2669844
0.5827472
0.63575403
0.44777536
0.8459079199999999
0.9356152799999999
0.1810185
0.48120911999999993
0.20827980000000001
1.0000002
0.5296936
0.1861168
0.3052478
1.0
0.6752226
0.218456


4) Defending for Strikers

In [ ]:
!pip install pulp
import pulp
!apt-get install -y -qq glpk-utils

from pulp import GLPK
import pandas as pd # Library to handle data
import numpy as np
from statistics import mean

data = pd.read_csv("/content/DEA Model 1_Strikers.csv", encoding = 'unicode_escape', engine ='python')
#creating a list to store the optimal decision variables
weights_matrix = np.empty((5,52))
for k in range(52):  # Where k represents the number of observations
    model = pulp.LpProblem("DEA Model 1 for Strikers (Defending)", pulp.LpMaximize) # Create an LP maximization problem. We have 1 input, 6 outputs for goal scoring
    n1 = pulp.LpVariable("n1", lowBound=0.000000001, upBound=None, cat='Continuous') # Create a variable n1>=0, where n1 represents the weight associated with output 1 - with goal scoring, it will be goals scored
    n2 = pulp.LpVariable("n2", lowBound=0.000000001, upBound=None, cat='Continuous') # Create a variable n2>=0  , simmilar to above
    n3 = pulp.LpVariable("n3", lowBound=0.000000001, upBound=None, cat='Continuous') # Create a variable n3>=0
    n4 = pulp.LpVariable("n4", lowBound=0.000000001, upBound=None, cat='Continuous') # Create a variable n4>=0
    m1 = pulp.LpVariable("m1", lowBound=0.000000001, upBound=None, cat='Continuous') # Create a variable m1>=0 , where m is denotes my inputs. In DEA model 1, there is just 1 input - playing time
   
    model += n1*data["Tackles TklW"][k] + n2*data["Pressures Succ"][k] + n3*data["Blocks and Interceptions"][k]+ n4*data["Recoveries"][k] #objective function
    
    model += m1*data["Minutes Played"][k] == 1 #first constraint (equality)

    for i in range(52): #NUMBER OF STRIKERS
        model += n1*data["Tackles TklW"][i] + n2*data["Pressures Succ"][i] + n3*data["Blocks and Interceptions"][i] + n4*data["Recoveries"][i] - m1*data["Minutes Played"][i] <= 0
   
    status = model.solve(GLPK(msg=True, options=['--ranges', 'sensitivity.txt'])) 
    
    #ADD IN RELATIVE WEIGHT RESTRICTIONS AND CONDITION FOR WEIGHTS TO BE POSITIVE.
    model += n3*data["Blocks and Interceptions"][k] >= n2*data["Pressures Succ"][k]   #Goals > SoT
        
     # Displaying Optimal Decision Variables & Reduced Cost per Variable
    list_weights=[]
    for v in model.variables():
	      print(v.name, "=", v.varValue, "\tReduced Cost =", v.dj)
    for v in model.variables():  
        list_weights=list_weights+[v.varValue]
    for n in range(4):
        value= list_weights[n]
        weights_matrix[n,k] = value

    # Displaying Optimal Value of Objective Function	
    print("Objective=", pulp.value(model.objective))
	
    # Displaying Shadow Price & Slack Value per Constraint
    print ("\nSensitivity Analysis\nConstraint\t\tShadow Price\tSlack")
    for name, c in model.constraints.items():
	      print(name, ":", c, "\t", c.pi, "\t\t", c.slack)
	
	

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
m1 = 0.00108696 	Reduced Cost = None
n1 = 0.0036004 	Reduced Cost = None
n2 = 0.0 	Reduced Cost = None
n3 = 0.0 	Reduced Cost = None
n4 = 0.0138228 	Reduced Cost = None
Objective= 0.9999996

Sensitivity Analysis
Constraint		Shadow Price	Slack
_C1 : 920.0*m1 = 1.0 	 None 		 None
_C2 : -920.0*m1 + 9.0*n1 + 34.0*n2 + 25.0*n3 + 70.0*n4 <= -0.0 	 None 		 None
_C3 : -1112.0*m1 + 10.0*n1 + 75.0*n2 + 20.0*n3 + 76.0*n4 <= -0.0 	 None 		 None
_C4 : -1459.0*m1 + 9.0*n1 + 54.0*n2 + 23.0*n3 + 71.0*n4 <= -0.0 	 None 		 None
_C5 : -3082.0*m1 + 12.0*n1 + 99.0*n2 + 45.0*n3 + 155.0*n4 <= -0.0 	 None 		 None
_C6 : -3078.0*m1 + 13.0*n1 + 153.0*n2 + 23.0*n3 + 191.0*n4 <= -0.0 	 None 		 None
_C7 : -1375.0*m1 + 11.0*n1 + 59.0*n2 + 16.0*n3 + 73.0*n4 <= -0.0 	 None 		 None
_C8 : -1923.0*m1 + 19.0*n1 + 107.0*n2 + 31.0*n3 + 99.0*n4 <= -0.0 	 None 		 None
_C9 : -1613.0*m1 + 10.0*n1 + 52.0*n2 + 21.0*n3 + 81.0*n4 <= -

In [ ]:
efficiency_table =np.empty((52,5))
average_list =[]
for row in range(52):
    row_values=[]
    for column in range(5):
       value = ((weights_matrix[1,column]*data["Tackles TklW"][row])+(weights_matrix[2,column]*data["Pressures Succ"][row])+(weights_matrix[3,column]*data["Blocks and Interceptions"][row])+(weights_matrix[4,column]*data["Recoveries"][row]))/((weights_matrix[0,column]*data["Minutes Played"][row]))
       efficiency_table[row,column]=value
       row_values=row_values+[value]
    average =mean(row_values)
    average_list =average_list+[average]

    average_list_rounded = [ '%.2f' % elem for elem in average_list ]

    player_list = ['Aaron Connolly', 'Adama TraorÃ©', 'Aleksandar MitroviÄ‡', 'Alexandre Lacazette', 'Anthony Martial', 'Anwar El Ghazi', 'Ashley Barnes', 'Bertrand TraorÃ©', 'Billy Sharp', 'Callum Wilson', 'Che Adams', 'Chris Wood', 'Christian Benteke', 'Daniel James', 'Danny Ings', 'Danny Welbeck', 'Diogo Jota', 'Dominic Calvert-Lewin', 'Edinson Cavani', 'FÃ¡bio Silva', 'Gabriel Jesus', 'Gareth Bale', 'Harry Kane', 'Jamie Vardy', 'Kelechi Iheanacho', 'Marcus Rashford', 'Mason Greenwood', 'MatÄ›j Vydra', 'Mbaye Diagne', 'Michail Antonio', 'Michy Batshuayi', 'Mohamed Salah', 'Oliver Burke', 'Oliver McBurnie', 'Olivier Giroud', 'Ollie Watkins', 'Patrick Bamford', 'Pierre-Emerick Aubameyang', 'RaÃºl JimÃ©nez', 'Raheem Sterling', 'Rhian Brewster', 'Richarlison', 'Riyad Mahrez', 'Roberto Firmino', 'SÃ©bastien Haller', 'Sadio ManÃ©', 'Son Heung-min', 'Tammy Abraham', 'Timo Werner', 'TrÃ©zÃ©guet', 'Wilfried Zaha', 'Willian JosÃ©']
for player in player_list:
    index = player_list.index(player)
    print(average_list_rounded[index])

display(efficiency_table)
efficiency_table = efficiency_table.round(decimals=2)
display(efficiency_table)

0.19
0.31
0.17
0.14
0.22
0.21
0.26
0.16
0.15
0.15
0.16
0.25
0.19
0.20
0.21
0.20
0.12
0.15
0.13
0.15
0.15
0.23
0.23
0.15
0.27
0.25
0.19
0.16
0.12
0.18
0.21
0.23
0.20
0.28
0.24
0.14
0.22
0.12
0.13
0.23
0.24
0.20
0.15
0.23
0.17
0.25
0.30
0.21
0.12
0.20
0.27
0.25


array([[0.0324035 , 0.64037475, 0.03371321, 0.03371311, 0.20961814],
       [0.02978739, 1.00000153, 0.06152696, 0.06152678, 0.38255533],
       [0.02043264, 0.57224812, 0.0337635 , 0.0337634 , 0.20993084],
       [0.01289691, 0.46885022, 0.02930296, 0.02930288, 0.18219663],
       [0.01398981, 0.6912283 , 0.04534525, 0.04534512, 0.28194253],
       [0.02649886, 0.6795838 , 0.03914338, 0.03914326, 0.24338124],
       [0.0327274 , 0.87185125, 0.05075905, 0.0507589 , 0.31560384],
       [0.02053538, 0.5141796 , 0.02940884, 0.02940876, 0.18285496],
       [0.01641587, 0.48005219, 0.02863307, 0.02863299, 0.17803148],
       [0.01384475, 0.49474743, 0.03082106, 0.03082097, 0.19163566],
       [0.01273984, 0.52221805, 0.03333184, 0.03333174, 0.2072469 ],
       [0.01954834, 0.80533401, 0.05144434, 0.05144419, 0.31986475],
       [0.01589423, 0.62203725, 0.03939615, 0.03939603, 0.24495289],
       [0.01981622, 0.64546401, 0.03946182, 0.0394617 , 0.24536121],
       [0.01771314, 0.6767941 , 0.

array([[0.03, 0.64, 0.03, 0.03, 0.21],
       [0.03, 1.  , 0.06, 0.06, 0.38],
       [0.02, 0.57, 0.03, 0.03, 0.21],
       [0.01, 0.47, 0.03, 0.03, 0.18],
       [0.01, 0.69, 0.05, 0.05, 0.28],
       [0.03, 0.68, 0.04, 0.04, 0.24],
       [0.03, 0.87, 0.05, 0.05, 0.32],
       [0.02, 0.51, 0.03, 0.03, 0.18],
       [0.02, 0.48, 0.03, 0.03, 0.18],
       [0.01, 0.49, 0.03, 0.03, 0.19],
       [0.01, 0.52, 0.03, 0.03, 0.21],
       [0.02, 0.81, 0.05, 0.05, 0.32],
       [0.02, 0.62, 0.04, 0.04, 0.24],
       [0.02, 0.65, 0.04, 0.04, 0.25],
       [0.02, 0.68, 0.04, 0.04, 0.27],
       [0.02, 0.66, 0.04, 0.04, 0.26],
       [0.01, 0.4 , 0.03, 0.03, 0.16],
       [0.01, 0.48, 0.03, 0.03, 0.19],
       [0.02, 0.42, 0.02, 0.02, 0.15],
       [0.03, 0.52, 0.03, 0.03, 0.17],
       [0.01, 0.48, 0.03, 0.03, 0.19],
       [0.02, 0.74, 0.05, 0.05, 0.28],
       [0.02, 0.74, 0.05, 0.05, 0.29],
       [0.01, 0.48, 0.03, 0.03, 0.2 ],
       [0.04, 0.91, 0.05, 0.05, 0.32],
       [0.03, 0.83, 0.05,

In [ ]:
!pip install pulp
import pulp
!apt-get install -y -qq glpk-utils

from pulp import GLPK
import pandas as pd # Library to handle data
import numpy as np
from statistics import mean

data = pd.read_csv("/content/DEA Model 1_Strikers.csv", encoding = 'unicode_escape', engine ='python')
#creating a list to store the optimal decision variables
weights_matrix = np.empty((7,52))
for k in range(52):  # Where k represents the number of observations
    model = pulp.LpProblem("DEA Model 1 for Strikers (Defending)", pulp.LpMaximize) # Create an LP maximization problem. We have 1 input, 6 outputs for goal scoring
    n1 = pulp.LpVariable("n1", lowBound=0.0000000001, upBound=None, cat='Continuous') # Create a variable n1>=0, where n1 represents the weight associated with output 1 - with goal scoring, it will be goals scored
    n2 = pulp.LpVariable("n2", lowBound=0.0000000001, upBound=None, cat='Continuous') # Create a variable n2>=0  , simmilar to above
    n3 = pulp.LpVariable("n3", lowBound=0.0000000001, upBound=None, cat='Continuous') # Create a variable n3>=0
    n4 = pulp.LpVariable("n4", lowBound=0.0000000001, upBound=None, cat='Continuous') # Create a variable n4>=0
    m1 = pulp.LpVariable("m1", lowBound=0.0000000001, upBound=None, cat='Continuous') # Create a variable m1>=0 , where m is denotes my inputs. In DEA model 1, there is just 1 input - playing time
   
    model += n1*data["Tackles TklW"][k] + n2*data["Pressures Succ"][k] + n3*data["Blocks and Interceptions"][k]+ n4*data["Recoveries"][k] #objective function
    
    model += m1*data["Minutes Played"][k] == 1 #first constraint (equality)

    for i in range(52): #NUMBER OF STRIKERS
        model += n1*data["Tackles TklW"][i] + n2*data["Pressures Succ"][i] + n3*data["Blocks and Interceptions"][i] + n4*data["Recoveries"][i] - m1*data["Minutes Played"][i] <= 0
   
    status = model.solve(GLPK(msg=True, options=['--ranges', 'sensitivity.txt'])) 
    
    #ADD IN RELATIVE WEIGHT RESTRICTIONS AND CONDITION FOR WEIGHTS TO BE POSITIVE.
    model += n3*data["Blocks and Interceptions"][k] >= n2*data["Pressures Succ"][k]
    
    print(pulp.value(model.objective))
   

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
0.9999996
1.000002
0.65177803
0.66800066
0.84254447
0.72301426
0.8718503
0.66715264
0.581100635
0.55350679
0.61552252
0.8361264
0.6403068
0.7625178
0.72435825
0.7247540699999999
0.42180516
0.56060018
0.7187849599999999
0.82943574
0.52119907
0.73955158
0.79010918
0.56398171
0.90774576
0.82885991
0.69149745
0.6458158279999999
0.640710494
0.6504999600000001
0.6979477999999999
0.7678267
0.6645912
0.9991482
0.8724512499999999
0.862266744
0.7581209999999999
0.55906958
0.61943448
0.749768
0.8712371019999999
0.74193645
0.5602975299999999
0.76348935
0.751253708
0.8543455
1.0000008
0.7491257
0.6555648159999999
0.813503237
0.90643089
0.84537526


#Full Backs

In [ ]:
!pip install pulp
import pulp
!apt-get install -y -qq glpk-utils

from pulp import GLPK
import pandas as pd # Library to handle data
import numpy as np
from statistics import mean

data = pd.read_csv("/content/DEA1_FBs.csv", encoding = 'unicode_escape', engine ='python')
#creating a list to store the optimal decision variables
weights_matrix = np.empty((6,70))
for k in range(70):  # Where k represents the number of observations
    model = pulp.LpProblem("DEA Model 1 for Strikers (Goal-Scoring)", pulp.LpMaximize) # Create an LP maximization problem. We have 1 input, 6 outputs for goal scoring
    n1 = pulp.LpVariable("n1", lowBound=0.00001, upBound=None, cat='Continuous') # Create a variable n1>=0, where n1 represents the weight associated with output 1 - with goal scoring, it will be goals scored
    n2 = pulp.LpVariable("n2", lowBound=0.00001, upBound=None, cat='Continuous') # Create a variable n2>=0  , simmilar to above
    n3 = pulp.LpVariable("n3", lowBound=0.00001, upBound=None, cat='Continuous') # Create a variable n3>=0
    n4 = pulp.LpVariable("n4", lowBound=0.00001, upBound=None, cat='Continuous') # Create a variable n4>=0
    n5 = pulp.LpVariable("n5", lowBound=0.00001, upBound=None, cat='Continuous') # Create a variable n5>=0
    m1 = pulp.LpVariable("m1", lowBound=0.00001, upBound=None, cat='Continuous') # Create a variable m1>=0 , where m is denotes my inputs. In DEA model 1, there is just 1 input - playing time
    
   
    model += n1*data["Gls"][k] + n2*data["SoT"][k] + n3*data["G-xG"][k]+ n4*data["Big Chances Missed"][k] + n5*data["GCA"][k]  #objective function
    
    model += m1*data["Minutes Played"][k] == 1 #first constraint (equality)

    for i in range(70): #NUMBER OF STRIKERS
        model += n1*data["Gls"][i] + n2*data["SoT"][i] + n3*data["G-xG"][i] + n4*data["Big Chances Missed"][i] + n5*data["GCA"][i] -  m1*data["Minutes Played"][i] <= 0
   

    #ADD IN RELATIVE WEIGHT RESTRICTIONS AND CONDITION FOR WEIGHTS TO BE POSITIVE.
    model += n1*data["Gls"][i] >= n2*data["SoT"][i]  #Goals > SoT
    model += n1*data["Gls"][i] >= n3*data["G-xG"][i]  #Goals > G-Xg
    model += n1*data["Gls"][i] >= n4*data["Big Chances Missed"][i]  #Goals > Big Chances Missed
    model += n5*data["GCA"][i] >= n2*data["SoT"][i]  #GCA > Shots on Target
    model += n5*data["GCA"][i] >= n4*data["Big Chances Missed"][i]  #GCA > Big Chances Missed
    model += n5*data["GCA"][i] >= n3*data["G-xG"][i]  #GCA > Big Chances Missed
    
  
    status = model.solve(GLPK(msg=True, options=['--ranges', 'sensitivity.txt'])) 
    print("Model Status:{}".format(pulp.LpStatus[model.status])) 
 
    
     # Displaying Optimal Decision Variables & Reduced Cost per Variable
    list_weights=[]
    for v in model.variables():
	      print(v.name, "=", v.varValue, "\tReduced Cost =", v.dj)
    for v in model.variables():  
        list_weights=list_weights+[v.varValue]
    for n in range(5):
        value= list_weights[n]
        weights_matrix[n,k] = value
        
    # Displaying Optimal Value of Objective Function	
    print(pulp.value(model.objective))
	
    # Displaying Shadow Price & Slack Value per Constraint
    print ("\nSensitivity Analysis\nConstraint\t\tShadow Price\tSlack")
    for name, c in model.constraints.items():
	      print(name, ":", c, "\t", c.pi, "\t\t", c.slack)
   

Streaming output truncated to the last 5000 lines.
_C6 : -1404.0*m1 + n1 + 6.0*n2 + 0.4*n3 + 1.5*n4 + 2.0*n5 <= -0.0 	 None 		 None
_C7 : -969.0*m1 + n1 + 3.0*n2 + 0.7*n3 + 1.5*n4 + 3.0*n5 <= -0.0 	 None 		 None
_C8 : -839.0*m1 + n2 - 0.5*n3 + 1.5*n4 + n5 <= -0.0 	 None 		 None
_C9 : -569.0*m1 + n1 + 2.0*n2 + 0.7*n3 + 1.5*n4 + n5 <= -0.0 	 None 		 None
_C10 : -960.0*m1 + 2.0*n1 + 9.0*n2 + 0.3*n3 + 1.5*n4 + 2.0*n5 <= -0.0 	 None 		 None
_C11 : -1006.0*m1 + 2.0*n2 - 0.3*n3 + 1.5*n4 + 4.0*n5 <= -0.0 	 None 		 None
_C12 : -2373.0*m1 + n1 + 12.0*n2 - 0.6*n3 + 1.5*n4 + 5.0*n5 <= -0.0 	 None 		 None
_C13 : -690.0*m1 + n2 - 0.2*n3 + 1.5*n4 + 3.0*n5 <= -0.0 	 None 		 None
_C14 : -1350.0*m1 + n2 - 0.4*n3 + 1.5*n4 + 4.0*n5 <= -0.0 	 None 		 None
_C15 : -669.0*m1 + n1 + 2.0*n2 + 0.6*n3 + 1.5*n4 + n5 <= -0.0 	 None 		 None
_C16 : -2299.0*m1 + n1 + 3.0*n2 + 0.6*n3 + 1.5*n4 + 7.0*n5 <= -0.0 	 None 		 None
_C17 : -2286.0*m1 + 3.0*n1 + 10.0*n2 + 0.6*n3 + 1.5*n4 + 9.0*n5 <= -0.0 	 None 		 None
_C18 : -4

In [ ]:
!pip install pulp
import pulp
!apt-get install -y -qq glpk-utils

from pulp import GLPK
import pandas as pd # Library to handle data
import numpy as np
from statistics import mean

data = pd.read_csv("/content/DEA1_FBs.csv", encoding = 'unicode_escape', engine ='python')
#creating a list to store the optimal decision variables
weights_matrix = np.empty((6,70))
for k in range(70):  # Where k represents the number of observations
    model = pulp.LpProblem("DEA Model 1 for Strikers (Goal-Scoring)", pulp.LpMaximize) # Create an LP maximization problem. We have 1 input, 6 outputs for goal scoring
    n1 = pulp.LpVariable("n1", lowBound=0.00001, upBound=None, cat='Continuous') # Create a variable n1>=0, where n1 represents the weight associated with output 1 - with goal scoring, it will be goals scored
    n2 = pulp.LpVariable("n2", lowBound=0.00001, upBound=None, cat='Continuous') # Create a variable n2>=0  , simmilar to above
    n3 = pulp.LpVariable("n3", lowBound=0.00001, upBound=None, cat='Continuous') # Create a variable n3>=0
    n4 = pulp.LpVariable("n4", lowBound=0.00001, upBound=None, cat='Continuous') # Create a variable n4>=0
    n5 = pulp.LpVariable("n5", lowBound=0.00001, upBound=None, cat='Continuous') # Create a variable n5>=0
    m1 = pulp.LpVariable("m1", lowBound=0.00001, upBound=None, cat='Continuous') # Create a variable m1>=0 , where m is denotes my inputs. In DEA model 1, there is just 1 input - playing time
    
   
    model += n1*data["Gls"][k] + n2*data["SoT"][k] + n3*data["G-xG"][k]+ n4*data["Big Chances Missed"][k] + n5*data["GCA"][k]  #objective function
    
    model += m1*data["Minutes Played"][k] == 1 #first constraint (equality)

    for i in range(70): #NUMBER OF STRIKERS
        model += n1*data["Gls"][i] + n2*data["SoT"][i] + n3*data["G-xG"][i] + n4*data["Big Chances Missed"][i] + n5*data["GCA"][i] -  m1*data["Minutes Played"][i] <= 0
   

    #ADD IN RELATIVE WEIGHT RESTRICTIONS AND CONDITION FOR WEIGHTS TO BE POSITIVE.
    model += n1*data["Gls"][i] >= n2*data["SoT"][i]  #Goals > SoT
    model += n1*data["Gls"][i] >= n3*data["G-xG"][i]  #Goals > G-Xg
    model += n1*data["Gls"][i] >= n4*data["Big Chances Missed"][i]  #Goals > Big Chances Missed
    model += n5*data["GCA"][i] >= n2*data["SoT"][i]  #GCA > Shots on Target
    model += n5*data["GCA"][i] >= n4*data["Big Chances Missed"][i]  #GCA > Big Chances Missed
    model += n5*data["GCA"][i] >= n3*data["G-xG"][i]  #GCA > Big Chances Missed
    
  
    status = model.solve(GLPK(msg=True, options=['--ranges', 'sensitivity.txt']))  
    
        
    # Displaying Optimal Value of Objective Function	
    print(pulp.value(model.objective))
	
   

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
0.5869436
0.569979
0.37133049999999995
0.6033242
0.397771
0.7773812
0.264013
0.8138384
0.9227976
0.8807
0.4667865
0.963029
0.6562690000000001
0.6721112
0.674399
0.9477888999999999
1.4000000000000001e-05
0.9781084
0.299752
0.74221
0.8907479999999999
0.60082205
0.7896022
0.1589518
0.357255
0.9086772000000001
1.3000000000000001e-05
0.4192278
1.4000000000000001e-05
0.658209
0.524887
0.7678209999999999
0.19420059999999997
1.5000000000000002e-05
1.4000000000000001e-05
0.204927
0.776884
1.4000000000000001e-05
0.299131
0.193462
0.461967
1.000001
0.273798
0.3965842
0.9999986999999999
0.5076522
0.452048
0.9634800000000001
0.2739049
0.241153
0.404955
0.982004
0.4554411
0.686593
0.2463379
1.0000002000000001
2.4e-05
0.5861889
0.2557758
0.373971
0.42753779999999997
0.3699762
0.1963648
0.1867698
0.9180016999999999
0.9499937
0.260677
0.1825134
0.695851
0.24611839999999996


In [ ]:
from pulp import GLPK
import pandas as pd # Library to handle data
import numpy as np
from statistics import mean

data = pd.read_csv("/content/DEA1_FBs.csv", encoding = 'unicode_escape', engine ='python')
#creating a list to store the optimal decision variables
weights_matrix = np.empty((6,70))
for k in range(70):  # Where k represents the number of observations
    model = pulp.LpProblem("DEA Model 1 for Strikers (Creativity)", pulp.LpMaximize) # Create an LP maximization problem. We have 1 input, 6 outputs for goal scoring
    n1 = pulp.LpVariable("n1", lowBound=0.000001, upBound=None, cat='Continuous') # Create a variable n1>=0, where n1 represents the weight associated with output 1 - with goal scoring, it will be goals scored
    n2 = pulp.LpVariable("n2", lowBound=0.000001, upBound=None, cat='Continuous') # Create a variable n2>=0  , simmilar to above
    n3 = pulp.LpVariable("n3", lowBound=0.000001, upBound=None, cat='Continuous') # Create a variable n3>=0
    n4 = pulp.LpVariable("n4", lowBound=0.000001, upBound=None, cat='Continuous') # Create a variable n4>=0
    m1 = pulp.LpVariable("m1", lowBound=0.000001, upBound=None, cat='Continuous') # Create a variable m1>=0 , where m is denotes my inputs. In DEA model 1, there is just 1 input - playing time

    model += n1*data["xA"][k] + n2*data["KP"][k] + n3*data["PPA"][k]+ n4*data["SCA"][k] #objective function
    
    model += m1*data["Minutes Played"][k] == 1 #first constraint (equality)

    for i in range(70): #NUMBER OF STRIKERS
        model += n1*data["xA"][i] + n2*data["KP"][i] + n3*data["PPA"][i] + n4*data["SCA"][i] - m1*data["Minutes Played"][i] <= 0
   
    status = model.solve(GLPK(msg=True, options=['--ranges', 'sensitivity.txt'])) 
    
    #ADD IN RELATIVE WEIGHT RESTRICTIONS AND CONDITION FOR WEIGHTS TO BE POSITIVE.
    model += n1 >= n3 #xA > PPA
    model += n2 >= n3  #KP > PPA
    model += n4 >= n3   #SCA > PPA
    model += n1 >= n2   #SCA > PPA


    # Displaying Optimal Value of Objective Function	
    print(pulp.value(model.objective))
	

0.56050396
0.7570134399999999
0.46487392000000005
0.344381988
0.51289812
0.34766944
0.9299662000000001
0.9018501000000001
0.8218894
0.7758963
0.756479645
0.7415168
0.7103393399999999
0.6790467
0.6673138999999999
0.5983588400000001
0.2898143
0.75960046
0.48721948000000004
0.47961905700000007
0.46131598000000007
0.450893202
0.444879865
0.3122589
0.431296
0.7536508000000001
0.184861
0.23620881000000002
0.23999900000000002
0.30459436
0.283287
0.24090259
0.4604671
0.23334688
0.29037561
0.603650447
0.565823785
0.10411917999999999
0.5065786
0.34070890000000004
0.47957690000000003
0.6518425000000001
0.1495078
0.42452827500000007
0.5228704980000001
0.6072544200000001
0.55127381
0.9006665
0.3092483
0.38251534
0.47908839999999997
0.79628236
0.572416991
0.49761566999999995
0.28391854
0.4320924
0.31117875
0.37965392
0.310853548
0.4390712
0.1754884
0.25988439999999996
0.16199316000000002
0.37393688
0.9999984
0.999999
0.352464335
0.42169632
0.5138681599999999
0.3334356


Dribbling and Ball Carrying

In [ ]:
!pip install pulp
import pulp
!apt-get install -y -qq glpk-utils

from pulp import GLPK
import pandas as pd # Library to handle data
import numpy as np
from statistics import mean

data = pd.read_csv("/content/DEA1_FBs.csv", encoding = 'unicode_escape', engine ='python')
#creating a list to store the optimal decision variables
weights_matrix = np.empty((6,70))
for k in range(70):  # Where k represents the number of observations
    model = pulp.LpProblem("DEA Model 1 for Strikers (Dribbling and Ball Carrying)", pulp.LpMaximize) # Create an LP maximization problem. We have 1 input, 6 outputs for goal scoring
    m1 = pulp.LpVariable("m1", lowBound=0.00000000001, upBound=None, cat='Continuous') # Create a variable m1>=0 , where m is denotes my inputs. In DEA model 1, there is just 1 input - playing time
    n2 = pulp.LpVariable("n2", lowBound=0.00000000001, upBound=None, cat='Continuous') # Create a variable n2>=0  , simmilar to above
    n3 = pulp.LpVariable("n3", lowBound=0.00000000001, upBound=None, cat='Continuous') # Create a variable n3>=0
    n4 = pulp.LpVariable("n4", lowBound=0.00000000001, upBound=None, cat='Continuous') # Create a variable n4>=0
    n5 = pulp.LpVariable("n5", lowBound=0.00000000001, upBound=None, cat='Continuous') # Create a variable n5>=0
    n6 = pulp.LpVariable("n6", lowBound=0.00000000001, upBound=None, cat='Continuous') # Create a variable n6>=0
   
    model += n2*data["SCA Drib"][k] + n3*data["GCA Drib"][k]+ n4*data["Carry PrgDist"][k] + n5*data["Carries Final Third"][k] + n6*data["Carry into box"][k]    #objective function
    
    model += m1*data["Minutes Played"][k] == 1 #first constraint (equality)

    for i in range(70): #NUMBER OF STRIKERS
        model += n2*data["SCA Drib"][i] + n3*data["GCA Drib"][i] + n4*data["Carry PrgDist"][i] + n5*data["Carries Final Third"][i] + n6*data["Carry into box"][i] - m1*data["Minutes Played"][i] <= 0
   
    status = model.solve(GLPK(msg=True, options=['--ranges', 'sensitivity.txt'])) 
    
    #ADD IN RELATIVE WEIGHT RESTRICTIONS AND CONDITION FOR WEIGHTS TO BE POSITIVE.
    model += n3 >= n1   #Goals > SoT
    model += n3 >= n4   #Goals > SoT(%)
    model += n3 >= n5   #Goals > G-Xg
    model += n3 >= n6   #Goals > Big Chances Missed
    model += n2 >= n1   #Goals > Shots on Target
    model += n2 >= n4   #Goals > SoT(%)
    model += n2 >= n5   #Goals > Shots on Target
    model += n2 >= n6   #Goals > SoT(%)
        
    # Displaying Optimal Value of Objective Function	
    print(pulp.value(model.objective))
	
	

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
0.70829531
0.92362084
0.822582143
0.98553577
0.9999990000000001
0.330822428
0.495662622
0.539530476
0.6842292750000001
0.9999989
0.7664999180000001
0.67945603
0.51196
0.7722156
1.0
0.861280666
0.544456092
0.39288617709999996
0.79320504
0.6287475619999999
0.6703636
0.7392892369999999
0.5584127680000001
0.49897445
0.521667802
0.43724386400000004
0.2962421
0.5367767820000001
0.429402413
0.790624869
0.333163138
0.858559
0.5344350320000001
0.393843632
0.7957388599999999
0.9757243
0.807821
0.43312284
0.518215392
0.321183264
0.499963405
1.0000003
0.282968269
0.394139237
0.7038146190000001
0.362052582
0.8364111350000001
1.00000003
0.5925712000000001
0.34621962400000006
0.701902548
1.0000010400000001
0.3121783621
0.5962030020000001
0.292299
0.9999979999999999
0.477969
0.768384258
0.46430838999999996
0.527027019
0.226823696
0.307434223
0.3308688
0.4822432
1.0000031999999999
0.901237234
1.000000666


Defending

In [ ]:
!pip install pulp
import pulp
!apt-get install -y -qq glpk-utils

from pulp import GLPK
import pandas as pd # Library to handle data
import numpy as np
from statistics import mean

data = pd.read_csv("/content/DEA1_FBs.csv", encoding = 'unicode_escape', engine ='python')
#creating a list to store the optimal decision variables
weights_matrix = np.empty((5,70))
for k in range(70):  # Where k represents the number of observations
    model = pulp.LpProblem("DEA Model 1 for Strikers (Defending)", pulp.LpMaximize) # Create an LP maximization problem. We have 1 input, 6 outputs for goal scoring
    n1 = pulp.LpVariable("n1", lowBound=0.000000001, upBound=None, cat='Continuous') # Create a variable n1>=0, where n1 represents the weight associated with output 1 - with goal scoring, it will be goals scored
    n2 = pulp.LpVariable("n2", lowBound=0.000000001, upBound=None, cat='Continuous') # Create a variable n2>=0  , simmilar to above
    n3 = pulp.LpVariable("n3", lowBound=0.000000001, upBound=None, cat='Continuous') # Create a variable n3>=0
    n4 = pulp.LpVariable("n4", lowBound=0.000000001, upBound=None, cat='Continuous') # Create a variable n4>=0
    m1 = pulp.LpVariable("m1", lowBound=0.000000001, upBound=None, cat='Continuous') # Create a variable m1>=0 , where m is denotes my inputs. In DEA model 1, there is just 1 input - playing time
   
    model += n1*data["Tackles TklW"][k] + n2*data["Pressures Succ"][k] + n3*data["Blocks and Interceptions"][k]+ n4*data["Recoveries"][k] #objective function
    
    model += m1*data["Minutes Played"][k] == 1 #first constraint (equality)

    for i in range(70): #NUMBER OF STRIKERS
        model += n1*data["Tackles TklW"][i] + n2*data["Pressures Succ"][i] + n3*data["Blocks and Interceptions"][i] + n4*data["Recoveries"][i] - m1*data["Minutes Played"][i] <= 0
   
    status = model.solve(GLPK(msg=True, options=['--ranges', 'sensitivity.txt'])) 
    
    #ADD IN RELATIVE WEIGHT RESTRICTIONS AND CONDITION FOR WEIGHTS TO BE POSITIVE.
    model += n3*data["Blocks and Interceptions"][k] >= n2*data["Pressures Succ"][k]   #Goals > SoT
      

    # Displaying Optimal Value of Objective Function	
    print(pulp.value(model.objective))

	
	

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
0.95897392
0.99703276
0.84592799
0.80541538
0.7981108800000001
0.92903697
0.9999997500000001
0.8501148000000001
0.7865673
0.8824589300000001
0.844596856
0.7297976799999999
0.74238654
0.98107707
0.77104129
0.83506386
0.76680109
0.807977458
0.8664459820000001
0.833614203
0.80835196
0.9999996099999999
0.8766288200000001
0.67938041
0.88723716
0.889501585
0.8621612200000001
0.8034808999999999
0.83378776
0.6357534199999999
0.97635024
0.8755634699999999
1.00000007
0.81051085
0.91842522
0.90810177
0.88635263
0.96058932
0.93044739
0.73657559
1.0000032
0.8095798
0.84338285
0.78881045
0.94914892
0.8889920050000001
0.9999993
0.96025692
0.8768333500000001
0.74147265
0.9323278439999999
0.9350964
0.88277652
0.8397097099999999
0.695248689
0.75151989
1.0000004
0.9213367399999999
0.75593686
0.8525910400000001
0.9318345100000001
0.80462612
0.91376171
1.000000132
0.8863297800000001
0.9252064440000001
0.99999

**Attacking Midfielders**

Goal Scoring

In [ ]:
!pip install pulp
import pulp
!apt-get install -y -qq glpk-utils

from pulp import GLPK
import pandas as pd # Library to handle data
import numpy as np
from statistics import mean

data = pd.read_csv("/content/DEA1_AMs.csv", encoding = 'unicode_escape', engine ='python')
#creating a list to store the optimal decision variables
weights_matrix = np.empty((6,65))
for k in range(65):  # Where k represents the number of observations
    model = pulp.LpProblem("DEA Model 1 for Strikers (Goal-Scoring)", pulp.LpMaximize) # Create an LP maximization problem. We have 1 input, 6 outputs for goal scoring
    n1 = pulp.LpVariable("n1", lowBound=0.00001, upBound=None, cat='Continuous') # Create a variable n1>=0, where n1 represents the weight associated with output 1 - with goal scoring, it will be goals scored
    n2 = pulp.LpVariable("n2", lowBound=0.00001, upBound=None, cat='Continuous') # Create a variable n2>=0  , simmilar to above
    n3 = pulp.LpVariable("n3", lowBound=0.00001, upBound=None, cat='Continuous') # Create a variable n3>=0
    n4 = pulp.LpVariable("n4", lowBound=0.00001, upBound=None, cat='Continuous') # Create a variable n4>=0
    n5 = pulp.LpVariable("n5", lowBound=0.00001, upBound=None, cat='Continuous') # Create a variable n5>=0
    m1 = pulp.LpVariable("m1", lowBound=0.00001, upBound=None, cat='Continuous') # Create a variable m1>=0 , where m is denotes my inputs. In DEA model 1, there is just 1 input - playing time
    
   
    model += n1*data["Gls"][k] + n2*data["SoT"][k] + n3*data["G-xG"][k]+ n4*data["Big Chances Missed"][k] + n5*data["GCA"][k]  #objective function
    
    model += m1*data["Minutes Played"][k] == 1 #first constraint (equality)

    for i in range(65): #NUMBER OF STRIKERS
        model += n1*data["Gls"][i] + n2*data["SoT"][i] + n3*data["G-xG"][i] + n4*data["Big Chances Missed"][i] + n5*data["GCA"][i] -  m1*data["Minutes Played"][i] <= 0
   

    #ADD IN RELATIVE WEIGHT RESTRICTIONS AND CONDITION FOR WEIGHTS TO BE POSITIVE.
    model += n1*data["Gls"][i] >= n2*data["SoT"][i]  #Goals > SoT
    model += n1*data["Gls"][i] >= n3*data["G-xG"][i]  #Goals > G-Xg
    model += n1*data["Gls"][i] >= n4*data["Big Chances Missed"][i]  #Goals > Big Chances Missed
    model += n5*data["GCA"][i] >= n2*data["SoT"][i]  #GCA > Shots on Target
    model += n5*data["GCA"][i] >= n4*data["Big Chances Missed"][i]  #GCA > Big Chances Missed
    model += n5*data["GCA"][i] >= n3*data["G-xG"][i]  #GCA > Big Chances Missed
    
  
    status = model.solve(GLPK(msg=True, options=['--ranges', 'sensitivity.txt']))  
    
        
    # Displaying Optimal Value of Objective Function	
    print(pulp.value(model.objective))

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
0.63017795
0.7055756
0.9999994999999999
1.0000009
0.517515
0.5166736094
0.7040513399999998
0.8382473699999999
0.522009382
0.475298304
0.5064462
1.00000015
0.4384048575
0.421192055
0.4968856025
0.5370813392
0.66157044
0.4925553
0.5754935791
0.502175628
0.6781279509000001
0.43967409999999996
0.52030331
0.19987564000000002
0.2312649
0.9912038699999999
0.6569712
0.32100525
0.31032893
0.34769758
0.38146119999999994
0.9999989000000001
0.34581594
0.6412919
0.24553518000000002
0.6442012
0.504342
0.72981109
0.5061403210000001
0.30723588
0.33008557299999997
0.7963162
0.438777
0.60711172
0.7151989999999999
0.77234995
0.7058035500000001
0.830820995
0.69909018
0.549257
0.50126181
0.27783018
0.6405750000000001
0.7954854
0.9999987
0.27102914
1.0000010199999998
0.5928982781
0.50311502474
0.18253639999999996
0.999999962
0.9382585
0.260978275
0.3202758
0.18784595


In [ ]:
from pulp import GLPK
import pandas as pd # Library to handle data
import numpy as np
from statistics import mean

data = pd.read_csv("/content/DEA1_AMs.csv", encoding = 'unicode_escape', engine ='python')
#creating a list to store the optimal decision variables
weights_matrix = np.empty((6,65))
for k in range(65):  # Where k represents the number of observations
    model = pulp.LpProblem("DEA Model 1 for Strikers (Creativity)", pulp.LpMaximize) # Create an LP maximization problem. We have 1 input, 6 outputs for goal scoring
    n1 = pulp.LpVariable("n1", lowBound=0.000001, upBound=None, cat='Continuous') # Create a variable n1>=0, where n1 represents the weight associated with output 1 - with goal scoring, it will be goals scored
    n2 = pulp.LpVariable("n2", lowBound=0.000001, upBound=None, cat='Continuous') # Create a variable n2>=0  , simmilar to above
    n3 = pulp.LpVariable("n3", lowBound=0.000001, upBound=None, cat='Continuous') # Create a variable n3>=0
    n4 = pulp.LpVariable("n4", lowBound=0.000001, upBound=None, cat='Continuous') # Create a variable n4>=0
    m1 = pulp.LpVariable("m1", lowBound=0.000001, upBound=None, cat='Continuous') # Create a variable m1>=0 , where m is denotes my inputs. In DEA model 1, there is just 1 input - playing time

    model += n1*data["xA"][k] + n2*data["KP"][k] + n3*data["PPA"][k]+ n4*data["SCA"][k] #objective function
    
    model += m1*data["Minutes Played"][k] == 1 #first constraint (equality)

    for i in range(65): #NUMBER OF STRIKERS
        model += n1*data["xA"][i] + n2*data["KP"][i] + n3*data["PPA"][i] + n4*data["SCA"][i] - m1*data["Minutes Played"][i] <= 0
   
    status = model.solve(GLPK(msg=True, options=['--ranges', 'sensitivity.txt'])) 
    
    #ADD IN RELATIVE WEIGHT RESTRICTIONS AND CONDITION FOR WEIGHTS TO BE POSITIVE.
    model += n1 >= n3 #xA > PPA
    model += n2 >= n3  #KP > PPA
    model += n4 >= n3   #SCA > PPA
    model += n1 >= n2   #SCA > PPA


    # Displaying Optimal Value of Objective Function	
    print(pulp.value(model.objective))

0.6205736199999999
0.5545028
0.7737341799999999
1.00000064
0.42812094
0.53979592
0.49164129999999995
0.6410515400000001
0.56240219
0.58091954
0.3841674
0.5830559
0.5887186
0.61214477
0.5100362
0.79315732
0.6012441000000001
0.4990153
0.27020009
0.5448013
0.5498831000000001
0.21757400000000002
0.64192657
0.37335929999999995
0.9999988
0.6987768
0.56208164
0.44139266
0.46931336
0.26558999999999994
0.358655
0.60367793
0.22140522
0.5903877200000001
0.4091393
0.8399506999999999
0.5774737
0.49693190000000004
0.4212984
0.37896928999999996
0.42294342
0.6001335000000001
0.6809700999999999
0.35880038000000003
0.7154128
0.5099569
0.6820497000000001
0.6161922999999999
0.7034715500000001
1.000001
0.51644933
0.43441912999999993
0.5793403
0.8337210399999999
0.49732039999999994
0.3145075
0.57197374
0.43483648
0.38819949
0.44991739999999997
0.9654361
0.3219807
0.3647386
0.39683938
0.2277362


In [ ]:
!pip install pulp
import pulp
!apt-get install -y -qq glpk-utils

from pulp import GLPK
import pandas as pd # Library to handle data
import numpy as np
from statistics import mean

data = pd.read_csv("/content/DEA1_AMs.csv", encoding = 'unicode_escape', engine ='python')
#creating a list to store the optimal decision variables
weights_matrix = np.empty((6,65))
for k in range(65):  # Where k represents the number of observations
    model = pulp.LpProblem("DEA Model 1 for Strikers (Dribbling and Ball Carrying)", pulp.LpMaximize) # Create an LP maximization problem. We have 1 input, 6 outputs for goal scoring
    m1 = pulp.LpVariable("m1", lowBound=0.00000000001, upBound=None, cat='Continuous') # Create a variable m1>=0 , where m is denotes my inputs. In DEA model 1, there is just 1 input - playing time
    n2 = pulp.LpVariable("n2", lowBound=0.00000000001, upBound=None, cat='Continuous') # Create a variable n2>=0  , simmilar to above
    n3 = pulp.LpVariable("n3", lowBound=0.00000000001, upBound=None, cat='Continuous') # Create a variable n3>=0
    n4 = pulp.LpVariable("n4", lowBound=0.00000000001, upBound=None, cat='Continuous') # Create a variable n4>=0
    n5 = pulp.LpVariable("n5", lowBound=0.00000000001, upBound=None, cat='Continuous') # Create a variable n5>=0
    n6 = pulp.LpVariable("n6", lowBound=0.00000000001, upBound=None, cat='Continuous') # Create a variable n6>=0
   
    model += n2*data["SCA Drib"][k] + n3*data["GCA Drib"][k]+ n4*data["Carry PrgDist"][k] + n5*data["Carries Final Third"][k] + n6*data["Carry into box"][k]    #objective function
    
    model += m1*data["Minutes Played"][k] == 1 #first constraint (equality)

    for i in range(65): #NUMBER OF STRIKERS
        model += n2*data["SCA Drib"][i] + n3*data["GCA Drib"][i] + n4*data["Carry PrgDist"][i] + n5*data["Carries Final Third"][i] + n6*data["Carry into box"][i] - m1*data["Minutes Played"][i] <= 0
   
    status = model.solve(GLPK(msg=True, options=['--ranges', 'sensitivity.txt'])) 
    
    #ADD IN RELATIVE WEIGHT RESTRICTIONS AND CONDITION FOR WEIGHTS TO BE POSITIVE.
    model += n3 >= n1   #Goals > SoT
    model += n3 >= n4   #Goals > SoT(%)
    model += n3 >= n5   #Goals > G-Xg
    model += n3 >= n6   #Goals > Big Chances Missed
    model += n2 >= n1   #Goals > Shots on Target
    model += n2 >= n4   #Goals > SoT(%)
    model += n2 >= n5   #Goals > Shots on Target
    model += n2 >= n6   #Goals > SoT(%)
        
    # Displaying Optimal Value of Objective Function	
    print(pulp.value(model.objective))
	

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
0.6698414
1.00000076
0.5060801530000001
1.000000365
0.40479981
0.6237053600000001
0.9999998999999999
0.8719113
0.69947646
0.538383884
0.39195522499999996
0.9342391000000001
0.6597535693
0.9204779000000001
0.65656845
0.78160964
0.58062274
0.4791024
0.413979186
0.9018603
0.9999996
0.31210762000000003
0.7326876
0.414217702
0.6122835
0.7132757
0.4423103399
0.6462882799999999
0.7510112
0.38393243
0.5296883
0.6601214
0.398287596
0.44907590799999997
0.28541349099999996
0.476662667
0.6726525
0.555202441
0.47045374
0.519428472
0.71175753
0.5902285139999999
0.29782995
0.5526150000000001
1.0000008999999999
0.7250012
0.500259942
0.43822437000000003
0.5414268959999999
0.30100305
1.0
0.44166775999999996
0.57416656
0.9999982
0.5166538
0.322334449
0.49640808000000003
0.60229065
0.373328226
0.374110085
1.0
0.8067341
0.5536483808
0.5440697
0.400665699


In [ ]:
!pip install pulp
import pulp
!apt-get install -y -qq glpk-utils

from pulp import GLPK
import pandas as pd # Library to handle data
import numpy as np
from statistics import mean

data = pd.read_csv("/content/DEA1_AMs.csv", encoding = 'unicode_escape', engine ='python')
#creating a list to store the optimal decision variables
weights_matrix = np.empty((5,65))
for k in range(65):  # Where k represents the number of observations
    model = pulp.LpProblem("DEA Model 1 for Strikers (Defending)", pulp.LpMaximize) # Create an LP maximization problem. We have 1 input, 6 outputs for goal scoring
    n1 = pulp.LpVariable("n1", lowBound=0.000000001, upBound=None, cat='Continuous') # Create a variable n1>=0, where n1 represents the weight associated with output 1 - with goal scoring, it will be goals scored
    n2 = pulp.LpVariable("n2", lowBound=0.000000001, upBound=None, cat='Continuous') # Create a variable n2>=0  , simmilar to above
    n3 = pulp.LpVariable("n3", lowBound=0.000000001, upBound=None, cat='Continuous') # Create a variable n3>=0
    n4 = pulp.LpVariable("n4", lowBound=0.000000001, upBound=None, cat='Continuous') # Create a variable n4>=0
    m1 = pulp.LpVariable("m1", lowBound=0.000000001, upBound=None, cat='Continuous') # Create a variable m1>=0 , where m is denotes my inputs. In DEA model 1, there is just 1 input - playing time
   
    model += n1*data["Tackles TklW"][k] + n2*data["Pressures Succ"][k] + n3*data["Blocks and Interceptions"][k]+ n4*data["Recoveries"][k] #objective function
    
    model += m1*data["Minutes Played"][k] == 1 #first constraint (equality)

    for i in range(65): #NUMBER OF STRIKERS
        model += n1*data["Tackles TklW"][i] + n2*data["Pressures Succ"][i] + n3*data["Blocks and Interceptions"][i] + n4*data["Recoveries"][i] - m1*data["Minutes Played"][i] <= 0
   
    status = model.solve(GLPK(msg=True, options=['--ranges', 'sensitivity.txt'])) 
    
    #ADD IN RELATIVE WEIGHT RESTRICTIONS AND CONDITION FOR WEIGHTS TO BE POSITIVE.
    model += n3*data["Blocks and Interceptions"][k] >= n2*data["Pressures Succ"][k]   #Goals > SoT
      

    # Displaying Optimal Value of Objective Function	
    print(pulp.value(model.objective))

	
	

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
0.5953604
0.42661314000000006
0.695118261
0.71508456
0.6047288799999999
0.643259582
0.57369205
0.52273764
0.66790953
0.67598551
0.60439016
0.577351226
0.661831078
0.53715355
0.8827846799999999
0.7835604
0.7829610300000001
1.0000004999999998
0.6601359299999999
0.60989267
0.53474292
0.78004899
0.6880673
0.8176409600000001
0.7300749
0.6848324100000001
0.67165372
0.9999996699999999
0.6935437710000001
0.66756784
0.797407666
0.56868205
0.803908443
0.95067924
0.8471640600000001
0.69938765
0.94467618
1.00000153
0.62807064
0.95425593
0.69075121
0.569226438
0.48611476
0.7991729
0.94471268
0.72632436
0.5898141600000001
0.64631423
0.63235038
0.92197073
0.58029682
0.88249065
1.0000028
0.65820713
0.45566416
1.000002
0.568780779
0.639609863
0.7932837119999999
0.6324797600000001
0.75508192
0.62060828
0.68737717
0.6487929200000001
0.8081868999999999


# **CMs and CDMs**

In [ ]:
!pip install pulp
import pulp
!apt-get install -y -qq glpk-utils

from pulp import GLPK
import pandas as pd # Library to handle data
import numpy as np
from statistics import mean

data = pd.read_csv("/content/CM and CDMs.csv", encoding = 'unicode_escape', engine ='python')
#creating a list to store the optimal decision variables
weights_matrix = np.empty((5,97))
for k in range(97):  # Where k represents the number of observations
    model = pulp.LpProblem("DEA Model 1 for Strikers (Goal-Scoring)", pulp.LpMaximize) # Create an LP maximization problem. We have 1 input, 6 outputs for goal scoring
    n1 = pulp.LpVariable("n1", lowBound=0.00001, upBound=None, cat='Continuous') # Create a variable n1>=0, where n1 represents the weight associated with output 1 - with goal scoring, it will be goals scored
    n2 = pulp.LpVariable("n2", lowBound=0.00001, upBound=None, cat='Continuous') # Create a variable n2>=0  , simmilar to above
    n3 = pulp.LpVariable("n3", lowBound=0.00001, upBound=None, cat='Continuous') # Create a variable n3>=0
    n5 = pulp.LpVariable("n5", lowBound=0.00001, upBound=None, cat='Continuous') # Create a variable n5>=0
    m1 = pulp.LpVariable("m1", lowBound=0.00001, upBound=None, cat='Continuous') # Create a variable m1>=0 , where m is denotes my inputs. In DEA model 1, there is just 1 input - playing time
    
   
    model += n1*data["Gls"][k] + n2*data["SoT"][k] + n3*data["G-xG"][k]+ n5*data["GCA"][k]  #objective function
    
    model += m1*data["Minutes Played"][k] == 1 #first constraint (equality)

    for i in range(97): #NUMBER OF STRIKERS
        model += n1*data["Gls"][i] + n2*data["SoT"][i] + n3*data["G-xG"][i] + n5*data["GCA"][i] -  m1*data["Minutes Played"][i] <= 0
   

    #ADD IN RELATIVE WEIGHT RESTRICTIONS AND CONDITION FOR WEIGHTS TO BE POSITIVE.
    model += n1*data["Gls"][i] >= n2*data["SoT"][i]  #Goals > SoT
    model += n1*data["Gls"][i] >= n3*data["G-xG"][i]  #Goals > G-Xg
    model += n5*data["GCA"][i] >= n2*data["SoT"][i]  #GCA > Shots on Target
    model += n5*data["GCA"][i] >= n3*data["G-xG"][i]  #GCA > Big Chances Missed
    
  
    status = model.solve(GLPK(msg=True, options=['--ranges', 'sensitivity.txt']))  
    
        
    # Displaying Optimal Value of Objective Function	
    print(pulp.value(model.objective))

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
0.841609
0.51938651
0.99999986
0.71047952
0.8506946000000001
0.4027535
0.521788
0.19636430000000002
0.93023476
0.94068625
0.39088639999999997
0.20298962
0.11016870000000001
0.17059420000000003
0.3414266
0.41678150999999997
0.66270255
0.34496
0.439495
0.55063248
0.999998
0.535135
0.20843544000000003
0.23625786
0.24931719999999996
0.387315
0.1587388
0.9456526
0.62791888
1.0000006000000001
0.4906426
0.5152082
0.5088472
0.4040122
0.5481214999999999
0.352613
0.303014
0.41161266
0.3956562
0.37144279999999996
0.22502830000000001
0.21435289999999999
0.2488244
0.231049
0.16435059999999999
0.529293
0.2286718
0.214719
0.229926
0.255937
0.626876
0.16779550000000001
0.11646319999999999
0.23361759999999998
0.1705766
0.320462
0.3863653
0.2031984
0.4782766
0.1055592
0.6098726299999999
0.6105977000000001
0.62746198
0.7322932
0.29491335
0.6178794
0.5903144
0.27685949
0.2625864
0.457203
0.20768664999999997


In [ ]:
from pulp import GLPK
import pandas as pd # Library to handle data
import numpy as np
from statistics import mean

data = pd.read_csv("/content/CM and CDMs.csv", encoding = 'unicode_escape', engine ='python')
#creating a list to store the optimal decision variables
weights_matrix = np.empty((6,97))
for k in range(97):  # Where k represents the number of observations
    model = pulp.LpProblem("DEA Model 1 for Strikers (Creativity)", pulp.LpMaximize) # Create an LP maximization problem. We have 1 input, 6 outputs for goal scoring
    n1 = pulp.LpVariable("n1", lowBound=0.000001, upBound=None, cat='Continuous') # Create a variable n1>=0, where n1 represents the weight associated with output 1 - with goal scoring, it will be goals scored
    n2 = pulp.LpVariable("n2", lowBound=0.000001, upBound=None, cat='Continuous') # Create a variable n2>=0  , simmilar to above
    n3 = pulp.LpVariable("n3", lowBound=0.000001, upBound=None, cat='Continuous') # Create a variable n3>=0
    n4 = pulp.LpVariable("n4", lowBound=0.000001, upBound=None, cat='Continuous') # Create a variable n4>=0
    m1 = pulp.LpVariable("m1", lowBound=0.000001, upBound=None, cat='Continuous') # Create a variable m1>=0 , where m is denotes my inputs. In DEA model 1, there is just 1 input - playing time

    model += n1*data["xA"][k] + n2*data["KP"][k] + n3*data["PPA"][k]+ n4*data["SCA"][k] #objective function
    
    model += m1*data["Minutes Played"][k] == 1 #first constraint (equality)

    for i in range(97): #NUMBER OF STRIKERS
        model += n1*data["xA"][i] + n2*data["KP"][i] + n3*data["PPA"][i] + n4*data["SCA"][i] - m1*data["Minutes Played"][i] <= 0
   
    status = model.solve(GLPK(msg=True, options=['--ranges', 'sensitivity.txt'])) 
    
    #ADD IN RELATIVE WEIGHT RESTRICTIONS AND CONDITION FOR WEIGHTS TO BE POSITIVE.
    model += n1 >= n3 #xA > PPA
    model += n2 >= n3  #KP > PPA
    model += n4 >= n3   #SCA > PPA
    model += n1 >= n2   #SCA > PPA


    # Displaying Optimal Value of Objective Function	
    print(pulp.value(model.objective))

0.68848511
0.68272452
1.0
0.57267942
0.68109073
0.49956445000000005
0.72980108
0.53425806
1.00000024
0.8857160099999999
0.47175372000000004
0.3915388
0.35800023
0.4394404
0.5667203000000001
0.31895026
0.8552689
0.40618191
0.3859057
0.54435524
0.5635489
0.6528941
0.4947346
0.33284944000000005
0.38283574
0.33362715
0.22861405
0.69766958
0.6680923599999999
0.89255467
0.5422532
0.53517568
0.7141855
0.35067336
0.26866185
0.5722392399999999
0.33764606
0.43647189999999997
0.7402186100000001
0.6364003
0.4001322
0.33748024000000004
0.3716972
0.20986239999999998
0.39296381999999996
0.45306267999999994
0.7339784300000001
0.4609139
0.3170803
0.17306897999999998
0.854452
0.51052674
0.44706708
0.9999987999999999
0.3602324
0.40300254
0.47279094999999993
0.7395167999999999
0.50358879
0.26546000000000003
0.5959331
1.0000007
0.3095671
0.48826989
0.9057286499999999
1.0000000199999999
0.8322554600000001
0.7347998699999999
0.26943729
0.4314586
0.37418873999999996
0.31640480000000004
0.64161019
0.53665884
0

In [ ]:
!pip install pulp
import pulp
!apt-get install -y -qq glpk-utils

from pulp import GLPK
import pandas as pd # Library to handle data
import numpy as np
from statistics import mean

data = pd.read_csv("/content/CM and CDMs.csv", encoding = 'unicode_escape', engine ='python')
#creating a list to store the optimal decision variables
weights_matrix = np.empty((6,97))
for k in range(97):  # Where k represents the number of observations
    model = pulp.LpProblem("DEA Model 1 for Strikers (Dribbling and Ball Carrying)", pulp.LpMaximize) # Create an LP maximization problem. We have 1 input, 6 outputs for goal scoring
    m1 = pulp.LpVariable("m1", lowBound=0.00000000001, upBound=None, cat='Continuous') # Create a variable m1>=0 , where m is denotes my inputs. In DEA model 1, there is just 1 input - playing time
    n1 = pulp.LpVariable("n1", lowBound=0.00000000001, upBound=None, cat='Continuous') # Create a variable n2>=0  , simmilar to above
    n2 = pulp.LpVariable("n2", lowBound=0.00000000001, upBound=None, cat='Continuous') # Create a variable n3>=0
    n3 = pulp.LpVariable("n3", lowBound=0.00000000001, upBound=None, cat='Continuous') # Create a variable n4>=0
    n4 = pulp.LpVariable("n4", lowBound=0.00000000001, upBound=None, cat='Continuous') # Create a variable n5>=0
    n5 = pulp.LpVariable("n5", lowBound=0.00000000001, upBound=None, cat='Continuous') # Create a variable n6>=0
   
    model += n1*data["SCA Drib"][k] + n2*data["GCA Drib"][k]+ n3*data["Carry PrgDist"][k] + n4*data["Carries Final Third"][k] + n5*data["Carry into box"][k]    #objective function
    
    model += m1*data["Minutes Played"][k] == 1 #first constraint (equality)

    for i in range(97): #NUMBER OF STRIKERS
        model += n1*data["SCA Drib"][i] + n2*data["GCA Drib"][i] + n3*data["Carry PrgDist"][i] + n4*data["Carries Final Third"][i] + n5*data["Carry into box"][i] - m1*data["Minutes Played"][i] <= 0
   
    status = model.solve(GLPK(msg=True, options=['--ranges', 'sensitivity.txt'])) 
    
    #ADD IN RELATIVE WEIGHT RESTRICTIONS AND CONDITION FOR WEIGHTS TO BE POSITIVE.
    model += n2 >= n3   #Goals > SoT(%)
    model += n2 >= n4   #Goals > G-Xg
    model += n2 >= n5   #Goals > Big Chances Missed
    model += n1 >= n3   #Goals > SoT(%)
    model += n1 >= n4   #Goals > Shots on Target
    model += n1 >= n5   #Goals > SoT(%)
        
    # Displaying Optimal Value of Objective Function	
    print(pulp.value(model.objective))

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
ERROR: Operation cancelled by user
0.5037614499999999
0.72849582
1.0000011
0.6864224800000001
0.9999986759999999
0.61030996
0.8706764119999999
0.5363826
0.9442141619000001
0.7678499
0.811881766
0.64712974
0.5572620382
0.825774768
0.838998926
0.4497705322
0.8068550000000001
0.393336466
0.8973766269
1.0
0.7172825
0.767336148
0.63313994
0.402732322
0.6665071546
0.469569182
0.28781586000000003
0.800120224
0.38576504879999995
0.9999994000000001
0.7852435400000001
0.2779845525
0.2081539314
0.28309508400000005
0.27786459799999996
0.5234325776000001
0.399976646
0.6049436847999999
0.8726583149999999
0.9318346142
0.312210464
0.312115439
0.4351611
0.38394364599999997
0.632190315
0.488770269
0.84948775314
0.474490134
0.4009544736
0.214468774
0.7943452719999999
0.313159669
0.55592221
0.6331238180000001
0.50120761
0.578928
0.9071994680000001
0.58576688
0.49463080000000004
0.479457885
0.3590057075000000

In [ ]:
!pip install pulp
import pulp
!apt-get install -y -qq glpk-utils

from pulp import GLPK
import pandas as pd # Library to handle data
import numpy as np
from statistics import mean

data = pd.read_csv("/content/CM and CDMs.csv", encoding = 'unicode_escape', engine ='python')
#creating a list to store the optimal decision variables
weights_matrix = np.empty((5,97))
for k in range(97):  # Where k represents the number of observations
    model = pulp.LpProblem("DEA Model 1 for Strikers (Defending)", pulp.LpMaximize) # Create an LP maximization problem. We have 1 input, 6 outputs for goal scoring
    n1 = pulp.LpVariable("n1", lowBound=0.000000001, upBound=None, cat='Continuous') # Create a variable n1>=0, where n1 represents the weight associated with output 1 - with goal scoring, it will be goals scored
    n2 = pulp.LpVariable("n2", lowBound=0.000000001, upBound=None, cat='Continuous') # Create a variable n2>=0  , simmilar to above
    n3 = pulp.LpVariable("n3", lowBound=0.000000001, upBound=None, cat='Continuous') # Create a variable n3>=0
    n4 = pulp.LpVariable("n4", lowBound=0.000000001, upBound=None, cat='Continuous') # Create a variable n4>=0
    m1 = pulp.LpVariable("m1", lowBound=0.000000001, upBound=None, cat='Continuous') # Create a variable m1>=0 , where m is denotes my inputs. In DEA model 1, there is just 1 input - playing time
   
    model += n1*data["Tackles TklW"][k] + n2*data["Pressures Succ"][k] + n3*data["Blocks and Interceptions"][k]+ n4*data["Recoveries"][k] #objective function
    
    model += m1*data["Minutes Played"][k] == 1 #first constraint (equality)

    for i in range(97): #NUMBER OF STRIKERS
        model += n1*data["Tackles TklW"][i] + n2*data["Pressures Succ"][i] + n3*data["Blocks and Interceptions"][i] + n4*data["Recoveries"][i] - m1*data["Minutes Played"][i] <= 0
   
    status = model.solve(GLPK(msg=True, options=['--ranges', 'sensitivity.txt'])) 
    
    #ADD IN RELATIVE WEIGHT RESTRICTIONS AND CONDITION FOR WEIGHTS TO BE POSITIVE.
    model += n3*data["Blocks and Interceptions"][k] >= n2*data["Pressures Succ"][k]   #Goals > SoT
      

    # Displaying Optimal Value of Objective Function	
    print(pulp.value(model.objective))


Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
0.797542752
0.6018923032000001
0.50190042
0.80369387656
0.517428013
0.50944013
0.7940378899999999
0.6321217532
0.66440606
0.8153508
0.8591364375999999
0.7827332400000001
0.80426564
0.6625411999999999
0.5859213200000001
0.86870136
0.730955834
0.84935152
0.8587222999999999
0.8379814267000001
1.00000085
1.00000051
0.79425935
0.8166559366899999
0.68573565
0.6752524
0.6512488000000001
0.66961348
0.637346
0.5315024
1.0000008599999999
0.6035120239999999
0.60065329
0.69264034
0.861161888
0.97314378
0.8707482999999999
0.9999994899999999
0.896050436
0.70498316
0.979328827
0.773185659
0.55985151
0.87916998
1.000000512
0.590097976
0.90038996
0.86159038
0.948083844
0.999999
0.8187864
0.96064664
0.978699856
0.9175967199999999
0.93029316
0.7334986000000001
0.7059226000000001
0.66500775
0.51619116
0.5962918100000001
0.912669486
0.612820292
0.9999978
0.654239996
0.782124448
0.60159442
0.7290889899999999
0

# **Center Backs**

In [ ]:
!pip install pulp
import pulp
!apt-get install -y -qq glpk-utils

from pulp import GLPK
import pandas as pd # Library to handle data
import numpy as np
from statistics import mean

data = pd.read_csv("/content/CBs.csv", encoding = 'unicode_escape', engine ='python')
#creating a list to store the optimal decision variables
weights_matrix = np.empty((5,84))
for k in range(84):  # Where k represents the number of observations
    model = pulp.LpProblem("DEA Model 1 for Strikers (Goal-Scoring)", pulp.LpMaximize) # Create an LP maximization problem. We have 1 input, 6 outputs for goal scoring
    n1 = pulp.LpVariable("n1", lowBound=0.00001, upBound=None, cat='Continuous') # Create a variable n1>=0, where n1 represents the weight associated with output 1 - with goal scoring, it will be goals scored
    n2 = pulp.LpVariable("n2", lowBound=0.00001, upBound=None, cat='Continuous') # Create a variable n2>=0  , simmilar to above
    n3 = pulp.LpVariable("n3", lowBound=0.00001, upBound=None, cat='Continuous') # Create a variable n3>=0
    n5 = pulp.LpVariable("n5", lowBound=0.00001, upBound=None, cat='Continuous') # Create a variable n5>=0
    m1 = pulp.LpVariable("m1", lowBound=0.00001, upBound=None, cat='Continuous') # Create a variable m1>=0 , where m is denotes my inputs. In DEA model 1, there is just 1 input - playing time
    
   
    model += n1*data["Gls"][k] + n2*data["SoT"][k] + n3*data["G-xG"][k]+ n5*data["GCA"][k]  #objective function
    
    model += m1*data["Minutes Played"][k] == 1 #first constraint (equality)

    for i in range(84): #NUMBER OF STRIKERS
        model += n1*data["Gls"][i] + n2*data["SoT"][i] + n3*data["G-xG"][i] + n5*data["GCA"][i] -  m1*data["Minutes Played"][i] <= 0
   

    #ADD IN RELATIVE WEIGHT RESTRICTIONS AND CONDITION FOR WEIGHTS TO BE POSITIVE.
    model += n1*data["Gls"][i] >= n2*data["SoT"][i]  #Goals > SoT
    model += n1*data["Gls"][i] >= n3*data["G-xG"][i]  #Goals > G-Xg
    model += n5*data["GCA"][i] >= n2*data["SoT"][i]  #GCA > Shots on Target
    model += n5*data["GCA"][i] >= n3*data["G-xG"][i]  #GCA > Big Chances Missed
    
  
    status = model.solve(GLPK(msg=True, options=['--ranges', 'sensitivity.txt']))  
    
        
    # Displaying Optimal Value of Objective Function	
    print(pulp.value(model.objective))

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
0.3865078
0.799647
0.4590709
0.8467728999999999
0.558821
0.5403685
0.3130704
0.48100519999999997
0.44220960000000004
0.3459868
0.577798
0.7499293
0.3150371
0.2121326
0.20612270000000002
0.25733280000000003
0.9134504999999999
0.1341704
0.600909
1.0000004
0.22746669999999997
0.219997
0.37030360000000007
0.5262870000000001
0.12284500000000001
0.406602
0.9161944
0.6316124000000001
0.35582050000000004
0.7805008
0.3766298
0.161863
0.22178850000000003
0.44582359999999993
0.1341077
0.6964097999999999
0.4931173
0.2600206
0.20861
0.3638344
0.49595219999999995
0.41898499999999994
0.4627143
0.7431384999999999
0.4778163999999999
0.257053
0.27885659999999995
0.39283
0.23470639999999998
0.488488
0.610402
0.15992
0.499426
0.6323880000000001
0.200325
0.147534
-1.0000000000000002e-06
0.5678219999999999
0.68437
None
0.24396389999999998
0.32876609999999995
0.5278921999999999
0.582334
0.9388259999999999
0.404

In [ ]:
from pulp import GLPK
import pandas as pd # Library to handle data
import numpy as np
from statistics import mean

data = pd.read_csv("/content/CBs.csv", encoding = 'unicode_escape', engine ='python')
#creating a list to store the optimal decision variables
weights_matrix = np.empty((6,84))
for k in range(84):  # Where k represents the number of observations
    model = pulp.LpProblem("DEA Model 1 for Strikers (Creativity)", pulp.LpMaximize) # Create an LP maximization problem. We have 1 input, 6 outputs for goal scoring
    n1 = pulp.LpVariable("n1", lowBound=0.000001, upBound=None, cat='Continuous') # Create a variable n1>=0, where n1 represents the weight associated with output 1 - with goal scoring, it will be goals scored
    n2 = pulp.LpVariable("n2", lowBound=0.000001, upBound=None, cat='Continuous') # Create a variable n2>=0  , simmilar to above
    n3 = pulp.LpVariable("n3", lowBound=0.000001, upBound=None, cat='Continuous') # Create a variable n3>=0
    n4 = pulp.LpVariable("n4", lowBound=0.000001, upBound=None, cat='Continuous') # Create a variable n4>=0
    m1 = pulp.LpVariable("m1", lowBound=0.000001, upBound=None, cat='Continuous') # Create a variable m1>=0 , where m is denotes my inputs. In DEA model 1, there is just 1 input - playing time

    model += n1*data["xA"][k] + n2*data["KP"][k] + n3*data["PPA"][k]+ n4*data["SCA"][k] #objective function
    
    model += m1*data["Minutes Played"][k] == 1 #first constraint (equality)

    for i in range(84): #NUMBER OF STRIKERS
        model += n1*data["xA"][i] + n2*data["KP"][i] + n3*data["PPA"][i] + n4*data["SCA"][i] - m1*data["Minutes Played"][i] <= 0
   
    status = model.solve(GLPK(msg=True, options=['--ranges', 'sensitivity.txt'])) 
    
    #ADD IN RELATIVE WEIGHT RESTRICTIONS AND CONDITION FOR WEIGHTS TO BE POSITIVE.
    model += n1 >= n3 #xA > PPA
    model += n2 >= n3  #KP > PPA
    model += n4 >= n3   #SCA > PPA
    model += n1 >= n2   #SCA > PPA


    # Displaying Optimal Value of Objective Function	
    print(pulp.value(model.objective))

0.15241329999999997
0.2622326
0.2602072
0.34335269999999996
0.1910595
0.24928629999999996
0.30091419999999997
0.15793474
0.1378527
0.1942864
0.5458275
0.24602313
0.32141749999999997
0.19132013
0.47003469999999997
0.14657605
0.24442930000000002
0.21427690000000002
0.28740154
0.1829647
0.2685547
0.5367462
0.05446415
0.1175481
0.0919552
0.1690821
0.24926629999999997
0.9095599000000001
0.17591280000000004
0.2162344
0.2549763
0.5744051
0.39351539999999996
0.16995809999999997
0.4367023
0.2763085
0.3139467
0.19968640000000001
0.2729451
0.197571
0.19517520000000002
0.0696912
0.2862654
1.0000003
0.2861558
0.35652939999999994
0.20615320000000004
0.4297828
0.1070837
0.274673
0.2981412
0.25210279999999996
0.23075600000000002
0.1402532
0.1999365
0.1135555
0.17091820000000002
0.34112719999999996
0.7222780000000001
0.1144056
0.17856799999999998
0.12499550000000001
0.31359549999999997
0.9999998
0.0977518
0.2727264
0.1105317
0.7024769000000001
0.2337215
0.0749978
0.1882024
0.9906349999999999
0.2612735


In [ ]:
!pip install pulp
import pulp
!apt-get install -y -qq glpk-utils

from pulp import GLPK
import pandas as pd # Library to handle data
import numpy as np
from statistics import mean

data = pd.read_csv("/content/CBs.csv", encoding = 'unicode_escape', engine ='python')
#creating a list to store the optimal decision variables
weights_matrix = np.empty((6,84))
for k in range(84):  # Where k represents the number of observations
    model = pulp.LpProblem("DEA Model 1 for Strikers (Dribbling and Ball Carrying)", pulp.LpMaximize) # Create an LP maximization problem. We have 1 input, 6 outputs for goal scoring
    m1 = pulp.LpVariable("m1", lowBound=0.00000000001, upBound=None, cat='Continuous') # Create a variable m1>=0 , where m is denotes my inputs. In DEA model 1, there is just 1 input - playing time
    n1 = pulp.LpVariable("n1", lowBound=0.00000000001, upBound=None, cat='Continuous') # Create a variable n2>=0  , simmilar to above
    n2 = pulp.LpVariable("n2", lowBound=0.00000000001, upBound=None, cat='Continuous') # Create a variable n3>=0
    n3 = pulp.LpVariable("n3", lowBound=0.00000000001, upBound=None, cat='Continuous') # Create a variable n4>=0
    n4 = pulp.LpVariable("n4", lowBound=0.00000000001, upBound=None, cat='Continuous') # Create a variable n5>=0
    n5 = pulp.LpVariable("n5", lowBound=0.00000000001, upBound=None, cat='Continuous') # Create a variable n6>=0
   
    model += n1*data["SCA Drib"][k] + n2*data["GCA Drib"][k]+ n3*data["Carry PrgDist"][k] + n4*data["Carries Final Third"][k] + n5*data["Carry into box"][k]    #objective function
    
    model += m1*data["Minutes Played"][k] == 1 #first constraint (equality)

    for i in range(84): #NUMBER OF STRIKERS
        model += n1*data["SCA Drib"][i] + n2*data["GCA Drib"][i] + n3*data["Carry PrgDist"][i] + n4*data["Carries Final Third"][i] + n5*data["Carry into box"][i] - m1*data["Minutes Played"][i] <= 0
   
    status = model.solve(GLPK(msg=True, options=['--ranges', 'sensitivity.txt'])) 
    
    #ADD IN RELATIVE WEIGHT RESTRICTIONS AND CONDITION FOR WEIGHTS TO BE POSITIVE.
    model += n2 >= n3   #Goals > SoT(%)
    model += n2 >= n4   #Goals > G-Xg
    model += n2 >= n5   #Goals > Big Chances Missed
    model += n1 >= n3   #Goals > SoT(%)
    model += n1 >= n4   #Goals > Shots on Target
    model += n1 >= n5   #Goals > SoT(%)
        
    # Displaying Optimal Value of Objective Function	
    print(pulp.value(model.objective))

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
0.381744168
0.49286808
1.000001259
0.9466766099999999
0.434350272
0.932629978
0.22711325499999999
0.438822598
0.129045312
0.38503211
0.70645225
0.474715612
0.513883335
0.641754587
0.5796907392
0.779889
0.989351466
0.612473348
0.5315365000000001
0.670957316
0.811305816
0.5155792880000001
0.14230315799999999
0.132322884
0.2629325426
0.861963484
0.5347428792
0.695020524
0.555386367
0.519163011
0.519854187
0.5394405099999999
0.417874608
0.6713634678999999
0.9052955
0.7588132710000001
0.904612968
0.38429339
0.332065
0.225711962
0.467226762
0.650191992
0.36332079500000003
0.7764340000000001
0.19361379299999998
1.000000598
0.8827303216
1.0
0.197348886
0.265172464
0.5773599899999999
0.57248586
0.139128492
0.205658865
0.279796
0.35389308
0.410437152
0.60979923
0.389306984
0.597938016
0.144678888
0.19477223
0.186787761
1.0
0.239966086
0.28444547200000003
0.496149108
1.0
0.352150364
0.567130905
0.99

# DEA MODEL 2 - Cost Efficiency

---



# Strikers

1) GOAL SCORING

In [ ]:
from pulp import GLPK
import pandas as pd # Library to handle data
import numpy as np
from statistics import mean

data = pd.read_csv("/content/Strikers DEA Model 2.csv", encoding = 'unicode_escape', engine ='python')
#creating a list to store the optimal decision variables
weights_matrix = np.empty((6,51))
for k in range(51):  # Where k represents the number of observations
    model = pulp.LpProblem("DEA Model 1 for Strikers (Goal-Scoring)", pulp.LpMaximize) # Create an LP maximization problem. We have 1 input, 6 outputs for goal scoring
    n1 = pulp.LpVariable("n1", lowBound=0.0000001, upBound=None, cat='Continuous') # Create a variable n1>=0, where n1 represents the weight associated with output 1 - with goal scoring, it will be goals scored
    n2 = pulp.LpVariable("n2", lowBound=0.0000001, upBound=None, cat='Continuous') # Create a variable n2>=0  , simmilar to above
    n3 = pulp.LpVariable("n3", lowBound=0.0000001, upBound=None, cat='Continuous') # Create a variable n4>=0
    n4 = pulp.LpVariable("n4", lowBound=0.0000001, upBound=None, cat='Continuous') # Create a variable n5>=0
    n5 = pulp.LpVariable("n5", lowBound=0.0000001, upBound=None, cat='Continuous') # Create a variable n6>=0
    m1 = pulp.LpVariable("m1", lowBound=0.0000001, upBound=None, cat='Continuous') # Create a variable m1>=0 , where m is denotes my inputs. In DEA model 2, there is just 1 input - Salary

    model += n1*data["Gls"][k] + n2*data["SoT"][k] + n3*data["G-xG"][k] + n5*data["GCA"][k]  #objective function
    
    model += m1*data["Salary"][k] == 1 #first constraint (equality)

    for i in range(51): #NUMBER OF STRIKERS
        model += n1*data["Gls"][i] + n2*data["SoT"][i] + n3*data["G-xG"][i] + n5*data["GCA"][i] -  m1*data["Salary"][i] <= 0
   
    status = model.solve(GLPK(msg=True, options=['--ranges', 'sensitivity.txt'])) 
    print("Model Status:{}".format(pulp.LpStatus[model.status])) 
    
    #ADD IN RELATIVE WEIGHT RESTRICTIONS AND CONDITION FOR WEIGHTS TO BE POSITIVE.
    model += n1*data["Gls"][k] >= n2*data["SoT"][k]   #Goals > SoT
    model += n1*data["Gls"][k] >= n3*data["G-xG"][k]   #Goals > G-Xg
    model += n1*data["Gls"][k] >= n5*data["Big Chances Missed"][k]   #Goals > Big Chances Missed
    model += n3*data["G-xG"][k] >= n2*data["SoT"][k]   #Goals > Shots on Target
    model += n5*data["GCA"][k]>= n2*data["SoT"][k]  #Goals > Shots on Target
    model += n5*data["GCA"][k] >= n4*data["Big Chances Missed"][k]   #Goals > Big Chances Missed


    # Displaying Optimal Decision Variables & Reduced Cost per Variable
    list_weights=[]
    for v in model.variables():
	      print(v.name, "=", v.varValue, "\tReduced Cost =", v.dj)
    for v in model.variables():  
        list_weights=list_weights+[v.varValue]
    for n in range(5):
        value= list_weights[n]
        weights_matrix[n,k] = value
        
    # Displaying Optimal Value of Objective Function	
    print("Objective=", pulp.value(model.objective))
	
    # Displaying Shadow Price & Slack Value per Constraint
    print ("\nSensitivity Analysis\nConstraint\t\tShadow Price\tSlack")
    for name, c in model.constraints.items():
	      print(name, ":", c, "\t", c.pi, "\t\t", c.slack)

Model Status:Optimal
m1 = 0.0001 	Reduced Cost = None
n1 = 0.908637 	Reduced Cost = None
n2 = 1e-07 	Reduced Cost = None
n3 = 0.413529 	Reduced Cost = None
n4 = None 	Reduced Cost = None
n5 = 1e-07 	Reduced Cost = None
Objective= 0.9443492352599999

Sensitivity Analysis
Constraint		Shadow Price	Slack
_C1 : 10000*m1 = 1 	 None 		 None
_C2 : -10000*m1 + 0.5745*n1 + 0.617*n2 + 1.0213*n3 + 0.4936*n5 <= -0.0 	 None 		 None
_C3 : -43077*m1 + 0.5745*n1 + 0.8128*n2 + 1.1957*n3 + 0.834*n5 <= -0.0 	 None 		 None
_C4 : -60000*m1 + 0.6468*n1 + 0.966*n2 + 0.7489*n3 + 0.766*n5 <= -0.0 	 None 		 None
_C5 : -182115*m1 + 1.3872*n1 + 1.2766*n2 + 1.6681*n3 + 0.766*n5 <= -0.0 	 None 		 None
_C6 : -250000*m1 + 0.7234*n1 + 1.1234*n2 + 0.8851*n3 + 0.9702*n5 <= -0.0 	 None 		 None
_C7 : -30962*m1 + 1.166*n1 + 1.3149*n2 + 1.4809*n3 + 0.4936*n5 <= -0.0 	 None 		 None
_C8 : -40000*m1 + 0.6468*n1 + 0.7745*n2 + 0.9404*n3 + 0.5617*n5 <= -0.0 	 None 		 None
_C9 : -55000*m1 + 0.9447*n1 + 1.2*n2 + 1.3021*n3 + 1.0383*n

In [ ]:
efficiency_table =np.empty((52,6))
average_list =[]
for row in range(52):
    row_values=[]
    for column in range(6):
       value = ((weights_matrix[1,column]*data["Gls"][row])+(weights_matrix[2,column]*data["SoT"][row])+(weights_matrix[3,column]*data["G-xG"][row])+(weights_matrix[4,column]*data["Big Chances Missed"][row])+(weights_matrix[5,column]*data["GCA"][row]))/((weights_matrix[0,column]*data["Salary NORM"][row]))
       efficiency_table[row,column]=value
       row_values=row_values+[value]
    average =mean(row_values)
    average_list =average_list+[average]

    average_list_rounded = [ '%.2f' % elem for elem in average_list ]

    player_list = ['Aaron Connolly', 'Adama TraorÃ©', 'Aleksandar MitroviÄ‡', 'Alexandre Lacazette', 'Anthony Martial', 'Anwar El Ghazi', 'Ashley Barnes', 'Bertrand TraorÃ©', 'Billy Sharp', 'Callum Wilson', 'Che Adams', 'Chris Wood', 'Christian Benteke', 'Daniel James', 'Danny Ings', 'Danny Welbeck', 'Diogo Jota', 'Dominic Calvert-Lewin', 'Edinson Cavani', 'FÃ¡bio Silva', 'Gabriel Jesus', 'Gareth Bale', 'Harry Kane', 'Jamie Vardy', 'Kelechi Iheanacho', 'Marcus Rashford', 'Mason Greenwood', 'MatÄ›j Vydra', 'Mbaye Diagne', 'Michail Antonio', 'Michy Batshuayi', 'Mohamed Salah', 'Oliver Burke', 'Oliver McBurnie', 'Olivier Giroud', 'Ollie Watkins', 'Patrick Bamford', 'Pierre-Emerick Aubameyang', 'RaÃºl JimÃ©nez', 'Raheem Sterling', 'Rhian Brewster', 'Richarlison', 'Riyad Mahrez', 'Roberto Firmino', 'SÃ©bastien Haller', 'Sadio ManÃ©', 'Son Heung-min', 'Tammy Abraham', 'Timo Werner', 'TrÃ©zÃ©guet', 'Wilfried Zaha', 'Willian JosÃ©']
for player in player_list:
    index = player_list.index(player)
    print(average_list_rounded[index])

display(efficiency_table)
efficiency_table = efficiency_table.round(decimals=2)
display(efficiency_table)


0.58
0.76
0.37
0.41
0.20
0.73
0.49
0.57
0.82
0.53
0.63
0.50
0.48
0.70
0.64
0.47
0.54
0.72
0.87
0.35
0.40
0.45
0.22
0.39
0.22
0.70
0.36
0.46
0.41
0.49
0.43
0.47
0.35
0.61
0.51
0.37
0.43
0.61
0.25
0.68
0.19
0.56
0.29
0.52
0.23
0.49
0.29
0.59
0.51
0.17
0.45
0.50


array([[0.72460264, 0.21497624, 0.41821954, 0.72460159, 0.6199424 ,
        0.78145404],
       [0.76682312, 0.62219117, 0.84221886, 0.76682206, 0.73391894,
        0.85089557],
       [0.40806312, 0.17666768, 0.41474367, 0.40806261, 0.36009128,
        0.46602007],
       [0.5350816 , 0.08224145, 0.27707145, 0.53508085, 0.44270401,
        0.58082159],
       [0.23964614, 0.06627418, 0.20781899, 0.23964583, 0.20408051,
        0.27181617],
       [0.90951466, 0.20685152, 0.58610503, 0.90951341, 0.76572214,
        1.00000056],
       [0.56577234, 0.22433773, 0.43670341, 0.56577156, 0.49519494,
        0.62330984],
       [0.70442969, 0.18122108, 0.48448588, 0.70442872, 0.59720546,
        0.77748634],
       [0.93374899, 0.54326249, 0.68250954, 0.93374763, 0.85139641,
        1.00000062],
       [0.68707588, 0.12955112, 0.35809275, 0.68707494, 0.57318163,
        0.74323207],
       [0.7736632 , 0.13777247, 0.57571137, 0.77366219, 0.64381697,
        0.86958742],
       [0.57611974, 0

array([[0.72, 0.21, 0.42, 0.72, 0.62, 0.78],
       [0.77, 0.62, 0.84, 0.77, 0.73, 0.85],
       [0.41, 0.18, 0.41, 0.41, 0.36, 0.47],
       [0.54, 0.08, 0.28, 0.54, 0.44, 0.58],
       [0.24, 0.07, 0.21, 0.24, 0.2 , 0.27],
       [0.91, 0.21, 0.59, 0.91, 0.77, 1.  ],
       [0.57, 0.22, 0.44, 0.57, 0.5 , 0.62],
       [0.7 , 0.18, 0.48, 0.7 , 0.6 , 0.78],
       [0.93, 0.54, 0.68, 0.93, 0.85, 1.  ],
       [0.69, 0.13, 0.36, 0.69, 0.57, 0.74],
       [0.77, 0.14, 0.58, 0.77, 0.64, 0.87],
       [0.58, 0.12, 0.57, 0.58, 0.48, 0.67],
       [0.59, 0.12, 0.42, 0.59, 0.5 , 0.66],
       [0.8 , 0.45, 0.59, 0.8 , 0.72, 0.86],
       [0.83, 0.14, 0.42, 0.83, 0.69, 0.9 ],
       [0.6 , 0.14, 0.35, 0.6 , 0.5 , 0.65],
       [0.7 , 0.12, 0.4 , 0.7 , 0.58, 0.76],
       [0.85, 0.15, 0.79, 0.85, 0.7 , 0.98],
       [0.89, 0.74, 0.9 , 0.89, 0.85, 0.97],
       [0.47, 0.08, 0.21, 0.47, 0.39, 0.5 ],
       [0.46, 0.16, 0.37, 0.46, 0.4 , 0.52],
       [0.57, 0.14, 0.34, 0.57, 0.48, 0.62],
       [0.

In [ ]:
from pulp import GLPK
import pandas as pd # Library to handle data
import numpy as np
from statistics import mean

data = pd.read_csv("/content/Strikers DEA Model 2.csv", encoding = 'unicode_escape', engine ='python')
#creating a list to store the optimal decision variables
weights_matrix = np.empty((6,51))
for k in range(51):  # Where k represents the number of observations
    model = pulp.LpProblem("DEA Model 1 for Strikers (Goal-Scoring)", pulp.LpMaximize) # Create an LP maximization problem. We have 1 input, 6 outputs for goal scoring
    m1 = pulp.LpVariable("m1", lowBound=0.0000001, upBound=None, cat='Continuous') # Create a variable m1>=0 , where m is denotes my inputs. In DEA model 1, there is just 1 input - playing time
    n1 = pulp.LpVariable("n1", lowBound=0.00001, upBound=None, cat='Continuous') # Create a variable n1>=0, where n1 represents the weight associated with output 1 - with goal scoring, it will be goals scored
    n2 = pulp.LpVariable("n2", lowBound=0.0000001, upBound=None, cat='Continuous') # Create a variable n2>=0  , simmilar to above
    n4 = pulp.LpVariable("n4", lowBound=0.0000001, upBound=None, cat='Continuous') # Create a variable n4>=0
    n5 = pulp.LpVariable("n5", lowBound=0.0000001, upBound=None, cat='Continuous') # Create a variable n5>=0
    n6 = pulp.LpVariable("n6", lowBound=0.0000001, upBound=None, cat='Continuous') # Create a variable n6>=0
   
    model += n1*data["Gls"][k] + n2*data["SoT"][k] + n4*data["G-xG"][k] + n5*data["Big Chances Missed"][k] + n6*data["GCA"][k]  #objective function
    
    model += m1*data["Salary NORM"][k] == 1 #first constraint (equality)

    for i in range(51): #NUMBER OF STRIKERS
        model += n1*data["Gls"][i] + n2*data["SoT"][i] + n4*data["G-xG"][i] + n5*data["Big Chances Missed"][i] + n6*data["GCA"][i] -  m1*data["Salary NORM"][i] <= 0
   
    status = model.solve(GLPK(msg=True, options=['--ranges', 'sensitivity.txt'])) 

    
    #ADD IN RELATIVE WEIGHT RESTRICTIONS AND CONDITION FOR WEIGHTS TO BE POSITIVE.
    model += n1*data["Gls"][k] >= n2*data["SoT"][k]   #Goals > SoT
    model += n1*data["Gls"][k] >= n4*data["G-xG"][k]   #Goals > G-Xg
    model += n1*data["Gls"][k] >= n5*data["Big Chances Missed"][k]   #Goals > Big Chances Missed
    model += n4*data["G-xG"][k] >= n2*data["SoT"][k]   #Goals > Shots on Target
    model += n6*data["GCA"][k]>= n2*data["SoT"][k]  #Goals > Shots on Target
    model += n6*data["GCA"][k] >= n5*data["Big Chances Missed"][k]   #Goals > Big Chances Missed
        
    # Displaying Optimal Value of Objective Function	
    print(pulp.value(model.objective))
	

0.8024864727000003
0.99999949685
0.5464840974
0.59116602906
0.31853086036
1.00000010967
0.64447015175
0.8433068413999999
1.0000001884999998
0.84159891907
0.90863159561
0.73627563828
0.6678299239400001
0.8974983522400001
0.9534184571500001
0.69266392571
0.76539796485
0.9999990239700001
0.5133944447500001
0.55068836275
0.71844386489
0.30649698128
0.68988799071
0.73092958659
1.00000002524
0.58999057606
0.65484857282
0.64663770336
0.7790703509599999
0.6946289189000001
0.6582379763999999
0.60161076473
0.8272030953599999
0.7163476146900001
0.5101425690400001
0.79133551222
0.99999939105
0.36499802468
0.9405612249299998
0.37001792189
0.7102277550500001
0.5903902641800001
0.80214116899
0.41981958112
0.65861472981
0.6059365648299999
0.90907317132
0.6947070635799999
0.6115099793400002
0.61044837391
0.7604930582799999


DEA MODEL 2, CREATIVITY

In [ ]:
from pulp import GLPK
import pandas as pd # Library to handle data
import numpy as np
from statistics import mean

data = pd.read_csv("/content/Strikers DEA Model 2.csv", encoding = 'unicode_escape', engine ='python')
#creating a list to store the optimal decision variables
weights_matrix = np.empty((6,52))
for k in range(52):  # Where k represents the number of observations
    model = pulp.LpProblem("DEA Model 1 for Strikers (Creativity)", pulp.LpMaximize) # Create an LP maximization problem. We have 1 input, 6 outputs for goal scoring
    n1 = pulp.LpVariable("n1", lowBound=0.000001, upBound=None, cat='Continuous') # Create a variable n1>=0, where n1 represents the weight associated with output 1 - with goal scoring, it will be goals scored
    n2 = pulp.LpVariable("n2", lowBound=0.000001, upBound=None, cat='Continuous') # Create a variable n2>=0  , simmilar to above
    n3 = pulp.LpVariable("n3", lowBound=0.000001, upBound=None, cat='Continuous') # Create a variable n3>=0
    n4 = pulp.LpVariable("n4", lowBound=0.000001, upBound=None, cat='Continuous') # Create a variable n4>=0
    n5 = pulp.LpVariable("n5", lowBound=0.000001, upBound=None, cat='Continuous') # Create a variable n4>=0
    m1 = pulp.LpVariable("m1", lowBound=0.000001, upBound=None, cat='Continuous') # Create a variable m1>=0 , where m is denotes my inputs. In DEA model 1, there is just 1 input - playing time

    model += n1*data["xA"][k] + n2*data["KP"][k] + n3*data["PPA"][k]+ n4*data["SCA"][k] + n5*data["Progressive Passes"][k]  #objective function
    
    model += m1*data["Salary NORM"][k] == 1 #first constraint (equality)

    for i in range(52): #NUMBER OF STRIKERS
        model += n1*data["xA"][i] + n2*data["KP"][i] + n3*data["PPA"][i] + n4*data["SCA"][i] + n5*data["Progressive Passes"][i] - m1*data["Salary NORM"][i] <= 0
   
    status = model.solve(GLPK(msg=True, options=['--ranges', 'sensitivity.txt'])) 
    print("Model Status:{}".format(pulp.LpStatus[model.status])) 
    
    #ADD IN RELATIVE WEIGHT RESTRICTIONS AND CONDITION FOR WEIGHTS TO BE POSITIVE.
    model += n1 >= n3 #xA > PPA
    model += n2 >= n3  #KP > PPA
    model += n4 >= n3   #SCA > PPA
    model += n1 >= n2   #SCA > PPA

    # Displaying Optimal Decision Variables & Reduced Cost per Variable
    list_weights=[]
    for v in model.variables():
	      print(v.name, "=", v.varValue, "\tReduced Cost =", v.dj)
    for v in model.variables():  
        list_weights=list_weights+[v.varValue]
    for n in range(5):
        value= list_weights[n]
        weights_matrix[n,k] = value
        
    # Displaying Optimal Value of Objective Function	
    print("Objective=", pulp.value(model.objective))
	
    # Displaying Shadow Price & Slack Value per Constraint
    print ("\nSensitivity Analysis\nConstraint\t\tShadow Price\tSlack")
    for name, c in model.constraints.items():
	      print(name, ":", c, "\t", c.pi, "\t\t", c.slack)

Model Status:Optimal
m1 = 0.991946 	Reduced Cost = None
n1 = 0.351288 	Reduced Cost = None
n2 = 0.20723 	Reduced Cost = None
n3 = 0.37255 	Reduced Cost = None
n4 = 1e-06 	Reduced Cost = None
n5 = 1e-06 	Reduced Cost = None
Objective= 0.40058430204007595

Sensitivity Analysis
Constraint		Shadow Price	Slack
_C1 : 1.00811908*m1 = 1.0 	 None 		 None
_C2 : -1.00811908*m1 + 0.4255*n1 + 0.4468*n2 + 0.4255*n3 + 0.5277*n4 + 0.341340076*n5 <= -0.0 	 None 		 None
_C3 : -1.23191475*m1 + 1.4426*n1 + 1.6383*n2 + 1.0085*n3 + 1.9702*n4 + 2.140430351*n5 <= -0.0 	 None 		 None
_C4 : -1.346414073*m1 + 0.8936*n1 + 0.8468*n2 + 0.7064*n3 + 1.0255*n4 + 1.283880171*n5 <= -0.0 	 None 		 None
_C5 : -2.172631935*m1 + 0.9149*n1 + 0.7532*n2 + 0.8936*n3 + 1.0128*n4 + 2.152886115*n5 <= -0.0 	 None 		 None
_C6 : -2.631935047*m1 + 0.7787*n1 + 0.6809*n2 + 0.7532*n3 + 0.9702*n4 + 2.614864865*n5 <= -0.0 	 None 		 None
_C7 : -1.149945873*m1 + 0.8383*n1 + 0.8936*n2 + 0.8213*n3 + 1.1404*n4 + 2.176069436*n5 <= -0.0 	 None 		

In [ ]:
efficiency_table =np.empty((52,6))
average_list =[]
for row in range(52):
    row_values=[]
    for column in range(6):
       value = ((weights_matrix[1,column]*data["xA"][row])+(weights_matrix[2,column]*data["KP"][row])+(weights_matrix[3,column]*data["PPA"][row])+(weights_matrix[4,column]*data["SCA"][row])+(weights_matrix[5,column]*data["Progressive Passes"][row]))/((weights_matrix[0,column]*data["Salary NORM"][row]))
       efficiency_table[row,column]=value
       row_values=row_values+[value]
    average =mean(row_values)
    average_list =average_list+[average]

    average_list_rounded = [ '%.2f' % elem for elem in average_list ]

    player_list = ['Aaron Connolly', 'Adama Traore', 'Aleksandar Mitrovic', 'Alexandre Lacazette', 'Anthony Martial', 'Anwar El Ghazi', 'Ashley Barnes', 'Bertrand TraorÃ©', 'Billy Sharp', 'Callum Wilson', 'Che Adams', 'Chris Wood', 'Christian Benteke', 'Daniel James', 'Danny Ings', 'Danny Welbeck', 'Diogo Jota', 'Dominic Calvert-Lewin', 'Edinson Cavani', 'FÃ¡bio Silva', 'Gabriel Jesus', 'Gareth Bale', 'Harry Kane', 'Jamie Vardy', 'Kelechi Iheanacho', 'Marcus Rashford', 'Mason Greenwood', 'MatÄ›j Vydra', 'Mbaye Diagne', 'Michail Antonio', 'Michy Batshuayi', 'Mohamed Salah', 'Oliver Burke', 'Oliver McBurnie', 'Olivier Giroud', 'Ollie Watkins', 'Patrick Bamford', 'Pierre-Emerick Aubameyang', 'RaÃºl JimÃ©nez', 'Raheem Sterling', 'Rhian Brewster', 'Richarlison', 'Riyad Mahrez', 'Roberto Firmino', 'SÃ©bastien Haller', 'Sadio ManÃ©', 'Son Heung-min', 'Tammy Abraham', 'Timo Werner', 'TrÃ©zÃ©guet', 'Wilfried Zaha', 'Willian JosÃ©']
for player in player_list:
    index = player_list.index(player)
    print(average_list_rounded[index])

display(efficiency_table)
efficiency_table = efficiency_table.round(decimals=2)
display(efficiency_table)

0.25
0.68
0.36
0.24
0.17
0.44
0.29
0.48
0.25
0.35
0.64
0.35
0.22
0.28
0.37
0.35
0.26
0.43
0.20
0.22
0.38
0.09
0.42
0.34
0.39
0.35
0.32
0.35
0.34
0.36
0.22
0.45
0.39
0.36
0.17
0.50
0.51
0.20
0.27
0.26
0.32
0.38
0.49
0.42
0.22
0.61
0.55
0.23
0.37
0.31
0.37
0.23


array([[0.40058409, 0.17226323, 0.39635534, 0.18035959, 0.17816769,
        0.17375411],
       [0.99999895, 0.52631575, 0.99999644, 0.50369367, 0.51305938,
        0.51033537],
       [0.56347749, 0.25065377, 0.56430994, 0.27280921, 0.2723256 ,
        0.26140633],
       [0.37602807, 0.15341046, 0.3827912 , 0.1739424 , 0.17060765,
        0.16257226],
       [0.26630656, 0.12131183, 0.27471256, 0.12628189, 0.1251086 ,
        0.12212474],
       [0.6887462 , 0.32635989, 0.69376184, 0.31989729, 0.31889489,
        0.31694602],
       [0.43793705, 0.23588902, 0.44788223, 0.20414291, 0.20548202,
        0.21267292],
       [0.73723596, 0.36808247, 0.74996234, 0.3459735 , 0.34630948,
        0.34870279],
       [0.43467937, 0.13706158, 0.41957577, 0.18950281, 0.18284957,
        0.16521007],
       [0.51428349, 0.26834945, 0.55128571, 0.26296062, 0.26416041,
        0.26188803],
       [0.99999877, 0.37354837, 0.99999649, 0.50049743, 0.49546349,
        0.44837798],
       [0.52054655, 0

array([[0.4 , 0.17, 0.4 , 0.18, 0.18, 0.17],
       [1.  , 0.53, 1.  , 0.5 , 0.51, 0.51],
       [0.56, 0.25, 0.56, 0.27, 0.27, 0.26],
       [0.38, 0.15, 0.38, 0.17, 0.17, 0.16],
       [0.27, 0.12, 0.27, 0.13, 0.13, 0.12],
       [0.69, 0.33, 0.69, 0.32, 0.32, 0.32],
       [0.44, 0.24, 0.45, 0.2 , 0.21, 0.21],
       [0.74, 0.37, 0.75, 0.35, 0.35, 0.35],
       [0.43, 0.14, 0.42, 0.19, 0.18, 0.17],
       [0.51, 0.27, 0.55, 0.26, 0.26, 0.26],
       [1.  , 0.37, 1.  , 0.5 , 0.5 , 0.45],
       [0.52, 0.26, 0.52, 0.27, 0.27, 0.26],
       [0.35, 0.17, 0.36, 0.15, 0.15, 0.16],
       [0.48, 0.15, 0.46, 0.2 , 0.19, 0.18],
       [0.56, 0.27, 0.58, 0.27, 0.27, 0.26],
       [0.51, 0.27, 0.52, 0.26, 0.27, 0.26],
       [0.42, 0.18, 0.43, 0.19, 0.19, 0.18],
       [0.63, 0.33, 0.66, 0.32, 0.32, 0.32],
       [0.31, 0.12, 0.31, 0.15, 0.15, 0.14],
       [0.34, 0.18, 0.34, 0.15, 0.15, 0.16],
       [0.55, 0.29, 0.57, 0.29, 0.29, 0.29],
       [0.15, 0.07, 0.15, 0.07, 0.07, 0.06],
       [0.

In [ ]:
from pulp import GLPK
import pandas as pd # Library to handle data
import numpy as np
from statistics import mean

data = pd.read_csv("/content/Strikers DEA Model 2.csv", encoding = 'unicode_escape', engine ='python')
#creating a list to store the optimal decision variables
weights_matrix = np.empty((6,52))
for k in range(52):  # Where k represents the number of observations
    model = pulp.LpProblem("DEA Model 1 for Strikers (Creativity)", pulp.LpMaximize) # Create an LP maximization problem. We have 1 input, 6 outputs for goal scoring
    n1 = pulp.LpVariable("n1", lowBound=0.000001, upBound=None, cat='Continuous') # Create a variable n1>=0, where n1 represents the weight associated with output 1 - with goal scoring, it will be goals scored
    n2 = pulp.LpVariable("n2", lowBound=0.000001, upBound=None, cat='Continuous') # Create a variable n2>=0  , simmilar to above
    n3 = pulp.LpVariable("n3", lowBound=0.000001, upBound=None, cat='Continuous') # Create a variable n3>=0
    n4 = pulp.LpVariable("n4", lowBound=0.000001, upBound=None, cat='Continuous') # Create a variable n4>=0
    n5 = pulp.LpVariable("n5", lowBound=0.000001, upBound=None, cat='Continuous') # Create a variable n4>=0
    m1 = pulp.LpVariable("m1", lowBound=0.000001, upBound=None, cat='Continuous') # Create a variable m1>=0 , where m is denotes my inputs. In DEA model 1, there is just 1 input - playing time

    model += n1*data["xA"][k] + n2*data["KP"][k] + n3*data["PPA"][k]+ n4*data["SCA"][k] + n5*data["Progressive Passes"][k]  #objective function
    
    model += m1*data["Salary NORM"][k] == 1 #first constraint (equality)

    for i in range(52): #NUMBER OF STRIKERS
        model += n1*data["xA"][i] + n2*data["KP"][i] + n3*data["PPA"][i] + n4*data["SCA"][i] + n5*data["Progressive Passes"][i] - m1*data["Salary NORM"][i] <= 0
   
    status = model.solve(GLPK(msg=True, options=['--ranges', 'sensitivity.txt'])) 
    
    #ADD IN RELATIVE WEIGHT RESTRICTIONS AND CONDITION FOR WEIGHTS TO BE POSITIVE.
    model += n1 >= n3 #xA > PPA
    model += n2 >= n3  #KP > PPA
    model += n4 >= n3   #SCA > PPA
    model += n1 >= n2   #SCA > PPA

        
    # Displaying Optimal Value of Objective Function	
    print(pulp.value(model.objective))

	

0.40058430204007595
0.9999990945673529
0.564311556980171
0.44888093906830495
0.40354739493979497
0.8502483557971361
0.540317350247336
0.8692874980173511
0.44015119629387806
0.5512868936236079
0.99999983191248
0.533654743780883
0.42490377379973
0.76311934183426
0.65945609487318
0.5292668539020939
0.8843694235258199
0.656468179726646
0.314915717381818
0.3823544075112719
0.570971688099418
0.24097367774988182
0.7666309880695
0.548695078153521
0.6667471316826801
0.61807085174193
0.6373832689189101
0.547891797291685
0.571597943080326
0.573580619717629
0.41089490222691
0.806842238682288
0.615194637341844
1.00000028161555
0.267459106687397
0.778713245647115
0.7924368984540981
0.35563474022752795
0.6656877263882279
0.40212637243895477
0.5220314380920601
0.604493504816358
1.00000179202719
0.863543285779691
0.523837310558252
1.000000927525708
0.9234501565109831
0.371649063464994
0.5893495673915601
0.706129294663282
0.65553405078094
0.393579725963618


3) DRIBBLING AND BALL CARRYING

In [ ]:
!pip install pulp
import pulp
!apt-get install -y -qq glpk-utils

from pulp import GLPK
import pandas as pd # Library to handle data
import numpy as np
from statistics import mean

data = pd.read_csv("/content/Strikers DEA Model 2.csv", encoding = 'unicode_escape', engine ='python')
#creating a list to store the optimal decision variables
weights_matrix = np.empty((7,52))
for k in range(52):  # Where k represents the number of observations
    model = pulp.LpProblem("DEA Model 1 for Strikers (Dribbling and Ball Carrying)", pulp.LpMaximize) # Create an LP maximization problem. We have 1 input, 6 outputs for goal scoring
    m1 = pulp.LpVariable("m1", lowBound=0.00000000001, upBound=None, cat='Continuous') # Create a variable m1>=0 , where m is denotes my inputs. In DEA model 1, there is just 1 input - playing time
    n1 = pulp.LpVariable("n1", lowBound=0.00000000001, upBound=None, cat='Continuous') # Create a variable n1>=0
    n2 = pulp.LpVariable("n2", lowBound=0.00000000001, upBound=None, cat='Continuous') # Create a variable n2>=0  , simmilar to above
    n3 = pulp.LpVariable("n3", lowBound=0.00000000001, upBound=None, cat='Continuous') # Create a variable n3>=0
    n4 = pulp.LpVariable("n4", lowBound=0.00000000001, upBound=None, cat='Continuous') # Create a variable n4>=0
    n5 = pulp.LpVariable("n5", lowBound=0.0000000001, upBound=None, cat='Continuous') # Create a variable n5>=0
    n6 = pulp.LpVariable("n6", lowBound=0.00000000001, upBound=None, cat='Continuous') # Create a variable n6>=0
   
    model += n1*data["Dribb Succ"][k] + n2*data["SCA Drib"][k] + n3*data["GCA Drib"][k]+ n4*data["Carry PrgDist"][k] + n5*data["Carries Final Third"][k] + n6*data["Carry into box"][k]    #objective function
    
    model += m1*data["Salary NORM"][k] == 1 #first constraint (equality)

    for i in range(52): #NUMBER OF STRIKERS
        model += n1*data["Dribb Succ"][i] + n2*data["SCA Drib"][i] + n3*data["GCA Drib"][i] + n4*data["Carry PrgDist"][i] + n5*data["Carries Final Third"][i] + n6*data["Carry into box"][i] - m1*data["Salary NORM"][i] <= 0
   
    status = model.solve(GLPK(msg=True, options=['--ranges', 'sensitivity.txt'])) 
    print("Model Status:{}".format(pulp.LpStatus[model.status])) 
    
    #ADD IN RELATIVE WEIGHT RESTRICTIONS AND CONDITION FOR WEIGHTS TO BE POSITIVE.
    model += n3 >= n4   #Goals > SoT(%)
    model += n3 >= n5   #Goals > G-Xg
    model += n3 >= n6   #Goals > Big Chances Missed
    model += n2 >= n4   #Goals > SoT(%)
    model += n2 >= n5   #Goals > Shots on Target
    model += n2 >= n6   #Goals > SoT(%)

    # Displaying Optimal Decision Variables & Reduced Cost per Variable
    list_weights=[]
    for v in model.variables():
	      print(v.name, "=", v.varValue, "\tReduced Cost =", v.dj)
    for v in model.variables():  
        list_weights=list_weights+[v.varValue]
    for n in range(6):
        value= list_weights[n]
        weights_matrix[n,k] = value
        

    # Displaying Optimal Value of Objective Function	
    print("Objective=", pulp.value(model.objective))
	
    # Displaying Shadow Price & Slack Value per Constraint
    print ("\nSensitivity Analysis\nConstraint\t\tShadow Price\tSlack")
    for name, c in model.constraints.items():
	      print(name, ":", c, "\t", c.pi, "\t\t", c.slack)
	

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Model Status:Optimal
m1 = 0.991946 	Reduced Cost = None
n1 = 0.0 	Reduced Cost = None
n2 = 0.210489 	Reduced Cost = None
n3 = 0.8363 	Reduced Cost = None
n4 = 0.0 	Reduced Cost = None
n5 = 0.0 	Reduced Cost = None
n6 = 0.0867926 	Reduced Cost = None
Objective= 0.54301154302

Sensitivity Analysis
Constraint		Shadow Price	Slack
_C1 : 1.00811908*m1 = 1.0 	 None 		 None
_C2 : -1.00811908*m1 + 1.15189873*n1 + 0.6681*n2 + 0.4255*n3 + 0.5191*n4 + 0.566*n5 + 0.5362*n6 <= -0.0 	 None 		 None
_C3 : -1.23191475*m1 + 5.0*n1 + 2.1277*n2 + 0.7106*n3 + 2.1277*n4 + 2.1277*n5 + 2.0723*n6 <= -0.0 	 None 		 None
_C4 : -1.346414073*m1 + 1.30379747*n1 + 0.8298*n2 + 0.7106*n3 + 0.5447*n4 + 0.5064*n5 + 0.5064*n6 <= -0.0 	 None 		 None
_C5 : -2.172631935*m1 + 1.4556962*n1 + 0.6681*n2 + 0.4255*n3 + 0.6043*n4 + 0.6043*n5 + 0.5915*n6 <= -0.0 	 None 		 None
_C6 : -2.631935047*m1 + 1.81012658*n1 + 0.6681*n2 + 0.4255*

In [ ]:
efficiency_table =np.empty((52,7))
average_list =[]
for row in range(52):
    row_values=[]
    for column in range(7):
       value = ((weights_matrix[1,column]*data["Dribb Succ"][row])+(weights_matrix[2,column]*data["SCA Drib"][row])+(weights_matrix[3,column]*data["GCA Drib"][row])+(weights_matrix[4,column]*data["Carry PrgDist"][row])+(weights_matrix[5,column]*data["Carries Final Third"][row])+ (weights_matrix[6,column]*data["Carry into box"][row]))/((weights_matrix[0,column]*data["Salary NORM"][row]))
       efficiency_table[row,column]=value
       row_values=row_values+[value]
    average =mean(row_values)
    average_list =average_list+[average]

    average_list_rounded = [ '%.2f' % elem for elem in average_list ]

    player_list = ['Aaron Connolly', 'Adama TraorÃ©', 'Aleksandar MitroviÄ‡', 'Alexandre Lacazette', 'Anthony Martial', 'Anwar El Ghazi', 'Ashley Barnes', 'Bertrand TraorÃ©', 'Billy Sharp', 'Callum Wilson', 'Che Adams', 'Chris Wood', 'Christian Benteke', 'Daniel James', 'Danny Ings', 'Danny Welbeck', 'Diogo Jota', 'Dominic Calvert-Lewin', 'Edinson Cavani', 'FÃ¡bio Silva', 'Gabriel Jesus', 'Gareth Bale', 'Harry Kane', 'Jamie Vardy', 'Kelechi Iheanacho', 'Marcus Rashford', 'Mason Greenwood', 'MatÄ›j Vydra', 'Mbaye Diagne', 'Michail Antonio', 'Michy Batshuayi', 'Mohamed Salah', 'Oliver Burke', 'Oliver McBurnie', 'Olivier Giroud', 'Ollie Watkins', 'Patrick Bamford', 'Pierre-Emerick Aubameyang', 'RaÃºl JimÃ©nez', 'Raheem Sterling', 'Rhian Brewster', 'Richarlison', 'Riyad Mahrez', 'Roberto Firmino', 'SÃ©bastien Haller', 'Sadio ManÃ©', 'Son Heung-min', 'Tammy Abraham', 'Timo Werner', 'TrÃ©zÃ©guet', 'Wilfried Zaha', 'Willian JosÃ©']
for player in player_list:
    index = player_list.index(player)
    print(average_list_rounded[index])

display(efficiency_table)
efficiency_table = efficiency_table.round(decimals=2)
display(efficiency_table)

0.47
0.92
0.53
0.23
0.21
0.48
0.38
0.46
0.45
0.41
0.47
0.74
0.41
0.39
0.85
0.38
0.49
0.48
0.20
0.33
0.52
0.11
0.87
0.64
0.57
0.52
0.70
0.82
0.43
0.42
0.31
0.27
0.50
0.44
0.27
0.57
0.81
0.29
0.58
0.45
0.42
0.73
0.59
0.29
0.32
0.45
0.56
0.35
0.60
0.41
0.61
0.37


array([[0.49647351, 0.28152267, 0.53346573, 0.53346614, 0.53187641,
        0.53187612, 0.40200947],
       [0.85281364, 1.00000059, 0.99999943, 1.00000038, 1.00000108,
        0.99999977, 0.56771197],
       [0.57573809, 0.2385846 , 0.61710577, 0.61710621, 0.57233402,
        0.57233397, 0.49646788],
       [0.23036779, 0.16508039, 0.26270381, 0.26270403, 0.25181093,
        0.25181078, 0.18687191],
       [0.19016594, 0.16945121, 0.23147001, 0.2314702 , 0.24696999,
        0.24696974, 0.15688161],
       [0.45015164, 0.35528569, 0.51544441, 0.51544484, 0.58524446,
        0.58524381, 0.36040238],
       [0.37075933, 0.20343811, 0.43044985, 0.43045018, 0.44771585,
        0.4477156 , 0.33496743],
       [0.55191644, 0.42056177, 0.49970859, 0.49970903, 0.48229324,
        0.48229277, 0.3137059 ],
       [0.4395094 , 0.27168853, 0.52371136, 0.52371177, 0.50230058,
        0.50230037, 0.39517461],
       [0.39721572, 0.30807525, 0.44227106, 0.44227143, 0.47826919,
        0.47826871, 0.3

array([[0.5 , 0.28, 0.53, 0.53, 0.53, 0.53, 0.4 ],
       [0.85, 1.  , 1.  , 1.  , 1.  , 1.  , 0.57],
       [0.58, 0.24, 0.62, 0.62, 0.57, 0.57, 0.5 ],
       [0.23, 0.17, 0.26, 0.26, 0.25, 0.25, 0.19],
       [0.19, 0.17, 0.23, 0.23, 0.25, 0.25, 0.16],
       [0.45, 0.36, 0.52, 0.52, 0.59, 0.59, 0.36],
       [0.37, 0.2 , 0.43, 0.43, 0.45, 0.45, 0.33],
       [0.55, 0.42, 0.5 , 0.5 , 0.48, 0.48, 0.31],
       [0.44, 0.27, 0.52, 0.52, 0.5 , 0.5 , 0.4 ],
       [0.4 , 0.31, 0.44, 0.44, 0.48, 0.48, 0.31],
       [0.41, 0.34, 0.51, 0.51, 0.56, 0.56, 0.36],
       [0.78, 0.25, 0.86, 0.86, 0.84, 0.84, 0.73],
       [0.42, 0.19, 0.48, 0.48, 0.46, 0.46, 0.38],
       [0.36, 0.23, 0.43, 0.43, 0.47, 0.47, 0.33],
       [0.91, 0.32, 1.  , 1.  , 0.95, 0.95, 0.83],
       [0.38, 0.26, 0.43, 0.43, 0.42, 0.42, 0.31],
       [0.47, 0.26, 0.56, 0.56, 0.58, 0.58, 0.44],
       [0.45, 0.33, 0.53, 0.53, 0.57, 0.57, 0.38],
       [0.2 , 0.11, 0.23, 0.23, 0.21, 0.21, 0.17],
       [0.34, 0.22, 0.38, 0.38,

In [ ]:

	!pip install pulp
import pulp
!apt-get install -y -qq glpk-utils

from pulp import GLPK
import pandas as pd # Library to handle data
import numpy as np
from statistics import mean

data = pd.read_csv("/content/Strikers DEA Model 2.csv", encoding = 'unicode_escape', engine ='python')
#creating a list to store the optimal decision variables
weights_matrix = np.empty((7,52))
for k in range(52):  # Where k represents the number of observations
    model = pulp.LpProblem("DEA Model 1 for Strikers (Dribbling and Ball Carrying)", pulp.LpMaximize) # Create an LP maximization problem. We have 1 input, 6 outputs for goal scoring
    m1 = pulp.LpVariable("m1", lowBound=0.00000000001, upBound=None, cat='Continuous') # Create a variable m1>=0 , where m is denotes my inputs. In DEA model 1, there is just 1 input - playing time
    n1 = pulp.LpVariable("n1", lowBound=0.00000000001, upBound=None, cat='Continuous') # Create a variable n1>=0
    n2 = pulp.LpVariable("n2", lowBound=0.00000000001, upBound=None, cat='Continuous') # Create a variable n2>=0  , simmilar to above
    n3 = pulp.LpVariable("n3", lowBound=0.00000000001, upBound=None, cat='Continuous') # Create a variable n3>=0
    n4 = pulp.LpVariable("n4", lowBound=0.00000000001, upBound=None, cat='Continuous') # Create a variable n4>=0
    n5 = pulp.LpVariable("n5", lowBound=0.0000000001, upBound=None, cat='Continuous') # Create a variable n5>=0
    n6 = pulp.LpVariable("n6", lowBound=0.00000000001, upBound=None, cat='Continuous') # Create a variable n6>=0
   
    model += n1*data["Dribb Succ"][k] + n2*data["SCA Drib"][k] + n3*data["GCA Drib"][k]+ n4*data["Carry PrgDist"][k] + n5*data["Carries Final Third"][k] + n6*data["Carry into box"][k]    #objective function
    
    model += m1*data["Salary NORM"][k] == 1 #first constraint (equality)

    for i in range(52): #NUMBER OF STRIKERS
        model += n1*data["Dribb Succ"][i] + n2*data["SCA Drib"][i] + n3*data["GCA Drib"][i] + n4*data["Carry PrgDist"][i] + n5*data["Carries Final Third"][i] + n6*data["Carry into box"][i] - m1*data["Salary NORM"][i] <= 0
   
    status = model.solve(GLPK(msg=True, options=['--ranges', 'sensitivity.txt'])) 
    
    #ADD IN RELATIVE WEIGHT RESTRICTIONS AND CONDITION FOR WEIGHTS TO BE POSITIVE.
    model += n3 >= n4   #Goals > SoT(%)
    model += n3 >= n5   #Goals > G-Xg
    model += n3 >= n6   #Goals > Big Chances Missed
    model += n2 >= n4   #Goals > SoT(%)
    model += n2 >= n5   #Goals > Shots on Target
    model += n2 >= n6   #Goals > SoT(%)
        

    # Displaying Optimal Value of Objective Function	
    print(pulp.value(model.objective))


Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
0.54301154302
1.0
0.617106129783239
0.2627038885318
0.24697026249999998
0.5852437144
0.44874304124
0.7602020804
0.5312850740386967
0.5156111350999999
0.5631687693999999
0.860728822647874
0.4866879438153472
0.4820485474
0.9967424759360349
0.43458001560000004
0.5989525168400001
0.6100248953
0.225428414536598
0.3770126995806656
0.6221360624
0.13428427043000002
0.9999998507
0.8245321741999999
0.656864923
0.6534590136
0.8974855782000001
0.999999604228065
0.504145735824972
0.506892304
0.36733635494000005
0.4941026584
0.6633892774999999
0.5058117311
0.311070426720212
0.7820039106000001
0.9999993812735736
0.3752007358
0.6798216332
0.59536681568
0.47983430153750806
0.8885147150000001
0.7984344053000001
0.3755626
0.37143181090216904
0.7008403
0.6826740152000002
0.4076787476401458
0.8276806711
0.47665469964
0.7726589398
0.43298912849999993


4) DEFENDING

In [ ]:
!pip install pulp
import pulp
!apt-get install -y -qq glpk-utils

from pulp import GLPK
import pandas as pd # Library to handle data
import numpy as np
from statistics import mean

data = pd.read_csv("/content/Strikers DEA Model 2.csv", encoding = 'unicode_escape', engine ='python')
#creating a list to store the optimal decision variables
weights_matrix = np.empty((5,52))
for k in range(52):  # Where k represents the number of observations
    model = pulp.LpProblem("DEA Model 1 for Strikers (Defending)", pulp.LpMaximize) # Create an LP maximization problem. We have 1 input, 6 outputs for goal scoring
    m1 = pulp.LpVariable("m1", lowBound=0.0000000000, upBound=None, cat='Continuous') # Create a variable m1>=0 , where m is denotes my inputs. In DEA model 1, there is just 1 input - playing time
    n1 = pulp.LpVariable("n1", lowBound=0.000000000, upBound=None, cat='Continuous') # Create a variable n1>=0, where n1 represents the weight associated with output 1 - with goal scoring, it will be goals scored
    n2 = pulp.LpVariable("n2", lowBound=0.0000000000, upBound=None, cat='Continuous') # Create a variable n2>=0  , simmilar to above
    n3 = pulp.LpVariable("n3", lowBound=0.0000000000, upBound=None, cat='Continuous') # Create a variable n3>=0
    n4 = pulp.LpVariable("n4", lowBound=0.0000000000, upBound=None, cat='Continuous') # Create a variable n4>=0
   
    model += n1*data["Tackles TklW"][k] + n2*data["Pressures Succ"][k] + n3*data["Blocks and Interceptions"][k]+ n4*data["Recoveries"][k] #objective function
    
    model += m1*data["Salary NORM"][k] == 1 #first constraint (equality)

    for i in range(52): #NUMBER OF STRIKERS
        model += n1*data["Tackles TklW"][i] + n2*data["Pressures Succ"][i] + n3*data["Blocks and Interceptions"][i] + n4*data["Recoveries"][i] - m1*data["Salary NORM"][i] <= 0
   
    
    status = model.solve(GLPK(msg=True, options=['--ranges', 'sensitivity.txt'])) 
    print("Model Status:{}".format(pulp.LpStatus[model.status])) 

    #ADD IN RELATIVE WEIGHT RESTRICTIONS AND CONDITION FOR WEIGHTS TO BE POSITIVE.
    model += n3 >= n2   #Goals > SoT
    
    # Displaying Optimal Decision Variables & Reduced Cost per Variable
    list_weights=[]
    for v in model.variables():
	      print(v.name, "=", v.varValue, "\tReduced Cost =", v.dj)
    for v in model.variables():  
        list_weights=list_weights+[v.varValue]
    for n in range(4):
        value= list_weights[n]
        weights_matrix[n,k] = value
        

    # Displaying Optimal Value of Objective Function	
    print("Objective=", pulp.value(model.objective))
	
    # Displaying Shadow Price & Slack Value per Constraint
    print ("\nSensitivity Analysis\nConstraint\t\tShadow Price\tSlack")
    for name, c in model.constraints.items():
	      print(name, ":", c, "\t", c.pi, "\t\t", c.slack)
   

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Model Status:Optimal
m1 = 0.991946 	Reduced Cost = None
n1 = 0.388505 	Reduced Cost = None
n2 = 0.180189 	Reduced Cost = None
n3 = 0.230426 	Reduced Cost = None
n4 = 0.0133867 	Reduced Cost = None
Objective= 0.5079361925

Sensitivity Analysis
Constraint		Shadow Price	Slack
_C1 : 1.00811908*m1 = 1.0 	 None 		 None
_C2 : -1.00811908*m1 + 0.6468*n1 + 0.7021*n2 + 0.5319*n3 + 0.566*n4 <= -0.0 	 None 		 None
_C3 : -1.23191475*m1 + 1.634*n1 + 1.4085*n2 + 1.3447*n3 + 1.7574*n4 <= -0.0 	 None 		 None
_C4 : -1.346414073*m1 + 0.8638*n1 + 1.0298*n2 + 0.8596*n3 + 0.8085*n4 <= -0.0 	 None 		 None
_C5 : -2.172631935*m1 + 1.4128*n1 + 1.4085*n2 + 1.1277*n3 + 1.1957*n4 <= -0.0 	 None 		 None
_C6 : -2.631935047*m1 + 0.4255*n1 + 0.7234*n2 + 0.9915*n3 + 0.8681*n4 <= -0.0 	 None 		 None
_C7 : -1.149945873*m1 + 0.9191*n1 + 0.8255*n2 + 0.8596*n3 + 1.0383*n4 <= -0.0 	 None 		 None
_C8 : -1.211096076*m1 + 0.7021*n

In [ ]:
efficiency_table =np.empty((52,5))
average_list =[]
for row in range(52):
    row_values=[]
    for column in range(5):
       value = ((weights_matrix[1,column]*data["Tackles TklW"][row])+(weights_matrix[2,column]*data["Pressures Succ"][row])+(weights_matrix[3,column]*data["Blocks and Interceptions"][row])+(weights_matrix[4,column]*data["Recoveries"][row]))/((weights_matrix[0,column]*data["Salary NORM"][row]))
       efficiency_table[row,column]=value
       row_values=row_values+[value]
    average =mean(row_values)
    average_list =average_list+[average]

    average_list_rounded = [ '%.2f' % elem for elem in average_list ]

    player_list = ['Aaron Connolly', 'Adama TraorÃ©', 'Aleksandar MitroviÄ‡', 'Alexandre Lacazette', 'Anthony Martial', 'Anwar El Ghazi', 'Ashley Barnes', 'Bertrand TraorÃ©', 'Billy Sharp', 'Callum Wilson', 'Che Adams', 'Chris Wood', 'Christian Benteke', 'Daniel James', 'Danny Ings', 'Danny Welbeck', 'Diogo Jota', 'Dominic Calvert-Lewin', 'Edinson Cavani', 'FÃ¡bio Silva', 'Gabriel Jesus', 'Gareth Bale', 'Harry Kane', 'Jamie Vardy', 'Kelechi Iheanacho', 'Marcus Rashford', 'Mason Greenwood', 'MatÄ›j Vydra', 'Mbaye Diagne', 'Michail Antonio', 'Michy Batshuayi', 'Mohamed Salah', 'Oliver Burke', 'Oliver McBurnie', 'Olivier Giroud', 'Ollie Watkins', 'Patrick Bamford', 'Pierre-Emerick Aubameyang', 'RaÃºl JimÃ©nez', 'Raheem Sterling', 'Rhian Brewster', 'Richarlison', 'Riyad Mahrez', 'Roberto Firmino', 'SÃ©bastien Haller', 'Sadio ManÃ©', 'Son Heung-min', 'Tammy Abraham', 'Timo Werner', 'TrÃ©zÃ©guet', 'Wilfried Zaha', 'Willian JosÃ©']
for player in player_list:
    index = player_list.index(player)
    print(average_list_rounded[index])

display(efficiency_table)
efficiency_table = efficiency_table.round(decimals=2)
display(efficiency_table)

0.39
0.78
0.43
0.38
0.19
0.50
0.43
0.64
0.34
0.46
0.78
0.57
0.33
0.47
0.66
0.48
0.38
0.73
0.23
0.34
0.53
0.12
0.38
0.32
0.43
0.31
0.40
0.46
0.35
0.48
0.24
0.32
0.62
0.54
0.21
0.64
0.74
0.25
0.33
0.27
0.51
0.78
0.42
0.59
0.26
0.78
0.57
0.30
0.39
0.65
0.60
0.31


array([[0.50035948, 0.        , 0.48203577, 0.49984251, 0.46441928],
       [0.9807481 , 0.        , 0.98822559, 0.98297673, 0.93102813],
       [0.5385142 , 0.        , 0.56290262, 0.51144392, 0.55416955],
       [0.49302164, 0.        , 0.47566289, 0.49682222, 0.45318902],
       [0.20075745, 0.        , 0.29782687, 0.14283359, 0.30933205],
       [0.61708153, 0.        , 0.66019866, 0.59723258, 0.63106468],
       [0.51003205, 0.        , 0.58536959, 0.46053397, 0.58079397],
       [0.6898164 , 0.        , 0.9862474 , 0.52848304, 0.99999814],
       [0.4581958 , 0.        , 0.39970574, 0.48261141, 0.37410728],
       [0.58158355, 0.        , 0.57284652, 0.56110575, 0.56903942],
       [0.98377747, 0.        , 0.99999934, 0.9351339 , 0.9955796 ],
       [0.68386561, 0.        , 0.77246633, 0.61768461, 0.77157169],
       [0.40170709, 0.        , 0.44030877, 0.37852513, 0.42817043],
       [0.55899959, 0.        , 0.64861678, 0.51713327, 0.62668743],
       [0.73373003, 0.        , 0.

array([[0.5 , 0.  , 0.48, 0.5 , 0.46],
       [0.98, 0.  , 0.99, 0.98, 0.93],
       [0.54, 0.  , 0.56, 0.51, 0.55],
       [0.49, 0.  , 0.48, 0.5 , 0.45],
       [0.2 , 0.  , 0.3 , 0.14, 0.31],
       [0.62, 0.  , 0.66, 0.6 , 0.63],
       [0.51, 0.  , 0.59, 0.46, 0.58],
       [0.69, 0.  , 0.99, 0.53, 1.  ],
       [0.46, 0.  , 0.4 , 0.48, 0.37],
       [0.58, 0.  , 0.57, 0.56, 0.57],
       [0.98, 0.  , 1.  , 0.94, 1.  ],
       [0.68, 0.  , 0.77, 0.62, 0.77],
       [0.4 , 0.  , 0.44, 0.38, 0.43],
       [0.56, 0.  , 0.65, 0.52, 0.63],
       [0.73, 0.  , 0.99, 0.59, 0.99],
       [0.55, 0.  , 0.67, 0.49, 0.67],
       [0.48, 0.  , 0.48, 0.47, 0.47],
       [0.87, 0.  , 1.  , 0.77, 1.  ],
       [0.3 , 0.  , 0.28, 0.31, 0.27],
       [0.43, 0.  , 0.44, 0.4 , 0.45],
       [0.63, 0.  , 0.73, 0.57, 0.73],
       [0.14, 0.  , 0.16, 0.12, 0.16],
       [0.43, 0.  , 0.54, 0.37, 0.55],
       [0.39, 0.  , 0.43, 0.35, 0.43],
       [0.52, 0.  , 0.59, 0.49, 0.57],
       [0.36, 0.  , 0.44,

In [ ]:
!pip install pulp
import pulp
!apt-get install -y -qq glpk-utils

from pulp import GLPK
import pandas as pd # Library to handle data
import numpy as np
from statistics import mean

data = pd.read_csv("/content/Strikers DEA Model 2.csv", encoding = 'unicode_escape', engine ='python')
#creating a list to store the optimal decision variables
weights_matrix = np.empty((5,52))
for k in range(52):  # Where k represents the number of observations
    model = pulp.LpProblem("DEA Model 1 for Strikers (Defending)", pulp.LpMaximize) # Create an LP maximization problem. We have 1 input, 6 outputs for goal scoring
    m1 = pulp.LpVariable("m1", lowBound=0.0000000000, upBound=None, cat='Continuous') # Create a variable m1>=0 , where m is denotes my inputs. In DEA model 1, there is just 1 input - playing time
    n1 = pulp.LpVariable("n1", lowBound=0.000000000, upBound=None, cat='Continuous') # Create a variable n1>=0, where n1 represents the weight associated with output 1 - with goal scoring, it will be goals scored
    n2 = pulp.LpVariable("n2", lowBound=0.0000000000, upBound=None, cat='Continuous') # Create a variable n2>=0  , simmilar to above
    n3 = pulp.LpVariable("n3", lowBound=0.0000000000, upBound=None, cat='Continuous') # Create a variable n3>=0
    n4 = pulp.LpVariable("n4", lowBound=0.0000000000, upBound=None, cat='Continuous') # Create a variable n4>=0
   
    model += n1*data["Tackles TklW"][k] + n2*data["Pressures Succ"][k] + n3*data["Blocks and Interceptions"][k]+ n4*data["Recoveries"][k] #objective function
    
    model += m1*data["Salary NORM"][k] == 1 #first constraint (equality)

    for i in range(52): #NUMBER OF STRIKERS
        model += n1*data["Tackles TklW"][i] + n2*data["Pressures Succ"][i] + n3*data["Blocks and Interceptions"][i] + n4*data["Recoveries"][i] - m1*data["Salary NORM"][i] <= 0
   
    
    status = model.solve(GLPK(msg=True, options=['--ranges', 'sensitivity.txt'])) 

    #ADD IN RELATIVE WEIGHT RESTRICTIONS AND CONDITION FOR WEIGHTS TO BE POSITIVE.
    model += n3 >= n2   #Goals > SoT
        

    # Displaying Optimal Value of Objective Function	
    print(pulp.value(model.objective))
	

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
0.5079361925
0.9999992628000001
0.56290294674
0.503389402485
0.30933238531999996
0.6662502593
0.6031427113
1.0000000884999998
0.48902274645999994
0.6422900614
0.9999998295999999
0.77246758229
0.442774177586
0.6535372530000001
0.9967590184999999
0.6743253117
0.49939111010000004
1.00000095021
0.31519490345
0.4871219991
0.72612980137
0.16651798995999997
0.56167313328
0.44002856926
0.5878609939199999
0.4825851671
0.5820336567000001
0.62441852076
0.5066559278
0.71079813735
0.33986734430000004
0.6498204888
0.8031103316900001
0.7601394332
0.2931280851
0.8985040303549999
0.9999996993000001
0.37164038015999995
0.4717656613000001
0.3461629776
0.6794806518000001
0.9999994604
0.5693534902999999
0.8361563122
0.3505074373
0.99999916874
0.81902084852
0.40714571089999996
0.5583833682
0.8959411518
0.7733409891099999
0.4607712557


# **DEA MODEL 3**

(This is not needed)
(Includes Team-mate ability as an additional input)

1) Goal Scoring

In [ ]:
!pip install pulp
import pulp
!apt-get install -y -qq glpk-utils

from pulp import GLPK
import pandas as pd # Library to handle data
import numpy as np
from statistics import mean

data = pd.read_csv("/content/DEA M2.csv", encoding = 'unicode_escape', engine ='python')
#creating a list to store the optimal decision variables
weights_matrix = np.empty((7,51))
for k in range(51):  # Where k represents the number of observations
    model = pulp.LpProblem("DEA Model 1 for Strikers (Goal-Scoring)", pulp.LpMaximize) # Create an LP maximization problem. We have 1 input, 6 outputs for goal scoring
    n1 = pulp.LpVariable("n1", lowBound=0.0000001, upBound=None, cat='Continuous') # Create a variable n1>=0, where n1 represents the weight associated with output 1 - with goal scoring, it will be goals scored
    n2 = pulp.LpVariable("n2", lowBound=0.0000001, upBound=None, cat='Continuous') # Create a variable n2>=0  , simmilar to above
    n3 = pulp.LpVariable("n3", lowBound=0.0000001, upBound=None, cat='Continuous') # Create a variable n4>=0
    n5 = pulp.LpVariable("n5", lowBound=0.0000001, upBound=None, cat='Continuous') # Create a variable n6>=0
    m1 = pulp.LpVariable("m1", lowBound=0.0000001, upBound=None, cat='Continuous') # Create a variable m1>=0 , where m is denotes my inputs. In DEA model 2, there is just 1 input - Salary
    m2 = pulp.LpVariable("m2", lowBound=0.0000001, upBound=None, cat='Continuous') # Create a variable m1>=0 , where m is denotes my inputs. In DEA model 2, there is just 1 input - Salary


    model += n1*data["Gls"][k] + n2*data["SoT"][k] + n3*data["G-xG"][k] + n5*data["GCA"][k]  #objective function
    
    model += m1*data["Minutes Played"][k] + m2*data["Team Points"][k] == 1 #first constraint (equality)

    for i in range(51): #NUMBER OF STRIKERS
        model += n1*data["Gls"][i] + n2*data["SoT"][i] + n3*data["G-xG"][i] + n5*data["GCA"][i] -  m1*data["Minutes Played"][i] - m2*data["Team Points"][i]<= 0
   
    status = model.solve(GLPK(msg=True, options=['--ranges', 'sensitivity.txt'])) 
    print("Model Status:{}".format(pulp.LpStatus[model.status])) 
    
    #ADD IN RELATIVE WEIGHT RESTRICTIONS AND CONDITION FOR WEIGHTS TO BE POSITIVE.
    model += n1*data["Gls"][k] >= n2*data["SoT"][k]   #Goals > SoT
    model += n1*data["Gls"][k] >= n3*data["G-xG"][k]   #Goals > G-Xg
    model += n3*data["G-xG"][k] >= n2*data["SoT"][k]   #Goals > Shots on Target
    model += n5*data["GCA"][k]>= n2*data["SoT"][k]  #Goals > Shots on Target


    # Displaying Optimal Decision Variables & Reduced Cost per Variable
    list_weights=[]
    for v in model.variables():
	      print(v.name, "=", v.varValue, "\tReduced Cost =", v.dj)
    for v in model.variables():  
        list_weights=list_weights+[v.varValue]
    for n in range(4):
        value= list_weights[n]
        weights_matrix[n,k] = value
        
    # Displaying Optimal Value of Objective Function	
    print("Objective=", pulp.value(model.objective))
	
    # Displaying Shadow Price & Slack Value per Constraint
    print ("\nSensitivity Analysis\nConstraint\t\tShadow Price\tSlack")
    for name, c in model.constraints.items():
	      print(name, ":", c, "\t", c.pi, "\t\t", c.slack)

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Model Status:Optimal
m1 = 0.00999991 	Reduced Cost = None
m2 = 1e-07 	Reduced Cost = None
n1 = 1e-07 	Reduced Cost = None
n2 = 1e-07 	Reduced Cost = None
n3 = 0.583863 	Reduced Cost = None
n5 = 1.17441 	Reduced Cost = None
Objective= 0.9454572506059999

Sensitivity Analysis
Constraint		Shadow Price	Slack
_C1 : 100.0*m1 + 86*m2 = 1.0 	 None 		 None
_C2 : -100.0*m1 - 86*m2 + 0.46178*n1 + 1.12878*n2 + 0.17445*n3 + 0.71832*n5 <= -0.0 	 None 		 None
_C3 : -159.77424*m1 - 62*m2 + 0.87224*n1 + 1.79579*n2 + 0.34377*n3 + 0.76963*n5 <= -0.0 	 None 		 None
_C4 : -158.13238*m1 - 62*m2 + 1.18009*n1 + 2.41149*n2 + 0.12827*n3 + 1.28271*n5 <= -0.0 	 None 		 None
_C5 : -133.50436*m1 - 67*m2 + 0.30785*n1 + 1.59056*n2 - 0.30272*n3 + 0.97486*n5 <= -0.0 	 None 		 None
_C6 : -145.61313*m1 - 69*m2 + 0.46178*n1 + 1.64187*n2 - 0.18471*n3 + 0.46178*n5 <= -0.0 	 None 		 None
_C7 : -136.8394*m1 - 43*m2 + 0.46178*n1 

In [ ]:
efficiency_table =np.empty((51,7))
average_list =[]
for row in range(51):
    row_values=[]
    for column in range(7):
       value = ((weights_matrix[2,column]*data["Gls"][row])+(weights_matrix[3,column]*data["SoT"][row])+(weights_matrix[4,column]*data["G-xG"][row])+(weights_matrix[5,column]*data["Big Chances Missed"][row])+(weights_matrix[6,column]*data["GCA"][row]))/((weights_matrix[0,column]*data["Minutes Played"][row])+ (weights_matrix[1,column]*data["Team Points"][row]))
       efficiency_table[row,column]=value
       row_values=row_values+[value]
    average =mean(row_values)
    average_list =average_list+[average]

    average_list_rounded = [ '%.2f' % elem for elem in average_list ]

    player_list = ['Aaron Connolly', 'Adama TraorÃ©', 'Aleksandar MitroviÄ‡', 'Alexandre Lacazette', 'Anthony Martial', 'Anwar El Ghazi', 'Ashley Barnes', 'Bertrand TraorÃ©', 'Billy Sharp', 'Callum Wilson', 'Che Adams', 'Chris Wood', 'Christian Benteke', 'Daniel James', 'Danny Ings', 'Danny Welbeck', 'Diogo Jota', 'Dominic Calvert-Lewin', 'Edinson Cavani', 'FÃ¡bio Silva', 'Gabriel Jesus', 'Gareth Bale', 'Harry Kane', 'Jamie Vardy', 'Kelechi Iheanacho', 'Marcus Rashford', 'Mason Greenwood', 'MatÄ›j Vydra', 'Mbaye Diagne', 'Michail Antonio', 'Michy Batshuayi', 'Mohamed Salah', 'Oliver Burke', 'Oliver McBurnie', 'Olivier Giroud', 'Ollie Watkins', 'Patrick Bamford', 'Pierre-Emerick Aubameyang', 'RaÃºl JimÃ©nez', 'Raheem Sterling', 'Rhian Brewster', 'Richarlison', 'Riyad Mahrez', 'Roberto Firmino', 'SÃ©bastien Haller', 'Sadio ManÃ©', 'Son Heung-min', 'Tammy Abraham', 'Timo Werner', 'TrÃ©zÃ©guet', 'Wilfried Zaha']
for player in player_list:
    index = player_list.index(player)
    print(average_list_rounded[index])

display(efficiency_table)
efficiency_table = efficiency_table.round(decimals=2)
display(efficiency_table)

0.38
0.26
0.50
0.46
0.35
0.51
0.38
0.38
0.43
0.40
0.49
0.57
0.62
0.25
0.49
0.40
0.51
0.57
0.36
0.41
0.28
0.52
0.58
0.38
0.49
0.41
0.37
0.33
0.43
0.40
0.35
0.54
0.36
0.46
0.33
0.52
0.54
0.34
0.42
0.34
0.39
0.40
0.34
0.38
0.32
0.42
0.46
0.35
0.38
0.33
0.39


array([[0.46509629, 0.14385657, 0.1930492 , 0.68978735, 0.00355831,
        0.67358238, 0.46509682],
       [0.29436317, 0.17264981, 0.23168854, 0.45685472, 0.00173893,
        0.39283251, 0.29436355],
       [0.59651534, 0.32977121, 0.44253882, 0.77896379, 0.00357914,
        0.77709666, 0.59651606],
       [0.52769676, 0.20004922, 0.2684573 , 0.85906036, 0.00362102,
        0.8366956 , 0.52769739],
       [0.49908865, 0.14511664, 0.19474029, 0.52414591, 0.00397638,
        0.61476185, 0.49908916],
       [0.62258831, 0.22852886, 0.3066758 , 0.87930021, 0.00433702,
        0.89270802, 0.62258902],
       [0.4550221 , 0.1898244 , 0.2547361 , 0.66087976, 0.00299728,
        0.64028954, 0.45502264],
       [0.45512279, 0.20856027, 0.27987885, 0.64628855, 0.00289451,
        0.62752619, 0.45512333],
       [0.40162575, 0.17685551, 0.23733206, 0.99999948, 0.00259163,
        0.77326057, 0.40162632],
       [0.39657164, 0.19705597, 0.26444043, 0.82303281, 0.0024554 ,
        0.73785171, 0.3

array([[0.47, 0.14, 0.19, 0.69, 0.  , 0.67, 0.47],
       [0.29, 0.17, 0.23, 0.46, 0.  , 0.39, 0.29],
       [0.6 , 0.33, 0.44, 0.78, 0.  , 0.78, 0.6 ],
       [0.53, 0.2 , 0.27, 0.86, 0.  , 0.84, 0.53],
       [0.5 , 0.15, 0.19, 0.52, 0.  , 0.61, 0.5 ],
       [0.62, 0.23, 0.31, 0.88, 0.  , 0.89, 0.62],
       [0.46, 0.19, 0.25, 0.66, 0.  , 0.64, 0.46],
       [0.46, 0.21, 0.28, 0.65, 0.  , 0.63, 0.46],
       [0.4 , 0.18, 0.24, 1.  , 0.  , 0.77, 0.4 ],
       [0.4 , 0.2 , 0.26, 0.82, 0.  , 0.74, 0.4 ],
       [0.55, 0.34, 0.45, 0.77, 0.  , 0.74, 0.55],
       [0.63, 0.43, 0.57, 0.88, 0.  , 0.87, 0.63],
       [0.75, 0.34, 0.46, 1.  , 0.  , 1.  , 0.75],
       [0.3 , 0.07, 0.09, 0.49, 0.  , 0.47, 0.3 ],
       [0.52, 0.28, 0.37, 0.93, 0.  , 0.83, 0.52],
       [0.45, 0.2 , 0.27, 0.75, 0.  , 0.7 , 0.45],
       [0.69, 0.18, 0.24, 0.84, 0.01, 0.93, 0.69],
       [0.67, 0.34, 0.45, 0.89, 0.  , 0.93, 0.67],
       [0.41, 0.11, 0.15, 0.7 , 0.  , 0.7 , 0.41],
       [0.51, 0.2 , 0.26, 0.68,

In [ ]:
!pip install pulp
import pulp
!apt-get install -y -qq glpk-utils

from pulp import GLPK
import pandas as pd # Library to handle data
import numpy as np
from statistics import mean

data = pd.read_csv("/content/DEA M2.csv", encoding = 'unicode_escape', engine ='python')
#creating a list to store the optimal decision variables
weights_matrix = np.empty((7,51))
for k in range(51):  # Where k represents the number of observations
    model = pulp.LpProblem("DEA Model 1 for Strikers (Goal-Scoring)", pulp.LpMaximize) # Create an LP maximization problem. We have 1 input, 6 outputs for goal scoring
    n1 = pulp.LpVariable("n1", lowBound=0.0000001, upBound=None, cat='Continuous') # Create a variable n1>=0, where n1 represents the weight associated with output 1 - with goal scoring, it will be goals scored
    n2 = pulp.LpVariable("n2", lowBound=0.0000001, upBound=None, cat='Continuous') # Create a variable n2>=0  , simmilar to above
    n3 = pulp.LpVariable("n3", lowBound=0.0000001, upBound=None, cat='Continuous') # Create a variable n4>=0
    n5 = pulp.LpVariable("n5", lowBound=0.0000001, upBound=None, cat='Continuous') # Create a variable n6>=0
    m1 = pulp.LpVariable("m1", lowBound=0.0000001, upBound=None, cat='Continuous') # Create a variable m1>=0 , where m is denotes my inputs. In DEA model 2, there is just 1 input - Salary
    m2 = pulp.LpVariable("m2", lowBound=0.0000001, upBound=None, cat='Continuous') # Create a variable m1>=0 , where m is denotes my inputs. In DEA model 2, there is just 1 input - Salary


    model += n1*data["Gls"][k] + n2*data["SoT"][k] + n3*data["G-xG"][k] + n5*data["GCA"][k]  #objective function
    
    model += m1*data["Minutes Played"][k] + m2*data["Team Points"][k] == 1 #first constraint (equality)

    for i in range(51): #NUMBER OF STRIKERS
        model += n1*data["Gls"][i] + n2*data["SoT"][i] + n3*data["G-xG"][i] + n5*data["GCA"][i] -  m1*data["Minutes Played"][i] - m2*data["Team Points"][i]<= 0
   
    status = model.solve(GLPK(msg=True, options=['--ranges', 'sensitivity.txt']))
    
    #ADD IN RELATIVE WEIGHT RESTRICTIONS AND CONDITION FOR WEIGHTS TO BE POSITIVE.
    model += n1*data["Gls"][k] >= n2*data["SoT"][k]   #Goals > SoT
    model += n1*data["Gls"][k] >= n3*data["G-xG"][k]   #Goals > G-Xg
    model += n3*data["G-xG"][k] >= n2*data["SoT"][k]   #Goals > Shots on Target
    model += n5*data["GCA"][k]>= n2*data["SoT"][k]  #Goals > Shots on Target
        
    # Displaying Optimal Value of Objective Function	
    print(pulp.value(model.objective))


Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
0.9454572506059999
0.9999997721660001
0.9999998052750001
0.900198556749
0.653323514737
0.8568578628450001
0.999999883779
0.9521753180160001
0.364015562676
0.737839440469
0.9055371830429999
0.681842384426
0.43599437204100006
0.7291807397730001
0.7657128846750001
0.911579518301
0.49033143456600004
0.657328230597
0.378906608078
0.999999364931
0.725786987709
0.86798876714
0.537368278509
0.30863809907900003
0.793304861715
0.6024031012050001
0.793737625186
0.9624331426689999
0.432097057578
0.539516406165
0.5020903901459999
0.925658737125
0.9470726805379999
0.783337627711
0.5335571531229999
0.937980461648
0.7241359679249999
0.6921819426829999
0.7573542411240001
0.6394460367039999
0.694464125892
0.5892497665349999
0.57124734512
0.6120042289959999
0.478799281932
1.0000008523169999
0.987524789267
1.000000741622
0.268360727023
0.481952973958
0.630738033381


DEA MODEL 3, Creativity

In [ ]:
from pulp import GLPK
import pandas as pd # Library to handle data
import numpy as np
from statistics import mean

data = pd.read_csv("/content/Strikers DEA Model 2 and 3.csv", encoding = 'unicode_escape', engine ='python')
#creating a list to store the optimal decision variables
weights_matrix = np.empty((7,51))
for k in range(51):  # Where k represents the number of observations
    model = pulp.LpProblem("DEA Model 1 for Strikers (Creativity)", pulp.LpMaximize) # Create an LP maximization problem. We have 1 input, 6 outputs for goal scoring
    n1 = pulp.LpVariable("n1", lowBound=0.000001, upBound=None, cat='Continuous') # Create a variable n1>=0, where n1 represents the weight associated with output 1 - with goal scoring, it will be goals scored
    n2 = pulp.LpVariable("n2", lowBound=0.000001, upBound=None, cat='Continuous') # Create a variable n2>=0  , simmilar to above
    n3 = pulp.LpVariable("n3", lowBound=0.000001, upBound=None, cat='Continuous') # Create a variable n3>=0
    n4 = pulp.LpVariable("n4", lowBound=0.000001, upBound=None, cat='Continuous') # Create a variable n4>=0
    n5 = pulp.LpVariable("n5", lowBound=0.000001, upBound=None, cat='Continuous') # Create a variable n4>=0
    m1 = pulp.LpVariable("m1", lowBound=0.000001, upBound=None, cat='Continuous') # Create a variable m1>=0 , where m is denotes my inputs. In DEA model 1, there is just 1 input - playing time
    m2 = pulp.LpVariable("m2", lowBound=0.000001, upBound=None, cat='Continuous') # Create a variable m1>=0 , where m is denotes my inputs. In DEA model 1, there is just 1 input - playing time

    model += n1*data["xA"][k] + n2*data["KP"][k] + n3*data["PPA"][k]+ n4*data["SCA"][k] + n5*data["Progressive Passes"][k]  #objective function
    
    model += m1*data["Salary NORM"][k] + m2*data["Teammate Ability"][k]  == 1 #first constraint (equality)

    for i in range(51): #NUMBER OF STRIKERS
        model += n1*data["xA"][i] + n2*data["KP"][i] + n3*data["PPA"][i] + n4*data["SCA"][i] + n5*data["Progressive Passes"][i] - m1*data["Salary NORM"][i] - m2*data["Teammate Ability"][i] <= 0
   
    status = model.solve(GLPK(msg=True, options=['--ranges', 'sensitivity.txt'])) 
    print("Model Status:{}".format(pulp.LpStatus[model.status])) 
    
    #ADD IN RELATIVE WEIGHT RESTRICTIONS AND CONDITION FOR WEIGHTS TO BE POSITIVE.
    model += n1 >= n3 #xA > PPA
    model += n2 >= n3  #KP > PPA
    model += n4 >= n3   #SCA > PPA
    model += n1 >= n2   #SCA > PPA

    # Displaying Optimal Decision Variables & Reduced Cost per Variable
    list_weights=[]
    for v in model.variables():
	      print(v.name, "=", v.varValue, "\tReduced Cost =", v.dj)
    for v in model.variables():  
        list_weights=list_weights+[v.varValue]
    for n in range(5):
        value= list_weights[n]
        weights_matrix[n,k] = value
        
    # Displaying Optimal Value of Objective Function	
    print("Objective=", pulp.value(model.objective))
	
    # Displaying Shadow Price & Slack Value per Constraint
    print ("\nSensitivity Analysis\nConstraint\t\tShadow Price\tSlack")
    for name, c in model.constraints.items():
	      print(name, ":", c, "\t", c.pi, "\t\t", c.slack)
	


Model Status:Optimal
m1 = 0.991906 	Reduced Cost = None
m2 = 1e-06 	Reduced Cost = None
n1 = 0.351283 	Reduced Cost = None
n2 = 0.207225 	Reduced Cost = None
n3 = 0.372559 	Reduced Cost = None
n4 = 1e-06 	Reduced Cost = None
n5 = 1e-06 	Reduced Cost = None
Objective= 0.4005837700400759

Sensitivity Analysis
Constraint		Shadow Price	Slack
_C1 : 1.00811908*m1 + 41*m2 = 1.0 	 None 		 None
_C2 : -1.00811908*m1 - 41*m2 + 0.4255*n1 + 0.4468*n2 + 0.4255*n3 + 0.5277*n4 + 0.341340076*n5 <= -0.0 	 None 		 None
_C3 : -1.23191475*m1 - 45*m2 + 1.4426*n1 + 1.6383*n2 + 1.0085*n3 + 1.9702*n4 + 2.140430351*n5 <= -0.0 	 None 		 None
_C4 : -1.346414073*m1 - 28*m2 + 0.8936*n1 + 0.8468*n2 + 0.7064*n3 + 1.0255*n4 + 1.283880171*n5 <= -0.0 	 None 		 None
_C5 : -2.172631935*m1 - 61*m2 + 0.9149*n1 + 0.7532*n2 + 0.8936*n3 + 1.0128*n4 + 2.152886115*n5 <= -0.0 	 None 		 None
_C6 : -2.631935047*m1 - 74*m2 + 0.7787*n1 + 0.6809*n2 + 0.7532*n3 + 0.9702*n4 + 2.614864865*n5 <= -0.0 	 None 		 None
_C7 : -1.149945873*m1 -

In [ ]:
efficiency_table =np.empty((51,7))
average_list =[]
for row in range(51):
    row_values=[]
    for column in range(7):
       value = ((weights_matrix[2,column]*data["xA"][row])+(weights_matrix[3,column]*data["KP"][row])+(weights_matrix[4,column]*data["PPA"][row])+(weights_matrix[5,column]*data["SCA"][row])+(weights_matrix[6,column]*data["Progressive Passes"][row]))/((weights_matrix[0,column]*data["Salary NORM"][row])+(weights_matrix[1,column]*data["Teammate Ability"][row]))
       efficiency_table[row,column]=value
       row_values=row_values+[value]
    average =mean(row_values)
    average_list =average_list+[average]

    average_list_rounded = [ '%.2f' % elem for elem in average_list ]

    player_list = ['Aaron Connolly', 'Adama Traore', 'Aleksandar Mitrovic', 'Alexandre Lacazette', 'Anthony Martial', 'Anwar El Ghazi', 'Ashley Barnes', 'Bertrand TraorÃ©', 'Billy Sharp', 'Callum Wilson', 'Che Adams', 'Chris Wood', 'Christian Benteke', 'Daniel James', 'Danny Ings', 'Danny Welbeck', 'Diogo Jota', 'Dominic Calvert-Lewin', 'Edinson Cavani', 'FÃ¡bio Silva', 'Gabriel Jesus', 'Gareth Bale', 'Harry Kane', 'Jamie Vardy', 'Kelechi Iheanacho', 'Marcus Rashford', 'Mason Greenwood', 'MatÄ›j Vydra', 'Mbaye Diagne', 'Michail Antonio', 'Michy Batshuayi', 'Mohamed Salah', 'Oliver Burke', 'Oliver McBurnie', 'Olivier Giroud', 'Ollie Watkins', 'Patrick Bamford', 'Pierre-Emerick Aubameyang', 'RaÃºl JimÃ©nez', 'Raheem Sterling', 'Rhian Brewster', 'Richarlison', 'Riyad Mahrez', 'Roberto Firmino', 'SÃ©bastien Haller', 'Sadio ManÃ©', 'Son Heung-min', 'Tammy Abraham', 'Timo Werner', 'TrÃ©zÃ©guet', 'Wilfried Zaha']
for player in player_list:
    index = player_list.index(player)
    print(average_list_rounded[index])

display(efficiency_table)
efficiency_table = efficiency_table.round(decimals=2)
display(efficiency_table)

0.25
0.67
0.55
0.30
0.21
0.40
0.32
0.46
0.40
0.37
0.66
0.39
0.31
0.24
0.43
0.38
0.25
0.33
0.23
0.26
0.29
0.21
0.52
0.33
0.37
0.42
0.27
0.38
0.47
0.30
0.26
0.57
0.56
0.58
0.17
0.49
0.42
0.31
0.29
0.30
0.47
0.35
0.46
0.48
0.22
0.62
0.60
0.20
0.40
0.29
0.51


array([[0.40058276, 0.29932775, 0.32247164, 0.34357046, 0.11144668,
        0.07300093, 0.2256851 ],
       [0.99999566, 0.99999596, 0.88084641, 0.83048203, 0.3092064 ,
        0.2025384 , 0.47907789],
       [0.56348588, 0.83069199, 0.90032491, 0.77397556, 0.17525293,
        0.11479268, 0.4788382 ],
       [0.37603199, 0.33915505, 0.45411632, 0.45194211, 0.1111937 ,
        0.07283392, 0.29816925],
       [0.26630918, 0.25273729, 0.31854987, 0.31515442, 0.07812461,
        0.05117305, 0.20723105],
       [0.68873865, 0.4462705 , 0.47024971, 0.51166282, 0.19248339,
        0.12608376, 0.33231895],
       [0.43793919, 0.44652118, 0.43553699, 0.4471165 , 0.11411566,
        0.0747482 , 0.30343251],
       [0.73723226, 0.55039687, 0.57275517, 0.61115818, 0.20373917,
        0.13345552, 0.40054631],
       [0.43468624, 0.50814691, 0.65223959, 0.60526224, 0.12977371,
        0.08500348, 0.39764302],
       [0.51428531, 0.40261133, 0.52347127, 0.5258734 , 0.1602247 ,
        0.10495101, 0.3

array([[0.4 , 0.3 , 0.32, 0.34, 0.11, 0.07, 0.23],
       [1.  , 1.  , 0.88, 0.83, 0.31, 0.2 , 0.48],
       [0.56, 0.83, 0.9 , 0.77, 0.18, 0.11, 0.48],
       [0.38, 0.34, 0.45, 0.45, 0.11, 0.07, 0.3 ],
       [0.27, 0.25, 0.32, 0.32, 0.08, 0.05, 0.21],
       [0.69, 0.45, 0.47, 0.51, 0.19, 0.13, 0.33],
       [0.44, 0.45, 0.44, 0.45, 0.11, 0.07, 0.3 ],
       [0.74, 0.55, 0.57, 0.61, 0.2 , 0.13, 0.4 ],
       [0.43, 0.51, 0.65, 0.61, 0.13, 0.09, 0.4 ],
       [0.51, 0.4 , 0.52, 0.53, 0.16, 0.1 , 0.33],
       [1.  , 0.72, 0.92, 0.88, 0.35, 0.23, 0.49],
       [0.52, 0.61, 0.56, 0.49, 0.17, 0.11, 0.28],
       [0.35, 0.43, 0.46, 0.46, 0.09, 0.06, 0.33],
       [0.48, 0.21, 0.27, 0.31, 0.13, 0.09, 0.21],
       [0.56, 0.54, 0.63, 0.62, 0.16, 0.11, 0.41],
       [0.51, 0.57, 0.53, 0.48, 0.16, 0.11, 0.27],
       [0.42, 0.24, 0.32, 0.35, 0.12, 0.08, 0.23],
       [0.63, 0.34, 0.38, 0.41, 0.19, 0.13, 0.25],
       [0.31, 0.25, 0.34, 0.33, 0.1 , 0.07, 0.2 ],
       [0.34, 0.36, 0.35, 0.36,

In [ ]:
from pulp import GLPK
import pandas as pd # Library to handle data
import numpy as np
from statistics import mean

data = pd.read_csv("/content/Strikers DEA Model 2 and 3.csv", encoding = 'unicode_escape', engine ='python')
#creating a list to store the optimal decision variables
weights_matrix = np.empty((7,51))
for k in range(51):  # Where k represents the number of observations
    model = pulp.LpProblem("DEA Model 1 for Strikers (Creativity)", pulp.LpMaximize) # Create an LP maximization problem. We have 1 input, 6 outputs for goal scoring
    n1 = pulp.LpVariable("n1", lowBound=0.000001, upBound=None, cat='Continuous') # Create a variable n1>=0, where n1 represents the weight associated with output 1 - with goal scoring, it will be goals scored
    n2 = pulp.LpVariable("n2", lowBound=0.000001, upBound=None, cat='Continuous') # Create a variable n2>=0  , simmilar to above
    n3 = pulp.LpVariable("n3", lowBound=0.000001, upBound=None, cat='Continuous') # Create a variable n3>=0
    n4 = pulp.LpVariable("n4", lowBound=0.000001, upBound=None, cat='Continuous') # Create a variable n4>=0
    n5 = pulp.LpVariable("n5", lowBound=0.000001, upBound=None, cat='Continuous') # Create a variable n4>=0
    m1 = pulp.LpVariable("m1", lowBound=0.000001, upBound=None, cat='Continuous') # Create a variable m1>=0 , where m is denotes my inputs. In DEA model 1, there is just 1 input - playing time
    m2 = pulp.LpVariable("m2", lowBound=0.000001, upBound=None, cat='Continuous') # Create a variable m1>=0 , where m is denotes my inputs. In DEA model 1, there is just 1 input - playing time

    model += n1*data["xA"][k] + n2*data["KP"][k] + n3*data["PPA"][k]+ n4*data["SCA"][k] + n5*data["Progressive Passes"][k]  #objective function
    
    model += m1*data["Salary NORM"][k] + m2*data["Teammate Ability"][k]  == 1 #first constraint (equality)

    for i in range(51): #NUMBER OF STRIKERS
        model += n1*data["xA"][i] + n2*data["KP"][i] + n3*data["PPA"][i] + n4*data["SCA"][i] + n5*data["Progressive Passes"][i] - m1*data["Salary NORM"][i] - m2*data["Teammate Ability"][i] <= 0
   
    status = model.solve(GLPK(msg=True, options=['--ranges', 'sensitivity.txt'])) 
    
    #ADD IN RELATIVE WEIGHT RESTRICTIONS AND CONDITION FOR WEIGHTS TO BE POSITIVE.
    model += n1 >= n3 #xA > PPA
    model += n2 >= n3  #KP > PPA
    model += n4 >= n3   #SCA > PPA
    model += n1 >= n2   #SCA > PPA
        
    # Displaying Optimal Value of Objective Function	
    print(pulp.value(model.objective))


0.4005837700400759
1.000000307230351
1.0000001572801709
0.512606329726115
0.40354406285060496
0.8502338133805201
0.5624616941666419
0.8692870203918501
0.7172427900938779
0.618628199033608
1.000000134092688
0.6407929640808828
0.554266156362555
0.763084117822165
0.7228623097123701
0.6162775058971579
0.884339639353156
0.656457571526646
0.37360746878181794
0.451801793304091
0.5709540069994179
0.4524707127554922
0.9123079717669751
0.5869154487135211
0.666738598838616
0.77415450640411
0.6373703685269261
0.6200384645216851
0.8317156768130055
0.5735738968176289
0.456603160271505
1.0000005797479528
0.992304478941844
1.00000028161555
0.26745903241954
0.778711803047115
0.7924261112540981
0.542497989174099
0.6656769170446271
0.501079412415457
0.9107046855987802
0.604492006916358
1.00000186357713
0.863536722479478
0.523824652525062
1.0000007903893238
1.000000547110983
0.371642378572685
0.68562839639156
0.706115225473372
0.9569466503575801


DEA Model 3: Dribllig and ball carrying

In [ ]:
!pip install pulp
import pulp
!apt-get install -y -qq glpk-utils

from pulp import GLPK
import pandas as pd # Library to handle data
import numpy as np
from statistics import mean

data = pd.read_csv("/content/Strikers DEA Model 2 and 3.csv", encoding = 'unicode_escape', engine ='python')
#creating a list to store the optimal decision variables
weights_matrix = np.empty((8,51))
for k in range(51):  # Where k represents the number of observations
    model = pulp.LpProblem("DEA Model 1 for Strikers (Dribbling and Ball Carrying)", pulp.LpMaximize) # Create an LP maximization problem. We have 1 input, 6 outputs for goal scoring
    n1 = pulp.LpVariable("n1", lowBound=0.00000000001, upBound=None, cat='Continuous') # Create a variable n1>=0
    n2 = pulp.LpVariable("n2", lowBound=0.00000000001, upBound=None, cat='Continuous') # Create a variable n2>=0  , simmilar to above
    n3 = pulp.LpVariable("n3", lowBound=0.00000000001, upBound=None, cat='Continuous') # Create a variable n3>=0
    n4 = pulp.LpVariable("n4", lowBound=0.00000000001, upBound=None, cat='Continuous') # Create a variable n4>=0
    n5 = pulp.LpVariable("n5", lowBound=0.0000000001, upBound=None, cat='Continuous') # Create a variable n5>=0
    n6 = pulp.LpVariable("n6", lowBound=0.00000000001, upBound=None, cat='Continuous') # Create a variable n6>=0
    m1 = pulp.LpVariable("m1", lowBound=0.00000000001, upBound=None, cat='Continuous') # Create a variable m1>=0 , where m is denotes my inputs. In DEA model 1, there is just 1 input - playing time
    m2 = pulp.LpVariable("m2", lowBound=0.00000000001, upBound=None, cat='Continuous') # Create a variable m1>=0
    
    model += n1*data["Dribb Succ"][k] + n2*data["SCA Drib"][k] + n3*data["GCA Drib"][k]+ n4*data["Carry PrgDist"][k] + n5*data["Carries Final Third"][k] + n6*data["Carry into box"][k]    #objective function
    
    model += m1*data["Salary NORM"][k] + m2*data["Teammate Ability"][k] == 1 #first constraint (equality)

    for i in range(51): #NUMBER OF STRIKERS
        model += n1*data["Dribb Succ"][i] + n2*data["SCA Drib"][i] + n3*data["GCA Drib"][i] + n4*data["Carry PrgDist"][i] + n5*data["Carries Final Third"][i] + n6*data["Carry into box"][i] - m1*data["Salary NORM"][i] - m2*data["Teammate Ability"][i] <= 0
   
    status = model.solve(GLPK(msg=True, options=['--ranges', 'sensitivity.txt'])) 
    print("Model Status:{}".format(pulp.LpStatus[model.status])) 
    
    #ADD IN RELATIVE WEIGHT RESTRICTIONS AND CONDITION FOR WEIGHTS TO BE POSITIVE.
    model += n3 >= n4   #Goals > SoT(%)
    model += n3 >= n5   #Goals > G-Xg
    model += n3 >= n6   #Goals > Big Chances Missed
    model += n2 >= n4   #Goals > SoT(%)
    model += n2 >= n5   #Goals > Shots on Target
    model += n2 >= n6   #Goals > SoT(%)

    # Displaying Optimal Decision Variables & Reduced Cost per Variable
    list_weights=[]
    for v in model.variables():
	      print(v.name, "=", v.varValue, "\tReduced Cost =", v.dj)
    for v in model.variables():  
        list_weights=list_weights+[v.varValue]
    for n in range(6):
        value= list_weights[n]
        weights_matrix[n,k] = value
        

    # Displaying Optimal Value of Objective Function	
    print("Objective=", pulp.value(model.objective))
	
    # Displaying Shadow Price & Slack Value per Constraint
    print ("\nSensitivity Analysis\nConstraint\t\tShadow Price\tSlack")
    for name, c in model.constraints.items():
	      print(name, ":", c, "\t", c.pi, "\t\t", c.slack)
	

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Model Status:Optimal
m1 = 0.991946 	Reduced Cost = None
m2 = 0.0 	Reduced Cost = None
n1 = 0.0 	Reduced Cost = None
n2 = 0.210489 	Reduced Cost = None
n3 = 0.8363 	Reduced Cost = None
n4 = 0.0 	Reduced Cost = None
n5 = 0.0 	Reduced Cost = None
n6 = 0.0867926 	Reduced Cost = None
Objective= 0.54301154302

Sensitivity Analysis
Constraint		Shadow Price	Slack
_C1 : 1.00811908*m1 + 41*m2 = 1.0 	 None 		 None
_C2 : -1.00811908*m1 - 41*m2 + 1.15189873*n1 + 0.6681*n2 + 0.4255*n3 + 0.5191*n4 + 0.566*n5 + 0.5362*n6 <= -0.0 	 None 		 None
_C3 : -1.23191475*m1 - 45*m2 + 5.0*n1 + 2.1277*n2 + 0.7106*n3 + 2.1277*n4 + 2.1277*n5 + 2.0723*n6 <= -0.0 	 None 		 None
_C4 : -1.346414073*m1 - 28*m2 + 1.30379747*n1 + 0.8298*n2 + 0.7106*n3 + 0.5447*n4 + 0.5064*n5 + 0.5064*n6 <= -0.0 	 None 		 None
_C5 : -2.172631935*m1 - 61*m2 + 1.4556962*n1 + 0.6681*n2 + 0.4255*n3 + 0.6043*n4 + 0.6043*n5 + 0.5915*n6 <= -0.0 	 No

In [ ]:
efficiency_table =np.empty((51,8))
average_list =[]
for row in range(51):
    row_values=[]
    for column in range(8):
       value = ((weights_matrix[2,column]*data["Dribb Succ"][row])+(weights_matrix[3,column]*data["SCA Drib"][row])+(weights_matrix[4,column]*data["GCA Drib"][row])+(weights_matrix[5,column]*data["Carry PrgDist"][row])+(weights_matrix[6,column]*data["Carries Final Third"][row])+ (weights_matrix[7,column]*data["Carry into box"][row]))/((weights_matrix[0,column]*data["Salary NORM"][row])+(weights_matrix[1,column]*data["Salary NORM"][row]))
       efficiency_table[row,column]=value
       row_values=row_values+[value]
    average =mean(row_values)
    average_list =average_list+[average]

    average_list_rounded = [ '%.2f' % elem for elem in average_list ]

    player_list = ['Aaron Connolly', 'Adama TraorÃ©', 'Aleksandar MitroviÄ‡', 'Alexandre Lacazette', 'Anthony Martial', 'Anwar El Ghazi', 'Ashley Barnes', 'Bertrand TraorÃ©', 'Billy Sharp', 'Callum Wilson', 'Che Adams', 'Chris Wood', 'Christian Benteke', 'Daniel James', 'Danny Ings', 'Danny Welbeck', 'Diogo Jota', 'Dominic Calvert-Lewin', 'Edinson Cavani', 'FÃ¡bio Silva', 'Gabriel Jesus', 'Gareth Bale', 'Harry Kane', 'Jamie Vardy', 'Kelechi Iheanacho', 'Marcus Rashford', 'Mason Greenwood', 'MatÄ›j Vydra', 'Mbaye Diagne', 'Michail Antonio', 'Michy Batshuayi', 'Mohamed Salah', 'Oliver Burke', 'Oliver McBurnie', 'Olivier Giroud', 'Ollie Watkins', 'Patrick Bamford', 'Pierre-Emerick Aubameyang', 'RaÃºl JimÃ©nez', 'Raheem Sterling', 'Rhian Brewster', 'Richarlison', 'Riyad Mahrez', 'Roberto Firmino', 'SÃ©bastien Haller', 'Sadio ManÃ©', 'Son Heung-min', 'Tammy Abraham', 'Timo Werner', 'TrÃ©zÃ©guet', 'Wilfried Zaha']
for player in player_list:
    index = player_list.index(player)
    print(average_list_rounded[index])

display(efficiency_table)
efficiency_table = efficiency_table.round(decimals=2)
display(efficiency_table)

6.59
15.42
7.05
3.41
3.16
6.90
5.14
7.24
6.41
5.95
6.75
9.24
5.48
5.37
10.95
5.50
6.60
6.88
2.75
4.78
7.42
1.61
10.38
8.20
7.77
7.30
9.30
10.64
6.35
6.50
4.46
4.08
7.31
6.21
3.74
8.06
10.27
3.55
7.61
6.04
5.93
9.69
7.59
4.36
4.57
7.16
7.13
4.88
7.35
6.02
8.17


array([[ 0.49647351, 10.28360552, 16.39096743, 16.39102907,  7.97811493,
         0.37212656,  0.39130166,  0.38370699],
       [ 0.85281364, 36.5285382 , 36.52846868, 36.52861704, 10.90327853,
         0.50856619,  0.53477182,  0.99999957],
       [ 0.57573809,  8.71514135, 17.89089594, 17.8909612 ,  9.97606154,
         0.46531762,  0.48929471,  0.35683288],
       [ 0.23036779,  6.03014192,  8.39663284,  8.39666503,  3.70191092,
         0.17266978,  0.18156719,  0.1780432 ],
       [ 0.19016594,  6.1898015 ,  7.69319742,  7.69322745,  3.05588464,
         0.14253691,  0.14988161,  0.1469726 ],
       [ 0.45015164, 12.97805916, 16.86046584, 16.86053118,  6.99414649,
         0.32623091,  0.34304108,  0.37706525],
       [ 0.37075933,  7.43129235, 12.93429524, 12.93434333,  6.6410007 ,
         0.30975898,  0.32572038,  0.20341878],
       [ 0.55191644, 15.36249742, 17.28108499, 17.28115363,  6.12752126,
         0.28580854,  0.30053581,  0.76020175],
       [ 0.4395094 ,  9.92437912

array([[ 0.5 , 10.28, 16.39, 16.39,  7.98,  0.37,  0.39,  0.38],
       [ 0.85, 36.53, 36.53, 36.53, 10.9 ,  0.51,  0.53,  1.  ],
       [ 0.58,  8.72, 17.89, 17.89,  9.98,  0.47,  0.49,  0.36],
       [ 0.23,  6.03,  8.4 ,  8.4 ,  3.7 ,  0.17,  0.18,  0.18],
       [ 0.19,  6.19,  7.69,  7.69,  3.06,  0.14,  0.15,  0.15],
       [ 0.45, 12.98, 16.86, 16.86,  6.99,  0.33,  0.34,  0.38],
       [ 0.37,  7.43, 12.93, 12.93,  6.64,  0.31,  0.33,  0.2 ],
       [ 0.55, 15.36, 17.28, 17.28,  6.13,  0.29,  0.3 ,  0.76],
       [ 0.44,  9.92, 16.03, 16.03,  7.87,  0.37,  0.39,  0.24],
       [ 0.4 , 11.25, 14.51, 14.51,  5.97,  0.28,  0.29,  0.36],
       [ 0.41, 12.45, 16.58, 16.58,  7.03,  0.33,  0.34,  0.26],
       [ 0.78,  9.  , 23.89, 23.89, 14.66,  0.68,  0.72,  0.34],
       [ 0.42,  6.96, 13.91, 13.91,  7.67,  0.36,  0.38,  0.22],
       [ 0.36,  8.51, 13.39, 13.39,  6.46,  0.3 ,  0.32,  0.2 ],
       [ 0.91, 11.72, 28.11, 28.11, 16.67,  0.78,  0.82,  0.46],
       [ 0.38,  9.46, 13.

In [ ]:
!pip install pulp
import pulp
!apt-get install -y -qq glpk-utils

from pulp import GLPK
import pandas as pd # Library to handle data
import numpy as np
from statistics import mean

data = pd.read_csv("/content/Strikers DEA Model 2 and 3.csv", encoding = 'unicode_escape', engine ='python')
#creating a list to store the optimal decision variables
weights_matrix = np.empty((8,51))
for k in range(51):  # Where k represents the number of observations
    model = pulp.LpProblem("DEA Model 1 for Strikers (Dribbling and Ball Carrying)", pulp.LpMaximize) # Create an LP maximization problem. We have 1 input, 6 outputs for goal scoring
    m1 = pulp.LpVariable("m1", lowBound=0.00000000001, upBound=None, cat='Continuous') # Create a variable m1>=0 , where m is denotes my inputs. In DEA model 1, there is just 1 input - playing time
    m2 = pulp.LpVariable("m2", lowBound=0.00000000001, upBound=None, cat='Continuous') # Create a variable m1>=0
    n1 = pulp.LpVariable("n1", lowBound=0.00000000001, upBound=None, cat='Continuous') # Create a variable n1>=0
    n2 = pulp.LpVariable("n2", lowBound=0.00000000001, upBound=None, cat='Continuous') # Create a variable n2>=0  , simmilar to above
    n3 = pulp.LpVariable("n3", lowBound=0.00000000001, upBound=None, cat='Continuous') # Create a variable n3>=0
    n4 = pulp.LpVariable("n4", lowBound=0.00000000001, upBound=None, cat='Continuous') # Create a variable n4>=0
    n5 = pulp.LpVariable("n5", lowBound=0.0000000001, upBound=None, cat='Continuous') # Create a variable n5>=0
    n6 = pulp.LpVariable("n6", lowBound=0.00000000001, upBound=None, cat='Continuous') # Create a variable n6>=0
   
    model += n1*data["Dribb Succ"][k] + n2*data["SCA Drib"][k] + n3*data["GCA Drib"][k]+ n4*data["Carry PrgDist"][k] + n5*data["Carries Final Third"][k] + n6*data["Carry into box"][k]    #objective function
    
    model += m1*data["Salary NORM"][k] + m2*data["Teammate Ability"][k] == 1 #first constraint (equality)

    for i in range(51): #NUMBER OF STRIKERS
        model += n1*data["Dribb Succ"][i] + n2*data["SCA Drib"][i] + n3*data["GCA Drib"][i] + n4*data["Carry PrgDist"][i] + n5*data["Carries Final Third"][i] + n6*data["Carry into box"][i] - m1*data["Salary NORM"][i] - m2*data["Teammate Ability"][i] <= 0
   
    status = model.solve(GLPK(msg=True, options=['--ranges', 'sensitivity.txt'])) 
    
    #ADD IN RELATIVE WEIGHT RESTRICTIONS AND CONDITION FOR WEIGHTS TO BE POSITIVE.
    model += n3 >= n4   #Goals > SoT(%)
    model += n3 >= n5   #Goals > G-Xg
    model += n3 >= n6   #Goals > Big Chances Missed
    model += n2 >= n4   #Goals > SoT(%)
    model += n2 >= n5   #Goals > Shots on Target
    model += n2 >= n6   #Goals > SoT(%)

    # Displaying Optimal Value of Objective Function	
    print(pulp.value(model.objective))


Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
0.54301154302
1.0
0.8603058466008501
0.29906254375254004
0.3023667285
0.5852437144
0.44874304124
0.7602020804
0.726076829468368
0.5436551801
0.5631687693999999
0.860728822647874
0.5694192651408
0.4820485474
0.9967424759360349
0.4445191925
0.5989525168400001
0.6100248953
0.225428414536598
0.390953409401088
0.6221360624
0.3818396779
0.9999998507
0.826145565
0.656864923
0.6884231778000001
0.8974855782000001
0.9999993842999999
0.66308476531398
0.506892304
0.418859444
0.5999631440000001
0.9774835510000001
0.7328189149
0.311070426720212
0.7822445433
1.0000001469
0.5130050442
0.6798216332
0.6595260322
0.7246621624362
0.8885147150000001
0.7984344053000001
0.4291224
0.37143181090216904
0.7008403
0.6827342065
0.4076787476401458
0.8346077196
0.47665469964
1.000000822


Defending DEA Model 3

In [ ]:
!pip install pulp
import pulp
!apt-get install -y -qq glpk-utils

from pulp import GLPK
import pandas as pd # Library to handle data
import numpy as np
from statistics import mean

data = pd.read_csv("/content/Strikers DEA Model 2 and 3.csv", encoding = 'unicode_escape', engine ='python')
#creating a list to store the optimal decision variables
weights_matrix = np.empty((6,51))
for k in range(51):  # Where k represents the number of observations
    model = pulp.LpProblem("DEA Model 1 for Strikers (Defending)", pulp.LpMaximize) # Create an LP maximization problem. We have 1 input, 6 outputs for goal scoring
    n1 = pulp.LpVariable("n1", lowBound=0.0000001, upBound=None, cat='Continuous') # Create a variable n1>=0, where n1 represents the weight associated with output 1 - with goal scoring, it will be goals scored
    n2 = pulp.LpVariable("n2", lowBound=0.0000001, upBound=None, cat='Continuous') # Create a variable n2>=0  , simmilar to above
    n3 = pulp.LpVariable("n3", lowBound=0.0000001, upBound=None, cat='Continuous') # Create a variable n3>=0
    n4 = pulp.LpVariable("n4", lowBound=0.0000001, upBound=None, cat='Continuous') # Create a variable n4>=0
    m1 = pulp.LpVariable("m1", lowBound=0.0000001, upBound=None, cat='Continuous') # Create a variable m1>=0 , where m is denotes my inputs. In DEA model 1, there is just 1 input - playing time
    m2 = pulp.LpVariable("m2", lowBound=0.0000001, upBound=None, cat='Continuous') # Create a variable m1>=0 , where m is denotes my inputs. In DEA model 1, there is just 1 input - playing time

    model += n1*data["Tackles TklW"][k] + n2*data["Pressures Succ"][k] + n3*data["Blocks and Interceptions"][k]+ n4*data["Recoveries"][k] #objective function
    
    model += m1*data["Salary NORM"][k] + m2*data["Teammate Ability"][k]  == 1 #first constraint (equality)

    for i in range(51): #NUMBER OF STRIKERS
        model += n1*data["Tackles TklW"][i] + n2*data["Pressures Succ"][i] + n3*data["Blocks and Interceptions"][i] + n4*data["Recoveries"][i] - m1*data["Salary NORM"][i] - m2*data["Teammate Ability"][i] <= 0
   
    
    status = model.solve(GLPK(msg=True, options=['--ranges', 'sensitivity.txt'])) 
    print("Model Status:{}".format(pulp.LpStatus[model.status])) 

    #ADD IN RELATIVE WEIGHT RESTRICTIONS AND CONDITION FOR WEIGHTS TO BE POSITIVE.
    model += n3 >= n2   #Goals > SoT
    
    # Displaying Optimal Decision Variables & Reduced Cost per Variable
    list_weights=[]
    for v in model.variables():
	      print(v.name, "=", v.varValue, "\tReduced Cost =", v.dj)
    for v in model.variables():  
        list_weights=list_weights+[v.varValue]
    for n in range(4):
        value= list_weights[n]
        weights_matrix[n,k] = value
    for m in range(2):
        value= list_weights[m]
        weights_matrix[m,k] = value
        

    # Displaying Optimal Value of Objective Function	
    print("Objective=", pulp.value(model.objective))
	
    # Displaying Shadow Price & Slack Value per Constraint
    print ("\nSensitivity Analysis\nConstraint\t\tShadow Price\tSlack")
    for name, c in model.constraints.items():
	      print(name, ":", c, "\t", c.pi, "\t\t", c.slack)

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


/usr/local/lib/python3.7/dist-packages/pulp/pulp.py:1352: UserWarning: Spaces are not permitted in the name. Converted to '_'
  warnings.warn("Spaces are not permitted in the name. Converted to '_'")


Model Status:Optimal
m1 = 0.739988 	Reduced Cost = None
m2 = 0.00619521 	Reduced Cost = None
n1 = 0.498293 	Reduced Cost = None
n2 = 0.267076 	Reduced Cost = None
n3 = 1e-07 	Reduced Cost = None
n4 = 1e-07 	Reduced Cost = None
Objective= 0.50981008179

Sensitivity Analysis
Constraint		Shadow Price	Slack
_C1 : 1.00811908*m1 + 41*m2 = 1.0 	 None 		 None
_C2 : -1.00811908*m1 - 41*m2 + 0.6468*n1 + 0.7021*n2 + 0.5319*n3 + 0.566*n4 <= -0.0 	 None 		 None
_C3 : -1.23191475*m1 - 45*m2 + 1.634*n1 + 1.4085*n2 + 1.3447*n3 + 1.7574*n4 <= -0.0 	 None 		 None
_C4 : -1.346414073*m1 - 28*m2 + 0.8638*n1 + 1.0298*n2 + 0.8596*n3 + 0.8085*n4 <= -0.0 	 None 		 None
_C5 : -2.172631935*m1 - 61*m2 + 1.4128*n1 + 1.4085*n2 + 1.1277*n3 + 1.1957*n4 <= -0.0 	 None 		 None
_C6 : -2.631935047*m1 - 74*m2 + 0.4255*n1 + 0.7234*n2 + 0.9915*n3 + 0.8681*n4 <= -0.0 	 None 		 None
_C7 : -1.149945873*m1 - 55*m2 + 0.9191*n1 + 0.8255*n2 + 0.8596*n3 + 1.0383*n4 <= -0.0 	 None 		 None
_C8 : -1.211096076*m1 - 39*m2 + 0.7021*n1 + 

In [ ]:
efficiency_table =np.empty((51,6))
average_list =[]
for row in range(51):
    row_values=[]
    for column in range(6):
       value = ((weights_matrix[0,column]*data["Tackles TklW"][row])+(weights_matrix[1,column]*data["Pressures Succ"][row])+(weights_matrix[2,column]*data["Blocks and Interceptions"][row])+(weights_matrix[3,column]*data["Recoveries"][row]))/((weights_matrix[0,column]*data["Salary NORM"][row])+(weights_matrix[1,column]*data["Teammate Ability"][row]))
       efficiency_table[row,column]=value
       row_values=row_values+[value]
    average =mean(row_values)
    average_list =average_list+[average]

    average_list_rounded = [ '%.2f' % elem for elem in average_list ]

    player_list = ['Aaron Connolly', 'Adama TraorÃ©', 'Aleksandar MitroviÄ‡', 'Alexandre Lacazette', 'Anthony Martial', 'Anwar El Ghazi', 'Ashley Barnes', 'Bertrand TraorÃ©', 'Billy Sharp', 'Callum Wilson', 'Che Adams', 'Chris Wood', 'Christian Benteke', 'Daniel James', 'Danny Ings', 'Danny Welbeck', 'Diogo Jota', 'Dominic Calvert-Lewin', 'Edinson Cavani', 'FÃ¡bio Silva', 'Gabriel Jesus', 'Gareth Bale', 'Harry Kane', 'Jamie Vardy', 'Kelechi Iheanacho', 'Marcus Rashford', 'Mason Greenwood', 'MatÄ›j Vydra', 'Mbaye Diagne', 'Michail Antonio', 'Michy Batshuayi', 'Mohamed Salah', 'Oliver Burke', 'Oliver McBurnie', 'Olivier Giroud', 'Ollie Watkins', 'Patrick Bamford', 'Pierre-Emerick Aubameyang', 'RaÃºl JimÃ©nez', 'Raheem Sterling', 'Rhian Brewster', 'Richarlison', 'Riyad Mahrez', 'Roberto Firmino', 'SÃ©bastien Haller', 'Sadio ManÃ©', 'Son Heung-min', 'Tammy Abraham', 'Timo Werner', 'TrÃ©zÃ©guet', 'Wilfried Zaha']
for player in player_list:
    index = player_list.index(player)
    print(average_list_rounded[index])

display(efficiency_table)
efficiency_table = efficiency_table.round(decimals=2)
display(efficiency_table)

0.48
1.07
0.72
0.57
0.27
0.60
0.60
0.77
0.57
0.61
0.98
0.80
0.52
0.49
0.92
0.65
0.45
0.77
0.34
0.48
0.55
0.26
0.57
0.42
0.50
0.45
0.47
0.59
0.57
0.54
0.36
0.47
0.97
0.90
0.27
0.81
0.78
0.38
0.45
0.41
0.86
1.03
0.50
0.80
0.31
0.96
0.76
0.34
0.56
0.81
0.94


array([[0.89918129, 0.47827229, 0.15198316, 0.47827108, 0.1816299 ,
        0.70595367],
       [1.98026451, 1.07556036, 0.41280889, 1.07555769, 0.40013405,
        1.45954741],
       [1.10262381, 0.94621118, 0.31885615, 0.94620923, 0.28568802,
        0.71943977],
       [0.97472812, 0.63992249, 0.21457703, 0.639921  , 0.23712734,
        0.71358971],
       [0.43442758, 0.39290449, 0.12437566, 0.39290362, 0.06156374,
        0.20762494],
       [1.16715196, 0.57019844, 0.19942854, 0.57019695, 0.19789521,
        0.89044236],
       [1.05525459, 0.69981947, 0.26739354, 0.69981783, 0.19496164,
        0.66330638],
       [1.44426394, 0.9422233 , 0.3155479 , 0.94222096, 0.18388012,
        0.80798369],
       [0.93622822, 0.63995149, 0.26088958, 0.63995011, 0.26535272,
        0.68389969],
       [1.10345139, 0.66564972, 0.26382358, 0.66564814, 0.22604009,
        0.76051067],
       [1.78323336, 1.05346442, 0.35264143, 1.05346184, 0.34672718,
        1.27632118],
       [1.36994962, 0

array([[0.9 , 0.48, 0.15, 0.48, 0.18, 0.71],
       [1.98, 1.08, 0.41, 1.08, 0.4 , 1.46],
       [1.1 , 0.95, 0.32, 0.95, 0.29, 0.72],
       [0.97, 0.64, 0.21, 0.64, 0.24, 0.71],
       [0.43, 0.39, 0.12, 0.39, 0.06, 0.21],
       [1.17, 0.57, 0.2 , 0.57, 0.2 , 0.89],
       [1.06, 0.7 , 0.27, 0.7 , 0.19, 0.66],
       [1.44, 0.94, 0.32, 0.94, 0.18, 0.81],
       [0.94, 0.64, 0.26, 0.64, 0.27, 0.68],
       [1.1 , 0.67, 0.26, 0.67, 0.23, 0.76],
       [1.78, 1.05, 0.35, 1.05, 0.35, 1.28],
       [1.37, 0.96, 0.34, 0.96, 0.27, 0.87],
       [0.87, 0.64, 0.25, 0.64, 0.19, 0.55],
       [0.97, 0.46, 0.12, 0.46, 0.14, 0.79],
       [1.51, 1.25, 0.32, 1.25, 0.27, 0.9 ],
       [1.11, 0.82, 0.23, 0.82, 0.21, 0.71],
       [0.87, 0.44, 0.16, 0.44, 0.16, 0.66],
       [1.51, 0.76, 0.24, 0.76, 0.22, 1.1 ],
       [0.61, 0.35, 0.14, 0.35, 0.14, 0.45],
       [0.83, 0.56, 0.22, 0.56, 0.17, 0.54],
       [1.07, 0.55, 0.16, 0.55, 0.16, 0.8 ],
       [0.34, 0.39, 0.16, 0.39, 0.1 , 0.2 ],
       [0.

In [ ]:
!pip install pulp
import pulp
!apt-get install -y -qq glpk-utils

from pulp import GLPK
import pandas as pd # Library to handle data
import numpy as np
from statistics import mean

data = pd.read_csv("/content/Strikers DEA Model 2 and 3.csv", encoding = 'unicode_escape', engine ='python')
#creating a list to store the optimal decision variables
weights_matrix = np.empty((6,51))
for k in range(51):  # Where k represents the number of observations
    model = pulp.LpProblem("DEA Model 1 for Strikers (Defending)", pulp.LpMaximize) # Create an LP maximization problem. We have 1 input, 6 outputs for goal scoring
    m1 = pulp.LpVariable("m1", lowBound=0.0000000001, upBound=None, cat='Continuous') # Create a variable m1>=0 , where m is denotes my inputs. In DEA model 1, there is just 1 input - playing time
    m2 = pulp.LpVariable("m2", lowBound=0.0000000001, upBound=None, cat='Continuous') # Create a variable m1>=0 , where m is denotes my inputs. In DEA model 1, there is just 1 input - playing time
    n1 = pulp.LpVariable("n1", lowBound=0.0000000001, upBound=None, cat='Continuous') # Create a variable n1>=0, where n1 represents the weight associated with output 1 - with goal scoring, it will be goals scored
    n2 = pulp.LpVariable("n2", lowBound=0.0000000001, upBound=None, cat='Continuous') # Create a variable n2>=0  , simmilar to above
    n3 = pulp.LpVariable("n3", lowBound=0.0000000001, upBound=None, cat='Continuous') # Create a variable n3>=0
    n4 = pulp.LpVariable("n4", lowBound=0.0000000001, upBound=None, cat='Continuous') # Create a variable n4>=0
   
    model += n1*data["Tackles TklW"][k] + n2*data["Pressures Succ"][k] + n3*data["Blocks and Interceptions"][k]+ n4*data["Recoveries"][k] #objective function
    
    model += m1*data["Salary NORM"][k] + m2*data["Teammate Ability"][k]  == 1 #first constraint (equality)

    for i in range(51): #NUMBER OF STRIKERS
        model += n1*data["Tackles TklW"][i] + n2*data["Pressures Succ"][i] + n3*data["Blocks and Interceptions"][i] + n4*data["Recoveries"][i] - m1*data["Salary NORM"][i] - m2*data["Teammate Ability"][i] <= 0
   
    
    status = model.solve(GLPK(msg=True, options=['--ranges', 'sensitivity.txt'])) 

    #ADD IN RELATIVE WEIGHT RESTRICTIONS AND CONDITION FOR WEIGHTS TO BE POSITIVE.
    model += n3 >= n2   #Goals > SoT
  

    # Displaying Optimal Value of Objective Function	
    print(pulp.value(model.objective))
	


Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
0.509809972
0.9999998299999998
0.8083205455
0.6066337152
0.34552089620000004
0.6662502593
0.653953255
0.9999992254000001
0.703731336
0.7011725266
1.0000008502
0.8669524395999999
0.595338554099
0.6535372530000001
1.0000000331999999
0.68847533788
0.49939111010000004
1.0000007747600002
0.3526881165
0.5723378176
0.72612980137
0.398625409
0.700882219744
0.45703893551999997
0.5878609939199999
0.5462760360050001
0.5820336567000001
0.6814985886
0.7358182911200001
0.71081149815
0.383001613
0.7656933864000001
1.0000000395
1.0000031999999999
0.2931280851
0.9417355958999999
0.9999996993000001
0.4696284756
0.47399388928999997
0.4273492214
0.9903523925
0.9999992069600001
0.5693534902999999
0.8948716830899999
0.3505074373
1.0000009885
0.8482311493000001
0.40714571089999996
0.6236052579
0.8959564482
0.9862498761


K-Means Clustering for DEA Model 1

In [ ]:
from sklearn.cluster import KMeans
import pandas as pd
from sklearn.preprocessing import MinMaxScaler
from matplotlib import pyplot as plt
%matplotlib inline

df = pd.read_csv('/content/DEA Model 1 Clustering.csv',encoding= 'unicode_escape' )

km = KMeans(n_clusters=7)
y_predicted = km.fit_predict(df[['GOAL-SCORING DEA EFFICIENCY SCORE (RWRs, NO POSITIVE WEIGHTS)',	'Creativity. Effiiency','Dribbling and Ball Carrying Efficiency',	'Defending Efficiency']])
y_predicted


array([1, 1, 5, 6, 0, 5, 6, 5, 2, 0, 6, 6, 6, 4, 1, 6, 4, 6, 3, 6, 5, 4,
       2, 0, 5, 2, 1, 2, 0, 0, 4, 5, 1, 3, 5, 6, 6, 6, 2, 2, 6, 1, 4, 3,
       5, 5, 3, 6, 2, 5, 1, 6], dtype=int32)

In [ ]:
df

ï»¿Player  \
0              Aaron Connolly   
1                Adama Traore   
2         Aleksandar Mitrovic   
3         Alexandre Lacazette   
4             Anthony Martial   
5              Anwar El Ghazi   
6               Ashley Barnes   
7          Bertrand TraorÃÂ©   
8                 Billy Sharp   
9               Callum Wilson   
10                  Che Adams   
11                 Chris Wood   
12          Christian Benteke   
13               Daniel James   
14                 Danny Ings   
15              Danny Welbeck   
16                 Diogo Jota   
17      Dominic Calvert-Lewin   
18             Edinson Cavani   
19             FÃÂ¡bio Silva   
20              Gabriel Jesus   
21                Gareth Bale   
22                 Harry Kane   
23                Jamie Vardy   
24          Kelechi Iheanacho   
25            Marcus Rashford   
26            Mason Greenwood   
27                Matej Vydra   
28               Mbaye Diagne   
29            Michail Antonio   
30            Michy Batshuayi   
31              Mohamed Salah   
32               Oliver Burke   
33            Oliver McBurnie   
34             Olivier Giroud   
35              Ollie Watkins   
36            Patrick Bamford   
37  Pierre-Emerick Aubameyang   
38         RaÃÂºl JimÃÂ©nez   
39            Raheem Sterling   
40             Rhian Brewster   
41                Richarlison   
42               Riyad Mahrez   
43            Roberto Firmino   
44        SÃÂ©bastien Haller   
45                 Sadio Mane   
46              Son Heung-min   
47              Tammy Abraham   
48                Timo Werner   
49                  Trezeguet   
50              Wilfried Zaha   
51            Willian JosÃÂ©   

    GOAL-SCORING DEA EFFICIENCY SCORE (RWRs, NO POSITIVE WEIGHTS)  \
0                                            0.716697               
1                                            0.449060               
2                                            0.714229               
3                                            0.613051               
4                                            0.863946               
5                                            0.599187               
6                                            0.547396               
7                                            0.630183               
8                                            0.813354               
9                                            0.782088               
10                                           0.519860               
11                                           0.507569               
12                                           0.582634               
13                                           0.827049               
14                                           0.711023               
15                                           0.660827               
16                                           0.766611               
17                                           0.521047               
18                                           0.684787               
19                                           0.665070               
20                                           0.789268               
21                                           1.000002               
22                                           0.999998               
23                                           0.938456               
24                                           0.734123               
25                                           0.814468               
26                                           0.573057               
27                                           0.790963               
28                                           0.963975               
29                                           0.819396               
30                                           0.867247               
31                                           0.648736         

In [ ]:
df.drop("ï»¿Player",axis='columns')

GOAL-SCORING DEA EFFICIENCY SCORE (RWRs, NO POSITIVE WEIGHTS)  \
0                                            0.716697               
1                                            0.449060               
2                                            0.714229               
3                                            0.613051               
4                                            0.863946               
5                                            0.599187               
6                                            0.547396               
7                                            0.630183               
8                                            0.813354               
9                                            0.782088               
10                                           0.519860               
11                                           0.507569               
12                                           0.582634               
13                                           0.827049               
14                                           0.711023               
15                                           0.660827               
16                                           0.766611               
17                                           0.521047               
18                                           0.684787               
19                                           0.665070               
20                                           0.789268               
21                                           1.000002               
22                                           0.999998               
23                                           0.938456               
24                                           0.734123               
25                                           0.814468               
26                                           0.573057               
27                                           0.790963               
28                                           0.963975               
29                                           0.819396               
30                                           0.867247               
31                                           0.648736               
32                                           0.501018               
33                                           0.616073               
34                                           0.693443               
35                                           0.604144               
36                                           0.750613               
37                                           0.544678               
38                                           0.987069               
39                                           0.810456               
40                                           0.473686               
41                                           0.521761               
42                                           0.974282               
43                                           0.525421               
44                                           0.614401               
45                                           0.634531               
46                                           0.673125               
47                                           0.665929               
48                                           0.941321               
49                                           0.609551               
50                                           0.678901               
51                                           0.555212               

    DEA Cross Effieicny (Goal-Scoring)  Creativity. Effiiency  \
0                                0.173               0.623413   
1                                0.065               0.845311   
2                                0.125               0.804695   
3                                0.205               0.651907   
4                    

In [ ]:
!pip install pulp
import pulp
!apt-get install -y -qq glpk-utils

from pulp import GLPK
import pandas as pd # Library to handle data
import numpy as np
from statistics import mean

data = pd.read_csv("/content/DEA Model 1_Strikers.csv", encoding = 'unicode_escape', engine ='python')
#creating a list to store the optimal decision variables
weights_matrix = np.empty((7,52))
for k in range(52):  # Where k represents the number of observations
    model = pulp.LpProblem("DEA Model 1 for Strikers (Goal-Scoring)", pulp.LpMaximize) # Create an LP maximization problem. We have 1 input, 6 outputs for goal scoring
    n1 = pulp.LpVariable("n1", lowBound=0.0000001, upBound=None, cat='Continuous') # Create a variable n1>=0, where n1 represents the weight associated with output 1 - with goal scoring, it will be goals scored
    n2 = pulp.LpVariable("n2", lowBound=0.0000001, upBound=None, cat='Continuous') # Create a variable n2>=0  , simmilar to above
    n3 = pulp.LpVariable("n3", lowBound=0.0000001, upBound=None, cat='Continuous') # Create a variable n3>=0
    n4 = pulp.LpVariable("n4", lowBound=0.0000001, upBound=None, cat='Continuous') # Create a variable n4>=0
    n5 = pulp.LpVariable("n5", lowBound=0.0000001, upBound=None, cat='Continuous') # Create a variable n5>=0
    m1 = pulp.LpVariable("m1", lowBound=0.0000001, upBound=None, cat='Continuous') # Create a variable m1>=0 , where m is denotes my inputs. In DEA model 1, there is just 1 input - playing time
    m2 = pulp.LpVariable("m2", lowBound=0.0000001, upBound=None, cat='Continuous') # Create a variable m1>=0 , where m is denotes my inputs. In DEA model 1, there is just 1 i
   
    model += n1*data["Gls"][k] + n2*data["SoT"][k] + n3*data["G-xG"][k]+ n4*data["Big Chances Missed"][k] + n5*data["GCA"][k]  #objective function
    
    model += m1*data["Minutes Played"][k] + m2*data["Team Points"][k]  == 1 #first constraint (equality)

    for i in range(52): #NUMBER OF STRIKERS
        model += n1*data["Gls"][i] + n2*data["SoT"][i] + n3*data["G-xG"][i] + n4*data["Big Chances Missed"][i] + n5*data["GCA"][i] -  m1*data["Minutes Played"][i] - m2*data["Team Points"][i]  <= 0
   

    #ADD IN RELATIVE WEIGHT RESTRICTIONS AND CONDITION FOR WEIGHTS TO BE POSITIVE.
    model += n1 >= n2  #Goals > SoT
    model += n1 >= n3   #Goals > G-Xg
    model += n1 >= n4  #Goals > Big Chances Missed
    model += n4 >= n2  #Goals > Shots on Target
    model += n5 >= n2  #Goals > Shots on Target
    model += n5 >= n4  #Goals > Big Chances Missed
    status = model.solve(GLPK(msg=True, options=['--ranges', 'sensitivity.txt'])) 
    
    
    # Displaying Optimal Value of Objective Function	
    print(pulp.value(model.objective))
	

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 14.2 MB 4.3 MB/s 
Selecting previously unselected package libsuitesparseconfig5:amd64.
(Reading database ... 155685 files and directories currently installed.)
Preparing to unpack .../libsuitesparseconfig5_1%3a5.1.2-2_amd64.deb ...
Unpacking libsuitesparseconfig5:amd64 (1:5.1.2-2) ...
Selecting previously unselected package libamd2:amd64.
Preparing to unpack .../libamd2_1%3a5.1.2-2_amd64.deb ...
Unpacking libamd2:amd64 (1:5.1.2-2) ...
Selecting previously unselected package libcolamd2:amd64.
Preparing to unpack .../libcolamd2_1%3a5.1.2-2_amd64.deb ...
Unpacking libcolamd2:amd64 (1:5.1.2-2) ...
Selecting previously unselected package libglpk40:amd64.
Preparing to unpack .../libglpk40_4.65-1_amd64.deb ...
Unpacking libglpk40:amd64 (4.65-1) ...
Selecting previously unselected package glpk-utils.
Preparing to unpack .../glpk-utils_4.65-1_amd64.deb ...
U

FileNotFoundError: ignored